# Test district from here

In [ ]:
import argparse
import os
from datetime import date
import threading
from concurrent.futures import ThreadPoolExecutor, as_completed

import pandas as pd
import numpy as np

from src.selenium_manager import create_stealth_driver
from src.scraping import Scraper
from src.cleaning import DataCleaner, drop_mixed_listings, is_land_only
from src.feature_engineering import FeatureEngineer
from src.address_standardizer import AddressStandardizer
from src import config
from src.utils import save_urls_to_csv, save_details_to_csv, chunks
from src.tasks import scrape_worker
from src.modelling import predict_alley_width

def run_cleaning_pipeline():
    """Step 3: Clean the raw data and structure it."""
    if not os.path.exists(config.DETAILS_OUTPUT_FILE):
        print(f"Raw details file not found: {config.DETAILS_OUTPUT_FILE}. Run with `--mode details` first.")
        return

    print(f"Reading raw data from '{config.DETAILS_OUTPUT_FILE}'...")
    df_raw = pd.read_csv(config.DETAILS_OUTPUT_FILE)
    df_raw = drop_mixed_listings(df_raw)

    cleaned_records = []
    for _, row in df_raw.iterrows():
        row_dict = row.to_dict()
        direct_features = DataCleaner.extract_direct_features(row_dict)

        # --- 1. Detect if it is a land-only property ---
        is_land = is_land_only(row_dict)

        # --- 2. Extract all data ---
        processed_data = {
            'Tỉnh/Thành phố': DataCleaner.extract_city(row_dict),
            'Thành phố/Quận/Huyện/Thị xã': DataCleaner.extract_district(row_dict),
            'Xã/Phường/Thị trấn': DataCleaner.extract_ward(row_dict),
            'Đường phố': DataCleaner.extract_street(row_dict),
            'Chi tiết': DataCleaner.extract_address_detail(row_dict),
            'Nguồn thông tin': row_dict.get('url'),
            'Tình trạng giao dịch': 'Rao bán',
            'Thời điểm giao dịch/rao bán': DataCleaner.extract_published_date(row_dict.get('main_info')),
            'Thông tin liên hệ': None,
            'Giá rao bán/giao dịch': DataCleaner.extract_total_price(row_dict.get('main_info')),
            'Loại đơn giá (đ/m2 hoặc đ/m ngang)': 'đ/m2',
            'Số tầng công trình': DataCleaner.extract_num_floors(row_dict),
            'Tổng diện tích sàn': DataCleaner.extract_built_area(row_dict),
            'Đơn giá xây dựng': DataCleaner.get_construction_cost(row_dict),
            'Năm xây dựng': None,
            'Chất lượng còn lại': DataCleaner.estimate_remaining_quality(row_dict),
            'Diện tích đất (m2)': DataCleaner.extract_total_area(row_dict),
            'Kích thước mặt tiền (m)': DataCleaner.extract_facade_width(row_dict),
            'Kích thước chiều dài (m)': DataCleaner.extract_land_length(row_dict),
            'Số mặt tiền tiếp giáp': DataCleaner.extract_facade_count(row_dict),
            'Hình dạng': DataCleaner.extract_land_shape(row_dict),
            'Độ rộng ngõ/ngách nhỏ nhất (m)': DataCleaner.extract_alley_width(row_dict),
            'Khoảng cách tới trục đường chính (m)': DataCleaner.extract_distance_to_main_road(row_dict),
            'Mục đích sử dụng đất': 'Đất ở',
            'Yếu tố khác': " | ".join(direct_features) if direct_features else None,
            'Tọa độ (vĩ độ)': row_dict.get('latitude'),
            'Tọa độ (kinh độ)': row_dict.get('longitude'),
            'Hình ảnh của bài đăng': row_dict.get('image_urls'),
            'description': row_dict.get('description'),
            'is_land': is_land  # <-- Add the temporary flag here
        }

        # --- 3. Apply special logic if it's land only ---
        if is_land:
            processed_data['Số tầng công trình'] = 0
            processed_data['Đơn giá xây dựng'] = 0
            processed_data['Tổng diện tích sàn'] = 0
            processed_data['Chất lượng còn lại'] = 0
        
        cleaned_records.append(processed_data)

    df_cleaned = pd.DataFrame(cleaned_records)

    try:
        # Standardize Province and District using the simplified AddressStandardizer
        address_std = AddressStandardizer(
            config.PROVINCES_SQL_FILE,
            config.DISTRICTS_SQL_FILE,
            config.WARDS_SQL_FILE,
            config.STREETS_SQL_FILE
        )
        df_cleaned['Tỉnh/Thành phố'] = df_cleaned['Tỉnh/Thành phố'].apply(address_std.standardize_province)
        df_cleaned['short_address'] = df_raw['short_address']
        df_cleaned['Thành phố/Quận/Huyện/Thị xã'] = df_cleaned.apply(address_std.standardize_district, axis=1)
        df_cleaned['Xã/Phường/Thị trấn'] = df_cleaned.apply(address_std.standardize_ward, axis = 1)
        df_cleaned.drop(columns=['short_address'], inplace = True)
        return df_cleaned
        # df_cleaned['Thành phố/Quận/Huyện/Thị xã'] = df_cleaned.apply(address_std.standardize_district, axis=1)
        # df_cleaned.drop(columns=['short_address'], inplace=True)
        # print("Province and District standardization complete.")
    except FileNotFoundError:
        print("Skipping province/district standardization because data files were not found.")

cleaned = run_cleaning_pipeline()

Reading raw data from 'output/listing_details.csv'...
Removed 4972 listings containing 'thổ cư'.
Error parsing price: local variable 'cleaned_num' referenced before assignment


In [ ]:
# from src.address_standardizer import AddressStandardizer
from src import config
import sqlite3
import pandas as pd
from unicodedata import normalize
from rapidfuzz import fuzz

conn = sqlite3.connect(":memory:")
conn.execute("CREATE TABLE provinces (name TEXT, code TEXT, status TEXT);")
conn.execute("CREATE TABLE districts (name TEXT, code TEXT, province_code TEXT, status TEXT);")
conn.execute("CREATE TABLE wards (name TEXT, code TEXT, district_code TEXT, status TEXT);")
conn.execute("CREATE TABLE streets (name TEXT, code TEXT, district_code TEXT, status TEXT);")

with open(config.PROVINCES_SQL_FILE, "r", encoding="utf-8") as f:
    conn.executescript(f.read())

with open(config.DISTRICTS_SQL_FILE, "r", encoding="utf-8") as f:
    dis_cleaned = f.read().replace("\\'", "''")
    conn.executescript(dis_cleaned)

with open(config.WARDS_SQL_FILE, "r", encoding="utf-8") as f:
    ward_cleaned = f.read().replace("\\'", "''")
    conn.executescript(ward_cleaned)

provinces_df = pd.read_sql_query("SELECT * FROM provinces", conn)
districts_df = pd.read_sql_query("""
    SELECT d.name AS district_name, p.name AS province_name
    FROM districts d
    JOIN provinces p ON d.province_code = p.code
    """, conn)

wards_df = pd.read_sql_query("""
    SELECT w.name AS ward_name,
        d.name AS district_name,
        p.name AS province_name
    FROM wards w
    JOIN districts d ON w.district_code = d.code
    JOIN provinces p ON d.province_code = p.code
""", conn)

if 'conn' in locals():
    conn.close()

reverse_province_map = {
    prov.replace("Thành phố ", "").replace("Tỉnh ", ""): prov
    for prov in provinces_df['name'].unique()
}

reverse_district = {}
for province in districts_df['province_name'].unique():
    reverse_district[province] = {}
    for district_name in districts_df[districts_df['province_name'] == province]['district_name'].unique():
        district_name_strip = district_name.replace('Thành phố ', '').replace('Thành Phố ', '').replace('Quận ', '').replace('Huyện ', '').replace('Thị xã ', '').replace('Thị Xã ', '').strip()
        reverse_district[province][district_name_strip] = district_name
reverse_district['Tỉnh Bà Rịa - Vũng Tàu']['Long Đất'] = 'Huyện Long Đất'
reverse_district['Thành phố Hồ Chí Minh']['Quận 2'] = 'Thành phố Thủ Đức'
reverse_district['Thành phố Hồ Chí Minh']['Quận 9'] = 'Thành phố Thủ Đức'

# for province in districts_df['province_name'].unique():
#     reverse_district[province] = {}
#     for district_name in districts_df[districts_df['province_name'] == province]['district_name'].unique():
#         # district_name_strip = normalize('NFKD', district_name.replace('Thành phố ', '').replace('Thành Phố ', '').replace('Quận ', '').replace('Huyện ', '').replace('Thị xã ', '').replace('Thị Xã ', '').strip())
#         district_name_strip = district_name.replace('Thành phố ', '').replace('Thành Phố ', '').replace('Quận ', '').replace('Huyện ', '').replace('Thị xã ', '').replace('Thị Xã ', '').strip()
#         reverse_district[province][district_name_strip] = district_name
# reverse_district['Tỉnh Bà Rịa - Vũng Tàu']['Long Đất'] = 'Huyện Long Đất'

reverse_ward = {}
for province in reverse_district.keys():
    reverse_ward[province] = {}
    for district in reverse_district[province].values():
        reverse_ward[province][district] = {}
        for ward in wards_df[wards_df['district_name'] == district]['ward_name'].unique():
            ward_name_strip = normalize('NFC', ward.replace('Xã ', '').replace('Phường ', '').replace('Thị trấn ', '').replace('Thị Trấn ', '').strip())
            reverse_ward[province][district][ward_name_strip] = ward
# for district in wards_df['district_name'].unique():
#     reverse_ward[district] = {}
#     for ward_name in wards_df[wards_df['district_name'] == district]['ward_name'].unique():
#         ward_name_strip = normalize('NFKD', ward_name.replace('Xã ', '').replace('Phường ', '').replace('Thị trấn ', '').replace('Thị Trấn ', '').strip())
#         reverse_ward[district][ward_name_strip] = ward_name

def standardize_district(row):
        prefix = ['Thành phố', 'Thành Phố', 'Quận', 'Huyện', 'Thị xã', 'Thị Xã', 'Đảo']
        district_value = row['Thành phố/Quận/Huyện/Thị xã']
        if isinstance(district_value, str):
            for pre in prefix:
                if district_value.startswith(pre):
                    return district_value
            province = row['Tỉnh/Thành phố']
            if district_value in reverse_district[province].keys():
                return reverse_district[province][district_value]
            for dis in reverse_district[province].keys():
                similarity = fuzz.ratio(district_value, dis)
                if similarity >= 66:
                    print(f'Value: {district_value}')
                    print(f"Short address: {row['short_address']}")
                    print(f"Predicted value: {reverse_district[province][dis]}")
                    print('-' * 50)
                    return reverse_district[province][dis]
            return district_value
        return None

def standardize_ward(row):
        ward_value = row['Xã/Phường/Thị trấn']

        def matching(ward_value, district_value, province_value):
            # Function to match values with its corresponding prefixes
            try:
                if ward_value in reverse_ward[province_value][district_value].keys():
                    return reverse_ward[province_value][district_value][ward_value]
            except:
                print(f'Ward value: {ward_value}\nDistrict value: {district_value}\nProvince value: {province_value}')
                print('-'*50)
                return None
            for ward in reverse_ward[province_value][district_value].keys():
                similarity = fuzz.ratio(ward_value, ward)
                if similarity >= 66:
                    return reverse_ward[province_value][district_value][ward]
                
        if ward_value:
            prefix = ['Xã', 'Phường', 'Thị trấn', 'Thị Trấn']
            for pre in prefix:
                if ward_value.startswith(pre):
                    return ward_value
            ward_value = normalize('NFC', ward_value)
            province_value = row['Tỉnh/Thành phố']
            district_value = row['Thành phố/Quận/Huyện/Thị xã']
            return matching(ward_value, district_value, province_value)
        else:
            short_add_value = row['short_address']
            if isinstance(short_add_value, str) and short_add_value != '':
                short_add_list = row['short_address'].split(',')
                if len(short_add_list) >= 3:
                    new_province_val = row['Tỉnh/Thành phố']
                    new_ward_val = normalize('NFC',short_add_list[-3].strip())
                    new_district_val = row['Thành phố/Quận/Huyện/Thị xã']
                    return matching(new_ward_val, new_district_val, new_province_val)
            return None


# cleaned['ward'] = cleaned.apply(standardize_ward, axis=1)

# Test Ward

In [ ]:
from unicodedata import normalize
import re

def standardize_ward(row):
        ward_value = row['Xã/Phường/Thị trấn']

        def matching(ward_value, district_value, province_value):
            # Function to match values with its corresponding prefixes
            if ward_value in reverse_ward[province_value][district_value].keys():
                return reverse_ward[province_value][district_value][ward_value]
            for ward in reverse_ward[province_value][district_value].keys():
                similarity = fuzz.ratio(ward_value, ward)
                if similarity >= 66:
                    return reverse_ward[province_value][district_value][ward]
            return None
                
        if ward_value:
            prefix = ['Xã', 'Phường', 'Thị trấn', 'Thị Trấn']
            for pre in prefix:
                if ward_value.startswith(pre):
                    return ward_value
            ward_value = normalize('NFC', ward_value)
            province_value = row['Tỉnh/Thành phố']
            district_value = row['Thành phố/Quận/Huyện/Thị xã']
            return matching(ward_value, district_value, province_value)
        else:
            short_add = row['short_address']
            if isinstance(short_add, str) and short_add != '':
                if 'xã' in short_add.lower():
                    print(f"Xã in short_add: {short_add.lower()}")
                    match_result = re.search(pattern='(xã [\w\s]+)', string=short_add.lower())
                    if match_result:
                        match_result = match_result[0]
                        result_split = match_result.split()
                        result = ' '.join(i.capitalize() for i in result_split)
                        return result
                elif 'phường' in short_add.lower():
                    print(f'Phường in short_add: {short_add.lower()}')
                    match_result = re.search(pattern='(phường [\w\s]+)', string=short_add.lower())
                    if match_result:
                        match_result = match_result[0]
                        result_split = match_result.split()
                        result = ' '.join(i.capitalize() for i in result_split)
                        return result
                elif 'thị trấn' in short_add.lower():
                    print(f'Thị trấn in short_add: {short_add.lower()}')
                    match_result = re.search(pattern='(thị trấn [\w\s]+)', string=short_add.lower())
                    if match_result:
                        match_result = match_result[0]
                        result_split = match_result.split()
                        result = ' '.join(i.capitalize() for i in result_split)
                        return result
                else:
                    short_add_list = row['short_address'].split(',')
                    if len(short_add_list) >= 3:
                        new_province_val = row['Tỉnh/Thành phố']
                        new_ward_val = normalize('NFC',short_add_list[-3].strip())
                        new_district_val = row['Thành phố/Quận/Huyện/Thị xã']
                        return matching(new_ward_val, new_district_val, new_province_val)

            else:
                return None
                # short_add_list = row['short_address'].split(',')
                # if len(short_add_list) >= 3:
                #     new_province_val = row['Tỉnh/Thành phố']
                #     new_ward_val = normalize('NFC',short_add_list[-3].strip())
                #     new_district_val = row['Thành phố/Quận/Huyện/Thị xã']
                #     return matching(new_ward_val, new_district_val, new_province_val)
            return None

In [ ]:
from rapidfuzz import fuzz

yo = cleaned['district'].iloc[24895]
dis = list(reverse_district['Tỉnh Đắk Lắk'].keys())[4]
print(fuzz.ratio(yo, dis))

66.66666666666667


# Test Prices (Mức giá)

In [ ]:
import pandas as pd
import numpy as np

listing_details = pd.read_csv('output/listing_details.csv')
listing_details.drop(['latitude', 'longitude', 'image_urls'], axis=1, inplace=True)
cleaned.rename(columns={"Nguồn thông tin": 'url'}, inplace=True)

df = pd.merge(left=cleaned, right=listing_details, how='left', on='url')
df.info()

In [ ]:
import json

df['other_info'] = df['other_info'].apply(json.loads)
df['price'] = df['other_info'].apply(lambda x: x.get('Mức giá'))

check_price_df = df[~df['price'].str.contains('tỷ', na=False)]
check_price_df = check_price_df[~(check_price_df['price'] == 'Thỏa thuận')]
print(f'Shape: {check_price_df.shape}')

check_price_df.dropna(subset = 'price', inplace=True, axis=0)
check_price_df['digit_price'] = check_price_df['price'].apply(lambda x: x.split()[0].replace(',', '.').strip())
check_price_df['digit_price'] = check_price_df['digit_price'].astype(float)
check_price_df['unit_price'] = check_price_df['price'].apply(lambda x: x.split()[1].strip())
print(check_price_df['unit_price'].unique())

nghin_met_vuong = check_price_df[check_price_df['unit_price'] == 'nghìn/m²']
nghin = check_price_df[check_price_df['unit_price'] == 'nghìn']
trieu_met_vuong = check_price_df[check_price_df['unit_price'] == 'triệu/m²']
trieu_incorrect = check_price_df[(check_price_df['unit_price'] == 'triệu') & (check_price_df['digit_price'] <= 300)]

# Test Khoảng cách tới trục đường chính

In [1]:
import pandas as pd
import json
import re

listing_details = pd.read_csv('output/listing_details.csv')
listing_details.drop(['latitude', 'longitude', 'image_urls', 'description'], axis=1, inplace=True)

listing_details_cleaned = pd.read_csv('output/listing_details_cleaned.csv')
listing_details_cleaned.rename(columns={'Nguồn thông tin': 'url'}, inplace=True)
df = pd.merge(listing_details_cleaned, listing_details, how='left', on='url')

df['other_info'] = df['other_info'].apply(json.loads)
df['main_info'] = df['main_info'].apply(json.loads)

In [2]:
df['Đường vào'] = df['other_info'].apply(lambda x: x.get('Đường vào'))
df['Đường vào'].isna().sum()
df.drop_duplicates(subset='description', inplace=True)
df.dropna(subset='description', inplace=True)

In [ ]:
import re
from src.cleaning import is_on_main_road

def extract_main_road_distance(des):
    if pd.notna(des):
        cach = re.findall(r'(cách\s*(?:\S+\s+){0,3}\d+(?:[.,]\d+)*m)', des.lower())
        ra = re.findall(r'(\d+(?:[.,]\d+)*m ra (?:\S+\s+){0,3})', des.lower())
        final = []
        if len(cach) > 0:
            final += cach
        if len(ra) > 0:
            final += ra
        if len(final) > 0:
            return str(final)
        if 'mặt phố' in des.lower() or 'mặt đường' in des.lower():
            return 'Mặt đường'
        return None
    return None

def new_extract_main_road_distance(des):
    if pd.notna(des):
        # ------TH1: Cách đường bao nhiêu m/bao nhiêu mét ra mặt đường------
        duong = 'đường|phố|mặt đường|mặt phố'
        mattien = 'mp|mặt tiền|mt|nhà|quốc lộ|ql'
        not_road = 'trường|chợ|siêu thị|vincom|aeon|lotte|biển|sông|hồ|bệnh viện|ubnd \
                    |công viên|cv|hẻm|hxh|ngõ|chung cư|cc|vườn|trung tâm|khu đô thị|kđt \
                    |kdt|vinmart|winmart|vin|mall|tttm|bigc|go|gigamall|sân bay|quận|q(?:\d+) \
                    |thành phố|tp|huyện|thị xã|thị trấn|tx|bến xe|bx'

        cach_duong_digit = re.search(rf'cách\s*(?:{duong})\s*(?:(?!\d+(?:[.,]\d+)*m)\S+\s*){{0,5}}?\D(\d+(?:[.,]\d+)*)m', des.lower())
        cach_not_digit_duong = re.search(rf'cách\s*(?:(?!\d+(?:[.,]\d+)*m)(?!{not_road})\S+\s*){{0,3}}?\D(\d+(?:[.,]\d+)*)m\s*(?:(?!{not_road})\S+\s*){{0,2}}(?:{duong})\s*', des.lower())
        ra_duong = re.search(rf'\D(\d+(?:[.,]\d+)*)m\s*ra\s*(?:{duong})\s*(?:\S+\s+){{0,5}}', des.lower())
        cach_mattien_digit = re.search(rf'cách\s*(?:{mattien})\s*(?:(?!\d+(?:[.,]\d+)*m)(?!{not_road})\S+\s*){{0,5}}?\D(\d+(?:[.,]\d+)*)m', des.lower())
        cach_not_digit_mattien = re.search(rf'cách\s*(?:(?!\d+(?:[.,]\d+)*m)(?!{not_road})\S+\s*){{0,3}}?\D(\d+(?:[.,]\d+)*)m\s*(?:(?!{not_road})\S+\s*){{0,2}}(?:{mattien})\s*', des.lower())
        ra_mattien = re.search(rf'\D(\d+(?:[.,]\d+)*)m\s*ra\s*(?:{mattien})\s*(?:\S+\s+){{0,5}}', des.lower())
        cach_not_digit_not_forbidden = re.search(rf'cách\s*(?:(?!\d+(?:[.,]\d+)*m)(?!:{not_road})\S+\s*){{0,3}}\s*\D(\d+(?:[.,]\d+)*)m', des.lower())
        ra_digit_not_for = re.search(rf'\D(\d+(?:[,.]\d+)*)m\s*ra\s*(?:(?!{not_road})\S+\s+)', des.lower())

        all_patterns = [cach_duong_digit, cach_not_digit_duong, ra_duong, cach_mattien_digit, cach_not_digit_mattien, ra_mattien, cach_not_digit_not_forbidden, ra_digit_not_for]
        for pattern in all_patterns:
            if pattern:
                return float(pattern.group(1).replace(',', '.'))
        if 'mặt phố' in des.lower() or 'mặt đường' in des.lower():
            return 'Mặt đường'
        return None
    return None

def new_ver2_extract_main_road_distance(des):
    if pd.notna(des):
        string = des.lower().replace('\n',' ')
        # ------TH1: Cách đường bao nhiêu m/bao nhiêu mét ra mặt đường------
        # First, reject any description that contains a forbidden word near "cách"
        duong = 'đường|phố|mặt đường|mặt phố|mp|vành đai|đại lộ|đl'
        mattien = 'mặt tiền|mt|trục chính|quốc lộ|ql|qlo|tỉnh lộ|tl|cầu|ngã tư|ngã ba|ngã 4|ngã 3|nhà'
        # not_road = 'trường|chợ|siêu thị|vincom|aeon|lotte|biển|sông|hồ|bệnh viện|ubnd \
        #             |công viên|cv|hẻm|hxh|ngõ|chung cư|cc|vườn|trung tâm|khu đô thị \
        #             |kđt|kdt|vinmart|winmart|vin|mall|tttm|bigc|go|gigamall|sân bay|quận|q(?:\d+) \
        #             |thành phố|tp|huyện|thị xã|thị trấn|tx|bệnh viện|bv|đại học|đh'
        # cach_duong_digit = re.search(rf'cách\s*(?:{duong})\s*(?:(?!\d+(?:[.,]\d+)*\s*k*m)\S+\s*){{0,5}}?\D(\d+(?:[.,]\d+)*\s*k*m)', des.lower())
        # cach_not_digit_duong = re.search(rf'cách\s*(?:(?!\d+(?:[.,]\d+)*\s*k*m)(?!{not_road})\S+\s*){{1,7}}?\D(\d+(?:[.,]\d+)*\s*k*m)\s*(?:(?!{not_road})\S+\s*){{0,2}}(?:{duong})\s*', des.lower())
        # ra_duong = re.search(rf'\D(\d+(?:[.,]\d+)*\s*k*m)\s*ra\s*(?:{duong})\s*(?:\S+\s+){{0,5}}', des.lower())
        # cach_mattien_digit = re.search(rf'cách\s*(?:{mattien})\s*(?:(?!\d+(?:[.,]\d+)*\s*k*m)(?!{not_road})\S+\s*){{1,7}}?\D(\d+(?:[.,]\d+)*\s*k*m)', des.lower())
        # cach_not_digit_mattien = re.search(rf'cách\s*(?:(?!\d+(?:[.,]\d+)*\s*k*m)(?!{not_road})\S+\s*){{1,7}}?\D(\d+(?:[.,]\d+)*\s*k*m)\s*(?:(?!{not_road})\S+\s*){{0,2}}(?:{mattien})\s*', des.lower())
        # ra_mattien = re.search(rf'\D(\d+(?:[.,]\d+)*\s*k*m)\s*ra\s*(?:{mattien})\s*(?:\S+\s+){{0,5}}', des.lower())
        # # cach_not_digit_not_forbidden = re.search(rf'cách\s*(?:(?!\d+(?:[.,]\d+)*k*m)(?!{not_road})\S+\s*){{1,7}}\D(\d+(?:[.,]\d+)*k*m)(?!\s*(?:\S+\s*){{0,7}}{not_road})', des.lower())
        # ra_digit_not_for = re.search(rf'\D(\d+(?:[,.]\d+)*\s*k*m)\s*ra\s*(?:(?!{not_road})\S+\s+)', des.lower())
        # all_patterns = [cach_duong_digit, cach_not_digit_duong, ra_duong, cach_mattien_digit, cach_not_digit_mattien, ra_mattien, ra_digit_not_for]
        # for pattern in all_patterns:
        #     if pattern:
        #         # return pattern.group(0)
        #         if re.search(not_road, pattern.group(0)):
        #             continue # pattern.group(1).replace(',', '.')
        #         return pattern.group(0)
        # cach_not_digit_not_forbidden = re.search(r'cách\s*(?:\S+\s*){1,7}\D(\d+(?:[.,]\d+)*\s*k*m)(?:\S+\s*){0,7}', des.lower())
        # if cach_not_digit_not_forbidden:
        #     if re.search(not_road, cach_not_digit_not_forbidden.group(0)):
        #         pass
        #     else:
        #         return cach_not_digit_not_forbidden.group(0)

        small_not_road = 'trường|chợ|siêu thị|vincom|aeon|lotte|công viên|cv|hẻm|hxh|ngõ|vườn|trung tâm|vinmart|winmart|vin|mall|tttm|bigc|go|gigamall|đại học|đh|bến xe|bx|ga'
        big_not_road = 'biển|sông|hồ|ubnd|chung cư|cc|khu đô thị|kđt|kdt|sân bay|bệnh viện|bv|quận|q(?:\d+)|thành phố|tp|huyện|thị xã|thị trấn|tx|bán kính'

        cach_duong_digit = re.search(rf'cách\s*(?:{duong})\s*(?:(?!\d{{1,3}}(?:[.,]\d+)*\s*(?:m|km))\S+\s*){{0,5}}?\D(\d{{1,3}}(?:[.,]\d+)?\s*(?:m|km))', string) # cách đường Phạm Văn Đồng 5m
        cach_not_digit_duong = re.search(rf'cách\s*(?:(?!\d{{1,3}}(?:[.,]\d+)?\s*(?:m|km))(?!{big_not_road}|{small_not_road})\S+\s*){{1,7}}?\D(\d{{1,3}}(?:[.,]\d+)?\s*(?:m|km))\s*(?:(?!{big_not_road}|{small_not_road})\S+\s*){{0,2}}(?:{duong})\s*', string) # cách nhà 20m là đường Thành Thái
        ra_duong = re.search(rf'\D(\d{{1,3}}(?:[.,]\d+)?\s*(?:m|km))\s*ra\s*(?:{duong})\s*(?:\S+\s+){{0,5}}', string) # 50m ra đường Cầu Giấy
        ra_duong_digit = re.search(rf'ra\s*(?:{duong}|{mattien})\s*(?:\S+\s+){{0,5}}\D(\d{{1,3}}(?:[.,]\d+)?\s*(?:m|km))', string) # ra mặt phố cổ 20 m
        # cach_not_digit_not_forbidden = re.search(r'(?:\b\w+\b\W+){0,5}?cách\s*(?:(?!\d+[.,])\S+\s*){0,7}\D(\d{1,3}(?:[.,]\d+)?\s*k*m)(?:\S+\s*){0,7}', string)
        cach_mattien_digit = re.search(rf'cách\s*(?:{mattien})\s*(?:(?!\d{{1,3}}(?:[.,]\d+)?\s*(?:m|km))(?!{big_not_road}|{small_not_road})\S+\s*){{1,7}}\D(\d{{1,3}}(?:[.,]\d+)?\s*(?:m|km))', string) # cách mặt tiền trần nhân tông 20m
        mattien_cach = re.search(rf'(?:{duong}|{mattien})\s*(?:\b\w+\b\W+){{0,5}}?cách\s*(?:\b\w+\b\W+){{0,5}}\s*(\d+(?:[.,]\d+)*\s*(?:m|km))', string) # đường trường chinh cách nhà 25 m
        cach_not_digit_mattien = re.search(rf'cách\s*(?:(?!\d{{1,3}}(?:[.,]\d+)?\s*(?:m|km))(?!{big_not_road}|{small_not_road})\S+\s*){{1,7}}?\D(\d{{1,3}}(?:[.,]\d+)?\s*(?:m|km))\s*(?:(?!{big_not_road}|{small_not_road})\S+\s*){{0,2}}(?:{mattien})\s*', string) # cách nhà 20m là quốc lộ 23b
        ra_mattien = re.search(rf'\D(\d{{1,3}}(?:[.,]\d+)?\s*(?:m|km))\s*ra\s*(?:\S+\s*){{0, 2}}(?:{mattien})\s*(?:\S+\s+){{0,5}}', string) # 50m ra quốc lộ 13
        ra_digit_not_for = re.search(rf'\D(\d{{1,3}}(?:[,.]\d+)?\s*(?:m|km))\s*ra\s*(?:(?!{big_not_road}|{small_not_road})\S+\s+)', string) # 28m ra trần hưng đạo
        all_patterns = [cach_duong_digit, cach_not_digit_duong, ra_duong, ra_duong_digit, cach_mattien_digit, mattien_cach, cach_not_digit_mattien, ra_mattien, ra_digit_not_for]
        for pattern in all_patterns:
            if pattern:
                # return pattern.group(0)
                if re.search(big_not_road, pattern.group(0)) or re.search(small_not_road, pattern.group(0)):
                    continue # pattern.group(1).replace(',', '.')
                if 'km' in pattern.group(1):
                    result = float(pattern.group(1).replace('km', '').replace(',', '.'))
                    result *= 1000
                    return result
                return float(pattern.group(1).replace('m', '').replace(',', '.'))
                # else:
                #     result = re.search('\d+(?:[.,]\d+)*', pattern.group(1))
                #     if 'km' in pattern.group(1):
                #         return 
                
        cach_not_digit_not_forbidden = re.search(r'(?:\b\w+\b\W+){0,5}?cách\s*(?:(?!\d+[.,])\S+\s*){0,7}\D(\d{1,3}(?:[.,]\d+)?\s*k*m)(?:\S+\s*){0,7}', string)
        if cach_not_digit_not_forbidden:
            if re.search(big_not_road, cach_not_digit_not_forbidden.group(0)) or re.search(small_not_road, cach_not_digit_not_forbidden.group(0)):
                pass
            else:
                if 'km' in cach_not_digit_not_forbidden.group(1):
                    result = float(cach_not_digit_not_forbidden.group(1).replace('km', '').replace(',', '.'))
                    result *= 1000
                    return result
                return float(cach_not_digit_not_forbidden.group(1).replace('m', '').replace(',', '.'))
        #------TH2: Ước lượng gần phố (nhà, bước chân, phút,...)------
        # cách \d nhà ra mặt phố
        if re.search(rf'cách\s*(?:\S+\s*){{0,2}}nhà\s*(?:\S+\s*){{0,3}}(?:{duong}|{mattien})', string):
            return 30
        # cách phố vài bước chân
        steps_1 = re.search(rf'bước\s*(?:\S+\s*){{0,5}}ra\s*(?:{duong}|{mattien})', string)
        steps_2 = re.search(rf'cách\s*(?:\S+\s*){{0,2}}(?:{duong}|{mattien}\s*)(?:\S+\s*){{0,2}}bước', string)
        if steps_1 or steps_2:
            return 5
        # vài phút
        if re.search(rf'phút(?:\S+\s*){{0,3}}ra\s*(?:{duong}|{mattien}\s*)', string):
            return 50
        # gần, sát, giáp
        if re.search(rf'(?:gần|giáp|sát)(?:\s+\S+){{0,2}}\s+(?:{duong}|{mattien})', string):
            return 40
        
        #------TH3: Ngõ nông------
        if re.search(r'ngõ\s*(?:\S+\s*){0,3}(?:nông|ngắn)', string):
            return 10
        #------TH4: Nếu nó ở trên đường chính------
        if 'mặt đường' in string or 'mặt phố' in string or 'mặt tiền đường' in string or 'mặt tiền phố' in string:
            return 0
        return None
    return None

# df['main_road_distance'] = df['description'].apply(extract_main_road_distance)
# df['new_main_road_distance'] = df['description'].apply(new_extract_main_road_distance)
df['new_ver4_main_road_distance'] = df['description'].apply(new_ver2_extract_main_road_distance)

In [23]:
duong = 'đường|phố|mặt đường|mặt phố|mp|vành đai|đại lộ|đl'
mattien = 'mặt tiền|mt|trục chính|quốc lộ|ql|qlo|tỉnh lộ|tl|cầu|ngã tư|ngã ba|ngã 4|ngã 3|nhà'

string = df.loc[9]['description'].lower().replace(',', '.').replace('\n', ' ')
string = 'chủ giảm 200tr thiện chí. phú hữu tp thủ đức (q9 cũ). chỉ còn 4.6 tỷ còn thương lượng cho khách thiện chí!  kết cấu: 1 trệt 2 lầu nhà mới đẹp. thiết kế hiện đại. hạ tầng hoàn chỉnh khu phân lô đồng bộ. đường rộng ô tô quay đầu thoải mái. pháp lý chuẩn chỉnh sổ riêng. công chứng ngay.  tiềm năng sinh lời cực cao nhờ vị trí nằm gần tuyến đường liên cảng cát lái phú hữu sắp hoàn thiện trục đường chiến lược dành riêng cho xe container kết nối các khu logistics lớn.  thích hợp mua ở. mở văn phòng. cho thuê hoặc đầu tư chờ tăng giá.  liên hệ ngay: mr. luân chuyên gia bất động sản khu đông. call/zalo: 0909 207 *** . đi xem nhà thực tế để cảm nhận giá trị!'
print(string)
print(re.search(rf'(?:gần|giáp|sát)(?:\s+\S+){{0,2}}\s+(?:{duong}|{mattien})', string))

chủ giảm 200tr thiện chí. phú hữu tp thủ đức (q9 cũ). chỉ còn 4.6 tỷ còn thương lượng cho khách thiện chí!  kết cấu: 1 trệt 2 lầu nhà mới đẹp. thiết kế hiện đại. hạ tầng hoàn chỉnh khu phân lô đồng bộ. đường rộng ô tô quay đầu thoải mái. pháp lý chuẩn chỉnh sổ riêng. công chứng ngay.  tiềm năng sinh lời cực cao nhờ vị trí nằm gần tuyến đường liên cảng cát lái phú hữu sắp hoàn thiện trục đường chiến lược dành riêng cho xe container kết nối các khu logistics lớn.  thích hợp mua ở. mở văn phòng. cho thuê hoặc đầu tư chờ tăng giá.  liên hệ ngay: mr. luân chuyên gia bất động sản khu đông. call/zalo: 0909 207 *** . đi xem nhà thực tế để cảm nhận giá trị!
<re.Match object; span=(328, 343), match='gần tuyến đường'>


In [32]:
pd.set_option('display.max_colwidth', None)

df[df['new_ver4_main_road_distance'].isna()][['description']][['description']].iloc[:20]

description
2                                                                                                                                                                                                                                                                                                                                                                                                                                                                      SIÊU PHẨM THÍCH QUẢNG ĐỨC - PHÚ NHUẬN - 5 TẦNG CHÍNH CHỦ 1 ĐỜI - 10.X TỶ\n\nHẺM Ô TÔ 7 CHỖ - 64M2 - ĐÃ XÂY FULL KHÔNG QUY HOẠCH KHÔNG LỘ GIỚI\n\nNHÀ ĐƯỢC CHÍNH CHÔNG TỰ XÂY - KIÊN CỐ 5 TẦNG - 9PN - VỀ KHAI THÁC CHDV TUYỆT VỜI\n\nThích Quảng Đức 64m² 5 tầng 3.4 x 19, 10.5 tỷ Phường 5 Phú Nhuận\n\nNhà 1 trệt 1 lững 2 lầu sân thượng - 9pn, 9wc, sân thượng trước sau, phòng thờ.\nSổ đẹp - hoàn công đầy đủ.\nGiá còn thương lượng nên anh chị em đánh mạnh - hiếm Phú Nhuận.\nHẻm 5m ô tô vào nhà quay đầu - khu dân trí cao - giá tốt\nALO XEM NHÀ\n0908 800 ***
3                                                                                                                                                                                                                                                                                                                       Bán nhà Phố Nguyễn Khánh Toàn, Cầu Giấy, khu phân lô, 82m², ở yên tĩnh.\n+ Nằm trong khu phân lô quân đội, ô tô vào tận cửa, khu vực dân trí cao, an ninh tốt.\n+ Giao thông di chuyển thuận tiện mọi nẻo đường, kết nối với Nguyễn Khánh Toàn, Nguyễn Đình Hoàn, Quan Hoa, Nguyễn Văn Huyên, Trần Cung, Đội Cấn,\nĐào Tấn, Bưởi, Trần Đăng Ninh, Nguyễn Phong Sắc,...\n+ Gần các trường cấp 1-2 Dịch Vọng, Công viên Nghĩa Đô, Trung tâm Thương mại Lotte,...\n+ Nhà dân xây chắc chắn, phù hợp cho thuê hoặc ở hộ gia đình đều được.\n+ Sổ đỏ đẹp, pháp lý rõ ràng, sẵn sàng giao dịch.\n+ Giá 18.2 tỷ (CÓ THƯƠNG LƯỢNG).\n\n***LH ngay để được tư vấn và hỗ trợ:\nMr. Thao\n0982 609 ***\n(miễn trung gian, môi giới).
10                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            Bán nhà cấp 4 giá rẻ đường Hưng Nhơn - SHR - 680 TR.\n- Diện tích: 5x18m.\n- Kết cấu: Nhà cấp 4, phòng khách, 2 phòng ngủ, 2 nhà vệ sinh, sân trước, sân sau.\n- Gần chợ, bệnh viện, ủy ban nhân dân, trường học.\n- Sổ hồng riêng.\n- Ngân hàng hỗ trợ vay 70%.\nLiên hệ:\n0936 382 ***\nPhương Linh để được trực tiếp xem nhà (miễn tiếp cò lái).
12                                                                                                                                                                                                    Nhà đẹp - dân xây - ba mặt thoáng - gần nhiều trường đại học - khu vực đông sinh viên - phù hợp ở hoặc cho thuê dòng tiền đều rất tuyệt vời.\n\nMô tả:\n- Nhà nằm vị trí cực đắc địa Phố Chùa Láng, nhà có thể vào từ nhiều hướng khác nhau, đẹp và gần nhất đi từ ngõ 850 đường Láng, xung quanh tiện ích ngập tràn, hàng quán tấp lập ngày đêm, phù hợp ở hoặc cho thuê giữ tiền đều rất tuyệt vời.\n\nThiết kế:\n- Nhà dân tự thiết kế và xây dựng 4 tầng 1 tum đầy đủ công năng sử dụng, KCBT cực chắc chắn, nội thất cơ bản đầy đủ.\n- Diện tích trên sổ 37m², từ tầng 2 đua 40m².\n\n+ Tầng 1: Phòng khách, khu bếp, wc, sân để xe.\n+ Tầng 2,3,4: Tổng 6 phòng ngủ, wc giữa.\n+ Tầng 5: Tum, sân phơi.\n- Giấy tờ pháp lý chuẩn, sẵn sàng giao dịch.\n- Liên hệ để được tư vấn và

In [6]:
def new_ver1_extract_main_road_distance(des):
    if pd.notna(des):
        string = des.lower().replace('\n',' ')
        # ------TH1: Cách đường bao nhiêu m/bao nhiêu mét ra mặt đường------
        # First, reject any description that contains a forbidden word near "cách"
        duong = 'đường|phố|mặt đường|mặt phố|mp|vành đai|đại lộ|đl'
        mattien = 'mặt tiền|mt|quốc lộ|ql|qlo|cầu|ngã tư|ngã ba|ngã 4|ngã 3'
        # not_road = 'trường|chợ|siêu thị|vincom|aeon|lotte|biển|sông|hồ|bệnh viện|ubnd \
        #             |công viên|cv|hẻm|hxh|ngõ|chung cư|cc|vườn|trung tâm|khu đô thị \
        #             |kđt|kdt|vinmart|winmart|vin|mall|tttm|bigc|go|gigamall|sân bay|quận|q(?:\d+) \
        #             |thành phố|tp|huyện|thị xã|thị trấn|tx|bệnh viện|bv|đại học|đh'
        # cach_duong_digit = re.search(rf'cách\s*(?:{duong})\s*(?:(?!\d+(?:[.,]\d+)*\s*k*m)\S+\s*){{0,5}}?\D(\d+(?:[.,]\d+)*\s*k*m)', des.lower())
        # cach_not_digit_duong = re.search(rf'cách\s*(?:(?!\d+(?:[.,]\d+)*\s*k*m)(?!{not_road})\S+\s*){{1,7}}?\D(\d+(?:[.,]\d+)*\s*k*m)\s*(?:(?!{not_road})\S+\s*){{0,2}}(?:{duong})\s*', des.lower())
        # ra_duong = re.search(rf'\D(\d+(?:[.,]\d+)*\s*k*m)\s*ra\s*(?:{duong})\s*(?:\S+\s+){{0,5}}', des.lower())
        # cach_mattien_digit = re.search(rf'cách\s*(?:{mattien})\s*(?:(?!\d+(?:[.,]\d+)*\s*k*m)(?!{not_road})\S+\s*){{1,7}}?\D(\d+(?:[.,]\d+)*\s*k*m)', des.lower())
        # cach_not_digit_mattien = re.search(rf'cách\s*(?:(?!\d+(?:[.,]\d+)*\s*k*m)(?!{not_road})\S+\s*){{1,7}}?\D(\d+(?:[.,]\d+)*\s*k*m)\s*(?:(?!{not_road})\S+\s*){{0,2}}(?:{mattien})\s*', des.lower())
        # ra_mattien = re.search(rf'\D(\d+(?:[.,]\d+)*\s*k*m)\s*ra\s*(?:{mattien})\s*(?:\S+\s+){{0,5}}', des.lower())
        # # cach_not_digit_not_forbidden = re.search(rf'cách\s*(?:(?!\d+(?:[.,]\d+)*k*m)(?!{not_road})\S+\s*){{1,7}}\D(\d+(?:[.,]\d+)*k*m)(?!\s*(?:\S+\s*){{0,7}}{not_road})', des.lower())
        # ra_digit_not_for = re.search(rf'\D(\d+(?:[,.]\d+)*\s*k*m)\s*ra\s*(?:(?!{not_road})\S+\s+)', des.lower())
        # all_patterns = [cach_duong_digit, cach_not_digit_duong, ra_duong, cach_mattien_digit, cach_not_digit_mattien, ra_mattien, ra_digit_not_for]
        # for pattern in all_patterns:
        #     if pattern:
        #         # return pattern.group(0)
        #         if re.search(not_road, pattern.group(0)):
        #             continue # pattern.group(1).replace(',', '.')
        #         return pattern.group(0)
        # cach_not_digit_not_forbidden = re.search(r'cách\s*(?:\S+\s*){1,7}\D(\d+(?:[.,]\d+)*\s*k*m)(?:\S+\s*){0,7}', des.lower())
        # if cach_not_digit_not_forbidden:
        #     if re.search(not_road, cach_not_digit_not_forbidden.group(0)):
        #         pass
        #     else:
        #         return cach_not_digit_not_forbidden.group(0)

        small_not_road = 'trường|chợ|siêu thị|vincom|aeon|lotte|công viên|cv|hẻm|hxh|ngõ|vườn|trung tâm|vinmart|winmart|vin|mall|tttm|bigc|go|gigamall|đại học|đh|bến xe|bx|ga'
        big_not_road = 'biển|sông|hồ|ubnd|chung cư|cc|khu đô thị|kđt|kdt|sân bay|bệnh viện|bv|quận|q(?:\d+)|thành phố|tp|huyện|thị xã|thị trấn|tx|bán kính'

        cach_duong_digit = re.search(rf'cách\s*(?:{duong})\s*(?:(?!\d{{1,3}}(?:[.,]\d+)*\s*(?:m|km))\S+\s*){{0,5}}?\D(\d{{1,3}}(?:[.,]\d+)?\s*(?:m|km))', string)
        cach_not_digit_duong = re.search(rf'cách\s*(?:(?!\d{{1,3}}(?:[.,]\d+)?\s*(?:m|km))(?!{big_not_road}|{small_not_road})\S+\s*){{1,7}}?\D(\d{{1,3}}(?:[.,]\d+)?\s*(?:m|km))\s*(?:(?!{big_not_road}|{small_not_road})\S+\s*){{0,2}}(?:{duong})\s*', string)
        ra_duong = re.search(rf'\D(\d{{1,3}}(?:[.,]\d+)?\s*(?:m|km))\s*ra\s*(?:{duong})\s*(?:\S+\s+){{0,5}}', string)
        cach_not_digit_not_forbidden = re.search(r'(?:\b\w+\b\W+){0,5}?cách\s*(?:(?!\d+[.,])\S+\s*){0,7}\D(\d{1,3}(?:[.,]\d+)?\s*k*m)(?:\S+\s*){0,7}', string)
        cach_mattien_digit = re.search(rf'cách\s*(?:{mattien})\s*(?:(?!\d{{1,3}}(?:[.,]\d+)?\s*(?:m|km))(?!{big_not_road}|{small_not_road})\S+\s*){{1,7}}\D(\d{{1,3}}(?:[.,]\d+)?\s*(?:m|km))', string)
        cach_not_digit_mattien = re.search(rf'cách\s*(?:(?!\d{{1,3}}(?:[.,]\d+)?\s*(?:m|km))(?!{big_not_road}|{small_not_road})\S+\s*){{1,7}}?\D(\d{{1,3}}(?:[.,]\d+)?\s*(?:m|km))\s*(?:(?!{big_not_road}|{small_not_road})\S+\s*){{0,2}}(?:{mattien})\s*', string)
        ra_mattien = re.search(rf'\D(\d{{1,3}}(?:[.,]\d+)?\s*(?:m|km))\s*ra\s*(?:\S+\s*){{0, 2}}(?:{mattien})\s*(?:\S+\s+){{0,5}}', string)
        ra_digit_not_for = re.search(rf'\D(\d{{1,3}}(?:[,.]\d+)?\s*(?:m|km))\s*ra\s*(?:(?!{big_not_road}|{small_not_road})\S+\s+)', string)
        all_patterns = [cach_duong_digit, cach_not_digit_duong, ra_duong, cach_not_digit_not_forbidden, cach_mattien_digit, cach_not_digit_mattien, ra_mattien, ra_digit_not_for]
        for pattern in all_patterns:
            if pattern:
                # return pattern.group(0)
                if re.search(big_not_road, pattern.group(0)) or re.search(small_not_road, pattern.group(0)):
                    continue # pattern.group(1).replace(',', '.')
                if 'km' in pattern.group(1):
                    result = float(pattern.group(1).replace('km', '').replace(',', '.'))
                    result *= 1000
                    return result
                return float(pattern.group(1).replace('m', '').replace(',', '.'))
                # else:
                #     result = re.search('\d+(?:[.,]\d+)*', pattern.group(1))
                #     if 'km' in pattern.group(1):
                #         return 
                
        # cach_not_digit_not_forbidden = re.search(r'(?:\b\w+\b\W+){0,5}?cách\s*(?:(?!\d+[.,])\S+\s*){0,7}\D(\d{1,3}(?:[.,]\d+)?\s*k*m)(?:\S+\s*){0,7}', string)
        # if cach_not_digit_not_forbidden:
        #     print(cach_not_digit_not_forbidden.group(0))
        #     if re.search(big_not_road, cach_not_digit_not_forbidden.group(0)) or re.search(small_not_road, cach_not_digit_not_forbidden.group(0)):
        #         pass
        #     else:
        #         if 'km' in cach_not_digit_not_forbidden.group(1):
        #             result = float(cach_not_digit_not_forbidden.group(1).replace('km', '').replace(',', '.'))
        #             result *= 1000
        #             return result
        #         return float(cach_not_digit_not_forbidden.group(1).replace('m', '').replace(',', '.'))

        if 'mặt phố' in string or 'mặt đường' in string:
            return 'Mặt đường'
        return None
    return None

df['new_ver1_main_road_distance'] = df['description'].apply(new_ver1_extract_main_road_distance)

In [38]:
des = df.loc[71]['description']
string = des.lower().replace('\n',' ')
print(string)
# ------TH1: Cách đường bao nhiêu m/bao nhiêu mét ra mặt đường------
# First, reject any description that contains a forbidden word near "cách"
duong = 'đường|phố|mặt đường|mặt phố|mp|vành đai|đại lộ|đl'
mattien = 'mặt tiền|mt|trục chính|quốc lộ|ql|qlo|cầu|ngã tư|ngã ba|ngã 4|ngã 3'
small_not_road = 'trường|chợ|siêu thị|vincom|aeon|lotte|công viên|cv|hẻm|hxh|ngõ|vườn|trung tâm|vinmart|winmart|vin|mall|tttm|bigc|go|gigamall|đại học|đh|bến xe|bx|ga'
big_not_road = 'biển|sông|hồ|ubnd|chung cư|cc|khu đô thị|kđt|kdt|sân bay|bệnh viện|bv|quận|q(?:\d+)|thành phố|tp|huyện|thị xã|thị trấn|tx|bán kính'

cach_not_digit_duong = re.search(rf'cách\s*(?:(?!\d{{1,3}}(?:[.,]\d+)?\s*(?:m|km))(?!{big_not_road}|{small_not_road})\S+\s*){{1,7}}?\D(\d{{1,3}}(?:[.,]\d+)?\s*(?:m|km))\s*(?:(?!{big_not_road}|{small_not_road})\S+\s*){{0,2}}(?:{duong})\s*', string)
print(cach_not_digit_duong)

nhanh tay sở hữu căn nhà riêng " có 1 không 2" xây dựng 56m² x 6 tầng, sổ đỏ 54m², thang máy, mặt ngõ 82 phố nguyễn an ninh, oto đỗ ngay mặt phố "cách nhà 15m". giá 14,5 tỷ có thương lượng. thiết kế theo phong cách hiện đại châu âu, có bản vẽ thiết kế riêng. tầng 1: phòng khách + khu thang máy, thang bộ, wc + phòng ăn và bếp. tầng 2,3,4,5: thiết kế mỗi tầng 02 phòng ngủ + wc khép kín từng phòng. tầng 6: thiết kế vườn trên cao, xanh mát mắt hòa mình với thiên nhiên + sân tập thể thao + sân phơi. - điểm nhấn: căn nhà có thiết kế hiện đại với 8 phòng ngủ và 9 phòng tắm, phù hợp cho gia đình lớn hoặc cho thuê. nội thất: dùng toàn nguyên liệu ngoại nhập cùng các nhà sản xuất có uy tín hàng đầu trong nước: - thang máy fuji 550kg chở 8 người lớn. - gạch ốp lát italia. - cầu thang bộ tay vịn gỗ lim. sổ đỏ chính chủ. - gần các tiện ích: + ngay sát các trường mẫu giáo chuẩn quốc gia, cấp 1,2 tân định. + cách các trường đại học lớn: bách khoa - xây dựng - kinh tế quốc dân - học viện tài chính, kh

In [ ]:
df[df['new_ver2_main_road_distance'] == 'Mặt đường'][['description', 'Khoảng cách tới trục đường chính (m)']]

description  \
51                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                   Căn hộ tập thể mặt phố vip - gần ô tô đỗ - view đẹp - đầu tư giữ tiền - kinh doanh online - khai thác homestay - chỉ 10,9 tỷ - sở hữu 60m² x 2 tầng - Quang Trung - Hoàn Kiếm.\nPháp lý: Sổ đỏ cất két giao dịch ngay.\n0372 739 ***\n.\nLH Ms: Vân nhà đẹp phố cổ.\n\nVị trí trung tâm cực hiếm nhà bán, thuộc tuyến phố cổ khách du lịch qua lại tấp nập. Kinh doanh Hometay siêu lợi nhuận.\nGần Hồ Hoàn Kiếm. Vimcom. Trường học. Bệnh Viện. Chợ dân sinh.\nKhông gian sống lý tưởng trong khu vực đáng sống bậc nhất Thủ đô.\nThiết kế 2 ngủ đủ công năng.   
68                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                       

# Test Area (Diện tích đất)

In [ ]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 27491 entries, 0 to 27490
Data columns (total 35 columns):
 #   Column                                Non-Null Count  Dtype  
---  ------                                --------------  -----  
 0   Tỉnh/Thành phố                        27491 non-null  object 
 1   Thành phố/Quận/Huyện/Thị xã           27491 non-null  object 
 2   Xã/Phường/Thị trấn                    27469 non-null  object 
 3   Đường phố                             23802 non-null  object 
 4   Chi tiết                              27491 non-null  object 
 5   url                                   27491 non-null  object 
 6   Tình trạng giao dịch                  27491 non-null  object 
 7   Thời điểm giao dịch/rao bán           27479 non-null  object 
 8   Thông tin liên hệ                     0 non-null      object 
 9   Giá rao bán/giao dịch                 24953 non-null  float64
 10  Loại đơn giá (đ/m2 hoặc đ/m ngang)    27491 non-null  object 
 11  Số tầng công tr

In [ ]:
def area(row):
    if row['other_info'] != {}:
        return row['other_info'].get('Diện tích')
    return row['main_info'][1].get('value')

df['area'] = df.apply(area, axis=1)
print(df.shape[0])
df = df[~(df['area'] == '')]
print(df.shape[0])
# df = df[df['area'].str.contains('m²')]
# df['digit_area'] = df['area'].apply(lambda x: float(x.split()[0].replace('.', '').replace(',','.')))

27491
27489


# Test number of floors (Số tầng công trình)

In [ ]:
import pandas as pd
import json

listing_details = pd.read_csv('output/listing_details.csv')
listing_details.drop(['latitude', 'longitude', 'image_urls', 'description'], axis=1, inplace=True)

listing_details_cleaned = pd.read_csv('output/listing_details_cleaned.csv')
listing_details_cleaned.rename(columns={'Nguồn thông tin': 'url'}, inplace=True)
df = pd.merge(listing_details_cleaned, listing_details, how='left', on='url')

df['other_info'] = df['other_info'].apply(json.loads)
df['main_info'] = df['main_info'].apply(json.loads)

In [ ]:
df['yes_floor'] = df['other_info'].apply(lambda x: x.get('Số tầng') if x.get('Số tầng') else None)
df['yes_floor'] = df['yes_floor'].apply(lambda x: int(x.split()[0]) if x is not None else None)
print(df[~df['yes_floor'].isna()].shape[0])
no_floor_in_other_info = df[df['yes_floor'].isna()]

16464


In [ ]:
df.shape[0]

18536

In [ ]:
import re
import numpy as np
# from rapidfuzz import fuzz

def check_additional_floor(value):
    additional_floor = ['sân thượng', 'sân thương', ' st ', 'trệt', 'trêt', 'tret', 'tum', 'hầm', 'hâm', 'gác lửng', 'gác mái', 'lửng', 'lững', 'lừng']
    result = 0
    for word in additional_floor:
        if word in value:
        # tokens = value.split()
        # for token in tokens:
        #     if fuzz.ratio(token, word) > 70:
            if word == 'sân thượng' or word == 'sân thương':
                additional_floor.remove(' st ')
            if word == ' st ':
                additional_floor.remove('sân thượng')
            print(f'Additional Floor word detected: {word}')
            result += 1
    return result

def clean_num_floor(row):
    print(f'Cleaning for row {row["index"]}')
    floor_keywords = ['tầng', 'lầu', 'tấm', 'mê']
    word_to_num = {
            "một": 1, "hai": 2, "ba": 3, "bốn": 4, "năm": 5, "sáu": 6,
            "bảy": 7, "bẩy": 7, "tám": 8, "chín": 9, "mười": 10,
            "mười một": 11, "mười hai": 12, "mười ba": 13, "mười bốn": 14,
            "mười lăm": 15, "mười sáu": 16
        }
    # reuse word_to_num from before
    num_words_pattern = "|".join(sorted(word_to_num.keys(), key=lambda x: -len(x)))
    # ------- TH1: Thông tin đã có sẵn ở other_info ------
    if row['other_info'] != {} and row['other_info'].get('Số tầng'):
        return int(row['other_info'].get('Số tầng').split()[0])
    # ------ TH2: Nhà cũ/nhà cấp 4 ở title/description ------
    if pd.notna(row['title']):
        lower_title = row['title'].lower()
        old_house = re.search(pattern=r'nhà (?:\w+\s){0,5}cũ', string=lower_title)
        if old_house:
            return 0
        cap4 = re.search(pattern = r'nhà cấp 4|nhà c4|cấp 4|nc4|nhà trệt', string=lower_title)
        if cap4:
            return 1
    if pd.notna(row['description']):
        try:
            lower_des = row['description'].lower()
            old_house = re.search(pattern=r'nhà (?:\w+\s){0,5}cũ', string=lower_des)
            if old_house:
                return 0
            cap4 = re.search(pattern = r'nhà cấp 4|nhà c4|cấp 4|nc4|nhà trệt', string=lower_des)
            if cap4:
                return 1
        except:
            print(row['description'] == np.nan)
    # ------ TH3: Xét số tầng ------
    # Tống số tầng trong title
    if pd.notna(row['title']):
        add_key = check_additional_floor(lower_title)
        for keyword in floor_keywords:
            if keyword in lower_title:
                num_floor = re.search(pattern=rf'(\d|{num_words_pattern})\s*{keyword}', string=lower_title)
                if num_floor:
                    print(f'Extracted floor in title: {num_floor.group(1)}')
                    print(f'Additional value: {add_key}')
                    if num_floor.group(1).isdigit():
                        possible_float = re.search(pattern=rf'(\d+[.,]\d+)\s*{keyword}', string=lower_title)
                        if possible_float:
                            print(f'Found possible float: {possible_float.group(1)}')
                            return float(possible_float.group(1).replace(',','.')) + add_key
                        return int(num_floor.group(1)) + add_key
                    return word_to_num[num_floor.group(1)] + add_key
                    # elif num_floor.group(1) in word_to_num.keys():
                    #     index_needed.append(row['index'])
                    #     return word_to_num[num_floor.group(1)] + add_key
    if pd.notna(row['description']):
        add_key = check_additional_floor(lower_des)
        # Trong trường hợp nêu rõ tầng 1, tầng 2,... thì max sẽ là tổng số tầng
        total_pattern = re.findall(pattern=r'(?:tầng|lầu|tấm|mê)\s* ([\d\w]+):', string=lower_des)
        if total_pattern:
            print(f"Extracted total floor in description: {total_pattern}")
            total_floor_num = []
            for digit in total_pattern:
                if digit.isdigit():
                    total_floor_num.append(int(digit))
                elif digit in word_to_num.keys():
                    total_floor_num.append(word_to_num[digit])
            if total_floor_num:
                return max(total_floor_num)
        
        # Trong trường hợp liệt kê ra cả lố tầng thì là cộng tổng vào
        separate_pattern = re.search(pattern=rf'(\d|{num_words_pattern})\s*(?:tầng|lầu|tấm|mê)', string=lower_des)
        if separate_pattern:
            print(f'Extracted floor that needs to be sum up: {separate_pattern.group(1)}')
            print(f'Additional value: {add_key}')
            if separate_pattern.group(1).isdigit():
                possible_float = re.search(pattern=rf'(\d+[.,]\d+)\s*(?:tầng|lầu|tấm|mê)', string=lower_des)
                if possible_float:
                    print(f'Found possible float: {possible_float.group(1)}')
                    return float(possible_float.group(1).replace(',','.')) + add_key
                return int(separate_pattern.group(1)) + add_key
            return word_to_num[separate_pattern.group(1)] + add_key
    return 'Không ghi rõ'
    # elif row['description'] is not None:
    #     lower_des = row['description'].lower()
    #     old_house = re.search(pattern=rf'nhà [\w+\s]{0-5}cũ', string=lower_des)
    #     if old_house:
    #         return 0
    #     cap4 = re.search(pattern = r'nhà cấp 4|nhà c4|cấp 4|nc4|nhà trệt', string=lower_des)
    #     if cap4:
    #         return 1
        
    #     add_key = check_additional_floor(lower_des)

df['index'] = df.index
df['floor_extracted_from'] = ''
df['floor'] = df.apply(clean_num_floor, axis = 1)

Cleaning for row 0
Cleaning for row 1
Cleaning for row 2
Cleaning for row 3
Cleaning for row 4
Cleaning for row 5
Cleaning for row 6
Cleaning for row 7
Cleaning for row 8
Cleaning for row 9
Cleaning for row 10
Cleaning for row 11
Cleaning for row 12
Cleaning for row 13
Cleaning for row 14
Cleaning for row 15
Cleaning for row 16
Cleaning for row 17
Cleaning for row 18
Cleaning for row 19
Cleaning for row 20
Cleaning for row 21
Cleaning for row 22
Cleaning for row 23
Cleaning for row 24
Cleaning for row 25
Cleaning for row 26
Cleaning for row 27
Extracted floor in title: 6
Additional value: 0
Cleaning for row 28
Cleaning for row 29
Cleaning for row 30
Cleaning for row 31
Cleaning for row 32
Cleaning for row 33
Cleaning for row 34
Cleaning for row 35
Cleaning for row 36
Cleaning for row 37
Cleaning for row 38
Cleaning for row 39
Cleaning for row 40
Additional Floor word detected: hầm
Extracted floor in title: 6
Additional value: 1
Cleaning for row 41
Cleaning for row 42
Cleaning for row 4

## Code extract num floor ở dưới này

In [ ]:
# Code không lỗi 
import re
import numpy as np
from rapidfuzz import fuzz

# def check_additional_floor(value):
#     additional_floor = ['sân thượng', 'sân thương', ' st ', 'trệt', 'trêt', 'tret', 'tum', 'hầm', 'hâm', 'gác lửng', 'gác mái', 'lửng', 'lững', 'lừng']
#     result = 0
#     for word in additional_floor:
#         if word in value:
#         # tokens = value.split()
#         # for token in tokens:
#         #     if fuzz.ratio(token, word) > 70:
#             if word == 'sân thượng' or word == 'sân thương':
#                 additional_floor.remove(' st ')
#             if word == ' st ':
#                 additional_floor.remove('sân thượng')
#             print(f'Additional Floor word detected: {word}')
#             result += 1
#     return result

def new_check_additional_floor(string, additional_floor):
    result = 0
    for word in additional_floor:
        if word in string:
            result += 1
    search_st = re.search(pattern=r'(\Wst\W)', string=string)
    if search_st:
        result += 1
    search_gl = re.search(pattern=r'gác lửng|gác lững|ghác lửng|ghác lững', string=string)
    if search_gl:
        result -= 1
    return result 

def is_float(num):
    try:
        float(num)
        return True
    except:
        return False

def extract_separate(lower_value, floor_keywords):
    value_list = lower_value.split()
    forbidden_pattern = r'giấy phép xây dựng|giấy phép xây|phép xây dựng|gpxd|có thể xây|cải tạo|được phép xây'
    additional_floor = ['sân thượng', 'sân thương', 'trêt', 'trệt', 'tret', 'tum', 'hầm', 'hâm', 'gác', 'gac', 'lửng', 'lững', 'lừng']
    if 'trệt' in floor_keywords:
        additional_floor = ['sân thượng', 'sân thương',  'tum', 'hầm', 'hâm', 'gác', 'gac', 'lửng', 'lững', 'lừng']
    word_to_num = {
            "một": 1, "hai": 2, "ba": 3, "bốn": 4, "năm": 5, "sáu": 6,
            "bảy": 7, "bẩy": 7, "tám": 8, "chín": 9, "mười": 10,
            "mười một": 11, "mười hai": 12, "mười ba": 13, "mười bốn": 14,
            "mười lăm": 15, "mười sáu": 16
        }
    for keyword in floor_keywords: # Check cho từng chiếc keyword
        if keyword in lower_value: # Nếu trong string có một trong những chiếc keyword
            i = 0
            while i < len(value_list):
                # for value in value_list: # Tìm trong list string mà đã được tách ra sẵn
            #     if keyword in value: # Nếu chiếc keyword đã tìm thấy ban nãy là của từ này
                    # word_index = value_list.index(value) # Lấy index của từ
                if keyword in value_list[i]: # Tìm index của chiếc từ keyword floor 
                    # Trong trường hợp mà nó bị dính chữ vào với nhau
                    extracted_floor = value_list[i].replace(keyword, '').replace(',','.')
                    if is_float(extracted_floor) or (extracted_floor in word_to_num.keys()): 
                        word_lower = i - 4 if i - 4 >= 0 else 0
                        word_upper = i + 4 if i + 4 < len(value_list) else len(value_list) - 1
                        search_range = ' '.join(value_list[word_lower:word_upper + 1]) # Tìm trong khoảng 5 từ trước - sau của từ
                        forbidden_word = re.search(pattern=forbidden_pattern, string=search_range)
                        if forbidden_word: # Nếu xuất hiện forbidden word
                            i += 1
                        else:
                            if 'hiện trạng' in ' '.join(value_list[word_lower:i]): # Nếu hiện trạng 3 tầng --> return luôn
                                if is_float(extracted_floor):
                                    return abs(float(extracted_floor))
                                if extracted_floor in word_to_num.keys():
                                    return word_to_num[extracted_floor]
                            else:
                                if is_float(extracted_floor) or (extracted_floor in word_to_num.keys()):
                                    add_key = new_check_additional_floor(search_range, additional_floor)
                                    if is_float(extracted_floor):
                                        return abs(float(extracted_floor)) + add_key
                                    return word_to_num[extracted_floor] + add_key
                                else:
                                    add_key = new_check_additional_floor(search_range, additional_floor)
                                    if add_key > 0:
                                        return add_key + 1
                                    else:
                                        i += 1
                    # Nếu có thể extract vị trí ở đằng trước keyword đã cho
                    elif i - 1 >= 0:
                        extracted_floor = value_list[i - 1].replace(',', '.')
                        word_lower = i - 4 if i - 4 >= 0 else 0
                        word_upper = i + 4 if i + 4 < len(value_list) else len(value_list) - 1
                        search_range = ' '.join(value_list[word_lower:word_upper + 1]) # Tìm trong khoảng 5 từ trước - sau của từ
                        forbidden_word = re.search(pattern=forbidden_pattern, string=search_range)
                        if forbidden_word: # Nếu xuất hiện forbidden word
                            i += 1
                        else:
                            if 'hiện trạng' in ' '.join(value_list[word_lower:i]): # Nếu hiện trạng 3 tầng --> return luôn
                                if is_float(extracted_floor):
                                    return abs(float(extracted_floor))
                                elif extracted_floor in word_to_num.keys():
                                    return word_to_num[extracted_floor]
                                else:
                                    i += 1
                            else:
                                if is_float(extracted_floor) or (extracted_floor in word_to_num.keys()):
                                    add_key = new_check_additional_floor(search_range, additional_floor)
                                    if is_float(extracted_floor):
                                        return abs(float(extracted_floor)) + add_key
                                    return word_to_num[extracted_floor] + add_key
                                else:
                                    add_key = new_check_additional_floor(search_range, additional_floor)
                                    if add_key > 0:
                                        return add_key + 1
                                    else:
                                        i += 1
                    else:
                        i += 1
                else:
                    i += 1
    
    return None


def clean_num_floor(row):
    floor_keywords = ['tầng', 'lầu', 'tấm', 'mê']
    word_to_num = {
            "một": 1, "hai": 2, "ba": 3, "bốn": 4, "năm": 5, "sáu": 6,
            "bảy": 7, "bẩy": 7, "tám": 8, "chín": 9, "mười": 10,
            "mười một": 11, "mười hai": 12, "mười ba": 13, "mười bốn": 14,
            "mười lăm": 15, "mười sáu": 16
        }
    # ------- TH1: Thông tin đã có sẵn ở other_info ------
    if row['other_info'] != {} and row['other_info'].get('Số tầng'):
        return int(row['other_info'].get('Số tầng').split()[0])
    # ------ TH2: Nhà cũ/nhà cấp 4 ở title/description ------
    # Xét của description trước do description thường được viết đầy đủ hơn
    if pd.notna(row['description']):
        lower_des = row['description'].lower().replace('+', ' ').replace('x',' ').replace('*', ' ')
        old_house = re.search(pattern=r'nhà (?:\w+\s*){0,5}cũ|bán(?:\s+\S\s*){0,5}đất', string=lower_des)
        if old_house:
            return 0
        cap4 = re.search(pattern = r'nhà cấp 4|nhà c4|cấp 4|nc4|nhà trệt|nhà nát', string=lower_des)
        if cap4:
            if cap4.group(0) == 'nhà trệt':
                extract_result = extract_separate(lower_des, floor_keywords)
                if extract_result:
                    return extract_result
            return 1
    if pd.notna(row['title']):
        lower_title = row['title'].lower().replace('+', ' ').replace('x',' ').replace('*', ' ')
        old_house = re.search(pattern=r'nhà (?:\w+\s*){0,5}cũ|bán(?:\s+\S\s*){0,5}đất', string=lower_title)
        if old_house:
            return 0
        cap4 = re.search(pattern = r'nhà cấp 4|nhà c4|cấp 4|nc4|nhà trệt|nhà nát', string=lower_title)
        if cap4:
            if cap4.group(0) == 'nhà trệt':
                extract_result = extract_separate(lower_title, floor_keywords)
                if extract_result:
                    return extract_result
            return 1
    # ------ TH3: Xét tổng số tầng ------
        extract_result = extract_separate(lower_title, floor_keywords)
        if extract_result:
            return extract_result
    # Có lẽ với trường hợp này, nếu có add_key thì skip xuống extract description cho đủ, nếu description không na hoặc kệ luôn
    # if pd.notna(row['title']):
    #     add_key = check_additional_floor(lower_title)
    #     for keyword in floor_keywords:
    #         if keyword in lower_title:
    #             num_floor = re.search(pattern=rf'(\d|{num_words_pattern})\s*{keyword}', string=lower_title)
    #             if num_floor:
    #                 print(f'Extracted floor in title: {num_floor.group(1)}')
    #                 print(f'Additional value: {add_key}')
    #                 if num_floor.group(1).isdigit():
    #                     possible_float = re.search(pattern=rf'(\d+[.,]\d+)\s*{keyword}', string=lower_title)
    #                     if possible_float:
    #                         print(f'Found possible float: {possible_float.group(1)}')
    #                         return float(possible_float.group(1).replace(',','.')) + add_key, 'title'
    #                     return int(num_floor.group(1)) + add_key, 'title'
    #                 return word_to_num[num_floor.group(1)] + add_key, 'title'
    #                 # elif num_floor.group(1) in word_to_num.keys():
    #                 #     index_needed.append(row['index'])
    #                 #     return word_to_num[num_floor.group(1)] + add_key
    if pd.notna(row['description']):
        # add_key = check_additional_floor(lower_des)
        # Trong trường hợp nêu rõ tầng 1, tầng 2,... thì max sẽ là tổng số tầng
        total_pattern = re.findall(pattern=r'(?:tầng|lầu|tấm|mê)\s* ([\d\w]+):', string=lower_des)
        if total_pattern:
            total_floor_num = []
            for digit in total_pattern:
                if is_float(digit):
                    total_floor_num.append(abs(float(digit)))
                elif digit in word_to_num.keys():
                    total_floor_num.append(word_to_num[digit])
            if total_floor_num:
                return max(total_floor_num)
    #------TH4: Xét số tầng mà có miêu tả cấu trúc cụ thể (Kiểu như trệt 2 lầu)------
        else:
            extract_result = extract_separate(lower_des, floor_keywords)
            if extract_result:
                return extract_result
            else:
                extract_result = extract_separate(lower_des, ['trệt', 'trêt', 'tret'])
                if extract_result:
                    return extract_result  
                extract_result = extract_separate(lower_title, ['trệt', 'trêt', 'tret'])     
                if extract_result:
                    return extract_result       
    # if pd.notna(row['description']):
    #     extract_result = extract_separate(lower_des)
    #     if extract_result:
    #         return extract_result, 'description'
    # if pd.notna(row['title']):
    #     extract_result = extract_separate(lower_title)
    #     if extract_result:
    #         return extract_result, 'title'
        # # Trong trường hợp liệt kê ra cả lố tầng thì là cộng tổng vào
        # separate_pattern = re.search(pattern=rf'(\d|{num_words_pattern})\s*(?:tầng|lầu|tấm|mê)', string=lower_des)
        # if separate_pattern:
        #     print(f'Extracted floor that needs to be sum up: {separate_pattern.group(1)}')
        #     print(f'Additional value: {add_key}')
        #     if separate_pattern.group(1).isdigit():
        #         possible_float = re.search(pattern=rf'(\d+[.,]\d+)\s*(?:tầng|lầu|tấm|mê)', string=lower_des)
        #         if possible_float:
        #             print(f'Found possible float: {possible_float.group(1)}')
        #             return float(possible_float.group(1).replace(',','.')) + add_key, 'description'
        #         return int(separate_pattern.group(1)) + add_key, 'description'
        #     return word_to_num[separate_pattern.group(1)] + add_key, 'description'
    return 1
    # elif row['description'] is not None:
    #     lower_des = row['description'].lower()
    #     old_house = re.search(pattern=rf'nhà [\w+\s]{0-5}cũ', string=lower_des)
    #     if old_house:
    #         return 0
    #     cap4 = re.search(pattern = r'nhà cấp 4|nhà c4|cấp 4|nc4|nhà trệt', string=lower_des)
    #     if cap4:
    #         return 1
        
    #     add_key = check_additional_floor(lower_des)

df['index'] = df.index
df['Số tầng công trình'] = df.apply(clean_num_floor, axis = 1, result_type='expand')

In [ ]:
# Code không có hiện trạng
import re
import numpy as np
from rapidfuzz import fuzz

# def check_additional_floor(value):
#     additional_floor = ['sân thượng', 'sân thương', ' st ', 'trệt', 'trêt', 'tret', 'tum', 'hầm', 'hâm', 'gác lửng', 'gác mái', 'lửng', 'lững', 'lừng']
#     result = 0
#     for word in additional_floor:
#         if word in value:
#         # tokens = value.split()
#         # for token in tokens:
#         #     if fuzz.ratio(token, word) > 70:
#             if word == 'sân thượng' or word == 'sân thương':
#                 additional_floor.remove(' st ')
#             if word == ' st ':
#                 additional_floor.remove('sân thượng')
#             print(f'Additional Floor word detected: {word}')
#             result += 1
#     return result

def new_check_additional_floor(string, additional_floor):
    result = 0
    for word in additional_floor:
        if word in string:
            result += 1
    search_st = re.search(pattern=r'(\Wst\W)', string=string)
    if search_st:
        result += 1
    search_gl = re.search(pattern=r'gác lửng|gác lững|ghác lửng|ghác lững', string=string)
    if search_gl:
        result -= 1
    return result 

def is_float(num):
    try:
        float(num)
        return True
    except:
        return False

def extract_separate(lower_value, floor_keywords):
    value_list = lower_value.split()
    forbidden_pattern = r'giấy phép xây dựng|giấy phép xây|phép xây dựng|gpxd|có thể xây|cải tạo|được phép xây'
    additional_floor = ['sân thượng', 'sân thương', 'trêt', 'trệt', 'tret', 'tum', 'hầm', 'hâm', 'gác', 'gac', 'lửng', 'lững', 'lừng']
    if 'trệt' in floor_keywords:
        additional_floor = ['sân thượng', 'sân thương',  'tum', 'hầm', 'hâm', 'gác', 'gac', 'lửng', 'lững', 'lừng']
    word_to_num = {
            "một": 1, "hai": 2, "ba": 3, "bốn": 4, "năm": 5, "sáu": 6,
            "bảy": 7, "bẩy": 7, "tám": 8, "chín": 9, "mười": 10,
            "mười một": 11, "mười hai": 12, "mười ba": 13, "mười bốn": 14,
            "mười lăm": 15, "mười sáu": 16
        }
    for keyword in floor_keywords: # Check cho từng chiếc keyword
        if keyword in lower_value: # Nếu trong string có một trong những chiếc keyword
            i = 0
            while i < len(value_list):
                # for value in value_list: # Tìm trong list string mà đã được tách ra sẵn
            #     if keyword in value: # Nếu chiếc keyword đã tìm thấy ban nãy là của từ này
                    # word_index = value_list.index(value) # Lấy index của từ
                if keyword in value_list[i]: # Tìm index của chiếc từ keyword floor 
                    # Trong trường hợp mà nó bị dính chữ vào với nhau
                    extracted_floor = value_list[i].replace(keyword, '').replace(',','.')
                    if is_float(extracted_floor) or (extracted_floor in word_to_num.keys()): 
                        word_lower = i - 4 if i - 4 >= 0 else 0
                        word_upper = i + 4 if i + 4 < len(value_list) else len(value_list) - 1
                        search_range = ' '.join(value_list[word_lower:word_upper + 1]) # Tìm trong khoảng 5 từ trước - sau của từ
                        forbidden_word = re.search(pattern=forbidden_pattern, string=search_range)
                        if forbidden_word: # Nếu xuất hiện forbidden word
                            i += 1
                        else:
                            # if 'hiện trạng' in ' '.join(value_list[word_lower:i]): # Nếu hiện trạng 3 tầng --> return luôn
                            #     if is_float(extracted_floor):
                            #         return abs(float(extracted_floor))
                            #     if extracted_floor in word_to_num.keys():
                            #         return word_to_num[extracted_floor]
                            # else:
                            if is_float(extracted_floor) or (extracted_floor in word_to_num.keys()):
                                add_key = new_check_additional_floor(search_range, additional_floor)
                                if is_float(extracted_floor):
                                    return abs(float(extracted_floor)) + add_key
                                return word_to_num[extracted_floor] + add_key
                            else:
                                add_key = new_check_additional_floor(search_range, additional_floor)
                                if add_key > 0:
                                    return add_key + 1
                                else:
                                    i += 1
                    # Nếu có thể extract vị trí ở đằng trước keyword đã cho
                    elif i - 1 >= 0:
                        extracted_floor = value_list[i - 1].replace(',', '.')
                        word_lower = i - 4 if i - 4 >= 0 else 0
                        word_upper = i + 4 if i + 4 < len(value_list) else len(value_list) - 1
                        search_range = ' '.join(value_list[word_lower:word_upper + 1]) # Tìm trong khoảng 5 từ trước - sau của từ
                        forbidden_word = re.search(pattern=forbidden_pattern, string=search_range)
                        if forbidden_word: # Nếu xuất hiện forbidden word
                            i += 1
                        else:
                            # if 'hiện trạng' in ' '.join(value_list[word_lower:i]): # Nếu hiện trạng 3 tầng --> return luôn
                            #     if is_float(extracted_floor):
                            #         return abs(float(extracted_floor))
                            #     elif extracted_floor in word_to_num.keys():
                            #         return word_to_num[extracted_floor]
                            #     else:
                            #         i += 1
                            # else:
                            if is_float(extracted_floor) or (extracted_floor in word_to_num.keys()):
                                add_key = new_check_additional_floor(search_range, additional_floor)
                                if is_float(extracted_floor):
                                    return abs(float(extracted_floor)) + add_key
                                return word_to_num[extracted_floor] + add_key
                            else:
                                add_key = new_check_additional_floor(search_range, additional_floor)
                                if add_key > 0:
                                    return add_key + 1
                                else:
                                    i += 1
                    else:
                        i += 1
                else:
                    i += 1
    
    return None


def clean_num_floor(row):
    floor_keywords = ['tầng', 'lầu', 'tấm', 'mê']
    word_to_num = {
            "một": 1, "hai": 2, "ba": 3, "bốn": 4, "năm": 5, "sáu": 6,
            "bảy": 7, "bẩy": 7, "tám": 8, "chín": 9, "mười": 10,
            "mười một": 11, "mười hai": 12, "mười ba": 13, "mười bốn": 14,
            "mười lăm": 15, "mười sáu": 16
        }
    # ------- TH1: Thông tin đã có sẵn ở other_info ------
    if row['other_info'] != {} and row['other_info'].get('Số tầng'):
        return int(row['other_info'].get('Số tầng').split()[0])
    # ------ TH2: Nhà cũ/nhà cấp 4 ở title/description ------
    # Xét của description trước do description thường được viết đầy đủ hơn
    if pd.notna(row['description']):
        lower_des = row['description'].lower().replace('+', ' ').replace('x',' ').replace('*', ' ')
        old_house = re.search(pattern=r'nhà (?:\w+\s*){0,5}cũ|bán(?:\s+\S\s*){0,5}đất', string=lower_des)
        if old_house:
            return 0
        cap4 = re.search(pattern = r'nhà cấp 4|nhà c4|cấp 4|nc4|nhà trệt|nhà nát', string=lower_des)
        if cap4:
            if cap4.group(0) == 'nhà trệt':
                extract_result = extract_separate(lower_des, floor_keywords)
                if extract_result:
                    return extract_result
            return 1
    if pd.notna(row['title']):
        lower_title = row['title'].lower().replace('+', ' ').replace('x',' ').replace('*', ' ')
        old_house = re.search(pattern=r'nhà (?:\w+\s*){0,5}cũ|bán(?:\s+\S\s*){0,5}đất', string=lower_title)
        if old_house:
            return 0
        cap4 = re.search(pattern = r'nhà cấp 4|nhà c4|cấp 4|nc4|nhà trệt|nhà nát', string=lower_title)
        if cap4:
            if cap4.group(0) == 'nhà trệt':
                extract_result = extract_separate(lower_title, floor_keywords)
                if extract_result:
                    return extract_result
            return 1
    # ------ TH3: Xét tổng số tầng ------
        extract_result = extract_separate(lower_title, floor_keywords)
        if extract_result:
            return extract_result
    # Có lẽ với trường hợp này, nếu có add_key thì skip xuống extract description cho đủ, nếu description không na hoặc kệ luôn
    # if pd.notna(row['title']):
    #     add_key = check_additional_floor(lower_title)
    #     for keyword in floor_keywords:
    #         if keyword in lower_title:
    #             num_floor = re.search(pattern=rf'(\d|{num_words_pattern})\s*{keyword}', string=lower_title)
    #             if num_floor:
    #                 print(f'Extracted floor in title: {num_floor.group(1)}')
    #                 print(f'Additional value: {add_key}')
    #                 if num_floor.group(1).isdigit():
    #                     possible_float = re.search(pattern=rf'(\d+[.,]\d+)\s*{keyword}', string=lower_title)
    #                     if possible_float:
    #                         print(f'Found possible float: {possible_float.group(1)}')
    #                         return float(possible_float.group(1).replace(',','.')) + add_key, 'title'
    #                     return int(num_floor.group(1)) + add_key, 'title'
    #                 return word_to_num[num_floor.group(1)] + add_key, 'title'
    #                 # elif num_floor.group(1) in word_to_num.keys():
    #                 #     index_needed.append(row['index'])
    #                 #     return word_to_num[num_floor.group(1)] + add_key
    if pd.notna(row['description']):
        # add_key = check_additional_floor(lower_des)
        # Trong trường hợp nêu rõ tầng 1, tầng 2,... thì max sẽ là tổng số tầng
        total_pattern = re.findall(pattern=r'(?:tầng|lầu|tấm|mê)\s* ([\d\w]+):', string=lower_des)
        if total_pattern:
            total_floor_num = []
            for digit in total_pattern:
                if is_float(digit):
                    total_floor_num.append(abs(float(digit)))
                elif digit in word_to_num.keys():
                    total_floor_num.append(word_to_num[digit])
            if total_floor_num:
                return max(total_floor_num)
    #------TH4: Xét số tầng mà có miêu tả cấu trúc cụ thể (Kiểu như trệt 2 lầu)------
        else:
            extract_result = extract_separate(lower_des, floor_keywords)
            if extract_result:
                return extract_result
            else:
                extract_result = extract_separate(lower_des, ['trệt', 'trêt', 'tret'])
                if extract_result:
                    return extract_result  
                extract_result = extract_separate(lower_title, ['trệt', 'trêt', 'tret'])     
                if extract_result:
                    return extract_result       
    # if pd.notna(row['description']):
    #     extract_result = extract_separate(lower_des)
    #     if extract_result:
    #         return extract_result, 'description'
    # if pd.notna(row['title']):
    #     extract_result = extract_separate(lower_title)
    #     if extract_result:
    #         return extract_result, 'title'
        # # Trong trường hợp liệt kê ra cả lố tầng thì là cộng tổng vào
        # separate_pattern = re.search(pattern=rf'(\d|{num_words_pattern})\s*(?:tầng|lầu|tấm|mê)', string=lower_des)
        # if separate_pattern:
        #     print(f'Extracted floor that needs to be sum up: {separate_pattern.group(1)}')
        #     print(f'Additional value: {add_key}')
        #     if separate_pattern.group(1).isdigit():
        #         possible_float = re.search(pattern=rf'(\d+[.,]\d+)\s*(?:tầng|lầu|tấm|mê)', string=lower_des)
        #         if possible_float:
        #             print(f'Found possible float: {possible_float.group(1)}')
        #             return float(possible_float.group(1).replace(',','.')) + add_key, 'description'
        #         return int(separate_pattern.group(1)) + add_key, 'description'
        #     return word_to_num[separate_pattern.group(1)] + add_key, 'description'
    return 1
    # elif row['description'] is not None:
    #     lower_des = row['description'].lower()
    #     old_house = re.search(pattern=rf'nhà [\w+\s]{0-5}cũ', string=lower_des)
    #     if old_house:
    #         return 0
    #     cap4 = re.search(pattern = r'nhà cấp 4|nhà c4|cấp 4|nc4|nhà trệt', string=lower_des)
    #     if cap4:
    #         return 1
        
    #     add_key = check_additional_floor(lower_des)

df['index'] = df.index
df['New Số tầng công trình'] = df.apply(clean_num_floor, axis = 1, result_type='expand')

In [ ]:
string = 'kết cấu tòa nhà: trệt 3 lầu sân thượng thoáng đãng'
pattern = r'(?:\S+\s+){0,5}(\d+(?:[.,]\d+)*|\w+)\s*lầu (?:\S+\s+){0,5}'
yes = re.search(pattern, string)
if yes:
    print(yes.group(1))

3


## New Code using Regex

In [ ]:
# TRY NEW ONE
import re
import numpy as np
from rapidfuzz import fuzz

def new_check_additional_floor(string):
    additional_floor = ['sân thượng', 'sân thương',  'tum', 'hầm', 'hâm', 'gác', 'gac', 'lửng', 'lững', 'lừng']
    result = 0
    for word in additional_floor:
        if word in string:
            result += 1
    search_st = re.search(pattern=r'(\Wst\W)', string=string)
    if search_st:
        result += 1
    search_tret = re.search(pattern=r'(?:trệt|trêt|tret)\s*(?:\S+\s+){0,3}(?:tầng|lầu|tấm|mê)', string=string)
    if search_tret:
        result += 1
    search_gl = re.search(pattern=r'gác lửng|gác lững|ghác lửng|ghác lững', string=string)
    if search_gl:
        result -= 1
    return result 

def is_float(num):
    try:
        float(num)
        return True
    except:
        return False
    
def extract_separate(lower_value, floor_keywords):
    # value_list = lower_value.split()
    forbidden_pattern = 'giấy phép xây dựng|giấy phép xây|phép xây dựng|gpxd|có thể xây|cải tạo|được phép xây'
    # additional_floor = ['sân thượng', 'sân thương', 'trêt', 'trệt', 'tret', 'tum', 'hầm', 'hâm', 'gác', 'gac', 'lửng', 'lững', 'lừng']
    # if 'trệt' in floor_keywords:
    
    word_to_num = {
            "một": 1, "hai": 2, "ba": 3, "bốn": 4, "năm": 5, "sáu": 6,
            "bảy": 7, "bẩy": 7, "tám": 8, "chín": 9, "mười": 10,
            "mười một": 11, "mười hai": 12, "mười ba": 13, "mười bốn": 14,
            "mười lăm": 15, "mười sáu": 16
        }
    floor_key = '|'.join(key for key in floor_keywords)
    found_floor_key = re.findall(rf'{floor_key}', lower_value)
    for key in found_floor_key:
        forbidden_word = re.search(rf'{forbidden_pattern}\s*(?:\S+\s*){{0,2}}{key}', lower_value)
        if forbidden_word:
            continue
        extracted_floor = re.search(rf'(?:\S+\s*){{0,5}}(\d+(?:[.,]\d+)*|\w+)\s*{key}\s*(?:\S+\s*){{0,5}}', lower_value)
        if extracted_floor:
            extracted_floor_num = extracted_floor.group(1).replace(',', '.')
            add_key = new_check_additional_floor(extracted_floor.group(0))
            if is_float(extracted_floor_num) or (extracted_floor_num in word_to_num.keys()):
                if is_float(extracted_floor_num):
                    return abs(float(extracted_floor_num)) + add_key
                return word_to_num[extracted_floor_num] + add_key
            else:
                if add_key > 0:
                    return add_key + 1 # Nếu trường hợp trệt lầu sân thượng thì phải cộng 1 cho cái lầu nữa
    return None
    
def new_clean_num_floor(row):
    floor_keywords = ['tầng', 'lầu', 'tấm', 'mê']
    word_to_num = {
            "một": 1, "hai": 2, "ba": 3, "bốn": 4, "năm": 5, "sáu": 6,
            "bảy": 7, "bẩy": 7, "tám": 8, "chín": 9, "mười": 10,
            "mười một": 11, "mười hai": 12, "mười ba": 13, "mười bốn": 14,
            "mười lăm": 15, "mười sáu": 16
        }
    # ------- TH1: Thông tin đã có sẵn ở other_info ------
    if row['other_info'] != {} and row['other_info'].get('Số tầng'):
        return int(row['other_info'].get('Số tầng').split()[0])
    # ------ TH2: Nhà cũ/nhà cấp 4 ở title/description ------
    # Xét của description trước do description thường được viết đầy đủ hơn
    if pd.notna(row['description']):
        lower_des = row['description'].lower().replace('+', ' ').replace('x',' ').replace('*', ' ')
        old_house = re.search(pattern=r'nhà (?:\w+\s*){0,5}cũ|bán(?:\s+\S\s*){0,5}đất', string=lower_des)
        if old_house:
            return 0
        cap4 = re.search(pattern = r'nhà cấp 4|nhà c4|cấp 4|nc4|nhà trệt|nhà nát', string=lower_des)
        if cap4:
            if cap4.group(0) == 'nhà trệt':
                extract_result = extract_separate(lower_des, floor_keywords)
                if extract_result:
                    return extract_result
            return 1
    if pd.notna(row['title']):
        lower_title = row['title'].lower().replace('+', ' ').replace('x',' ').replace('*', ' ')
        old_house = re.search(pattern=r'nhà (?:\w+\s*){0,5}cũ|bán(?:\s+\S\s*){0,5}đất', string=lower_title)
        if old_house:
            return 0
        cap4 = re.search(pattern = r'nhà cấp 4|nhà c4|cấp 4|nc4|nhà trệt|nhà nát', string=lower_title)
        if cap4:
            if cap4.group(0) == 'nhà trệt':
                extract_result = extract_separate(lower_des, floor_keywords)
                if extract_result:
                    return extract_result
            return 1
    # ------ TH3: Xét tổng số tầng ------
        extract_result = extract_separate(lower_title, floor_keywords)
        if extract_result:
            return extract_result
    if pd.notna(row['description']):
        total_pattern = re.findall(pattern=r'(?:tầng|lầu|tấm|mê)\s* ([\d\w]+):', string=lower_des)
        if total_pattern:
            total_floor_num = []
            for digit in total_pattern:
                if is_float(digit):
                    total_floor_num.append(abs(float(digit)))
                elif digit in word_to_num.keys():
                    total_floor_num.append(word_to_num[digit])
            if total_floor_num:
                return max(total_floor_num)
    #------TH4: Xét số tầng mà có miêu tả cấu trúc cụ thể (Kiểu như trệt 2 lầu)------
        else:
            extract_result = extract_separate(lower_des, floor_keywords)
            if extract_result:
                return extract_result
            else:
                extract_result = extract_separate(lower_des, ['trệt', 'trêt', 'tret'])
                if extract_result:
                    return extract_result  
                extract_result = extract_separate(lower_title, ['trệt', 'trêt', 'tret'])     
                if extract_result:
                    return extract_result       
    return 1

df['New Số tầng công trình'] = df.apply(new_clean_num_floor, axis = 1)
            

Sai
- 64: Scrape từ 5 thành 1
- 452: 1 trệt 1 gác (scrape từ 2 thành 1)
- 1487: trệt+lửng mà scrape thành 1
- 2122: 1 Trêt + 3lầu mà scrape thành 3
- 2294: trệt lửng (scrape thành 1)
- 3658: 1trệt 2lầu (scrape thành 2)
- 3670: 1 trệt 1 lửng (scrape thành 1)
- 3768: 1 trệt, 1 gác lửng (scrape thành 1)
- 3923: Trệt - Lầu (scrape thành 1)
- 6412:  trệt lửng (scrape thành 1)
- 6521: DT: 51m2_3tầng (scrape thành 1)
- 6562: Chính chủ muốn bán căn hộ tầng 2 trên khối nhà Pháp cổ 2 tầng (scrape thành 1)
- 6583: kết cấu 1 trệt, lầu, 1 lửng (scrape thành 1)
- 68431: 1 trệt 1 lầu (scrape thành 1)

Đúng
- 148: Scrape 8 thành 9
- 356: scrape từ 2 (chả hiểu lấy đâu ra) thành 1
- 2224: Phù hợp xây cao tầng 6,7 tầng (scrape thành 1)
- 5212: Kết cấu 4 tầng gồm 1 trệt , 2 lầu , sân thượng (scrape từ 5 thành 4)

In [ ]:
pd.set_option('display.max_colwidth', None)
pd.set_option('display.max_rows', None)

df[df['Số tầng công trình'] != df['New Số tầng công trình']][['description', 'title', 'other_info', 'Số tầng công trình', 'New Số tầng công trình']]

description  \
64                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                       Bán CHDV 12 phòng full nội thất gần Hiệp Thành City Quận 12, giá 9.5 tỷ tl\n\n-DT: 5x20m full thổ, hẻm 7m thông\n- 1 hầm 1 trệt 3 lầu có thang máy\n-Tổng 12 phòng full nội thất đều có bancol và máy giặt riêng.\n-Thang máy lên tới tầng thượng. Có thể cải tạo thêm 3 phòng nữa, đã chừa đường nước và điện\n-Trang bị đầy đủ hệ thống PCCC, thang máy, wifi, camera, cửa cuốn ...\n\nGiá bán: 9.5 tỷ có thương lượng   
148                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            + Bán Nhà Phân Lô Phố Ngọc Thụy , Khu Vip Nhà Giàu , Kinh Doanh Mọi ngành nghề\n+ Thiết kế 70m² * 8 Tầng Thang máy Kinh Doanh + Pen House , Nhà có Hầm để 4 Xe Oto Tiện lợi , Mặt Phố Phân Lô Rộng 12M Vỉa hè Thông Thoáng Nhộn Nhịp\n+ Sổ Đỏ Phân Lô Vuông Đẹp , Nhà Cho Thuê Dòng Tiền Lớn , Giá Có Thương Lượng   
356                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                    

In [ ]:
# import re
# import numpy as np
# from rapidfuzz import fuzz

# def check_additional_floor(value):
#     additional_floor = ['sân thượng', 'sân thương', ' st ', 'trệt', 'trêt', 'tret', 'tum', 'hầm', 'hâm', 'gác lửng', 'gác mái', 'lửng', 'lững', 'lừng']
#     result = 0
#     for word in additional_floor:
#         if word in value:
#         # tokens = value.split()
#         # for token in tokens:
#         #     if fuzz.ratio(token, word) > 70:
#             if word == 'sân thượng' or word == 'sân thương':
#                 additional_floor.remove(' st ')
#             if word == ' st ':
#                 additional_floor.remove('sân thượng')
#             print(f'Additional Floor word detected: {word}')
#             result += 1
#     return result

# def new_check_additional_floor(string, additional_floor):
#     print(f'Search string: {string}')
#     result = 0
#     for word in additional_floor:
#         if word in string:
#             result += 1
#     search_st = re.search(pattern=r'(\Wst\W)', string=string)
#     if search_st:
#         result += 1
#     return result 

# def is_float(num):
#     try:
#         float(num)
#         return True
#     except:
#         return False

# def extract_separate(lower_value, floor_keywords):
#     value_list = lower_value.split()
#     forbidden_pattern = r'giấy phép xây dựng|giấy phép xây|phép xây dựng|gpxd|có thể xây|cải tạo|được phép xây'
#     additional_floor = ['sân thượng', 'sân thương', 'trêt', 'trệt', 'tret', 'tum', 'hầm', 'hâm', 'gác mái', 'lửng', 'lững', 'lừng']
#     if 'trệt' in floor_keywords:
#         additional_floor = ['sân thượng', 'sân thương',  'tum', 'hầm', 'hâm', 'gác mái', 'lửng', 'lững', 'lừng']
#     word_to_num = {
#             "một": 1, "hai": 2, "ba": 3, "bốn": 4, "năm": 5, "sáu": 6,
#             "bảy": 7, "bẩy": 7, "tám": 8, "chín": 9, "mười": 10,
#             "mười một": 11, "mười hai": 12, "mười ba": 13, "mười bốn": 14,
#             "mười lăm": 15, "mười sáu": 16
#         }
#     for keyword in floor_keywords: # Check cho từng chiếc keyword
#         if keyword in lower_value: # Nếu trong string có một trong những chiếc keyword
#             i = 0
#             while i < len(value_list):
#                 print(f"Index {i} for keyword: {keyword}")
#                 print(f'Word: {value_list[i]}')
#                 # for value in value_list: # Tìm trong list string mà đã được tách ra sẵn
#             #     if keyword in value: # Nếu chiếc keyword đã tìm thấy ban nãy là của từ này
#                     # word_index = value_list.index(value) # Lấy index của từ
#                 if keyword in value_list[i]: # Tìm index của chiếc từ keyword floor 
#                     # Trong trường hợp mà nó bị dính chữ vào với nhau
#                     if value_list[i].endswith(keyword):
#                         print(value_list[i])
#                         extracted_floor = value_list[i].replace(keyword, '').replace(',','.')
#                         if is_float(extracted_floor) or (extracted_floor in word_to_num.keys()): 
#                             word_lower = i - 4 if i - 4 >= 0 else 0
#                             word_upper = i + 4 if i + 4 < len(value_list) else len(value_list) - 1
#                             search_range = ' '.join(value_list[word_lower:word_upper + 1]) # Tìm trong khoảng 5 từ trước - sau của từ
#                             forbidden_word = re.search(pattern=forbidden_pattern, string=search_range)
#                             if forbidden_word: # Nếu xuất hiện forbidden word
#                                 i += 1
#                                 continue
#                             else:
#                                 if 'hiện trạng' in ' '.join(value_list[word_lower:i]): # Nếu hiện trạng 3 tầng --> return luôn
#                                     if is_float(extracted_floor):
#                                         print(f'Extracted value: {abs(float(extracted_floor))}')
#                                         return abs(float(extracted_floor))
#                                     if extracted_floor in word_to_num.keys():
#                                         print(f'Extracted value: {word_to_num[extracted_floor]}')
#                                         return word_to_num[extracted_floor]
#                                 else:
#                                     if is_float(extracted_floor) or (extracted_floor in word_to_num.keys()):
#                                         print(f'Extracted Floor: {extracted_floor}')
#                                         add_key = new_check_additional_floor(search_range, additional_floor)
#                                         if is_float(extracted_floor):
#                                             print(f'Extracted value with add key: {abs(float(extracted_floor)) + add_key}')
#                                             return abs(float(extracted_floor)) + add_key
#                                         print(f'Extracted Floor: {extracted_floor}')
#                                         print(f'Extracted value with add key: {word_to_num[extracted_floor] + add_key}')
#                                         return word_to_num[extracted_floor] + add_key
#                                     else:
#                                         add_key = new_check_additional_floor(search_range, additional_floor)
#                                         if add_key > 0:
#                                             print(f'Extracted value using add key only: {add_key + 1}')
#                                             return add_key + 1
#                     else:
#                         # Nếu có thể extract vị trí ở đằng trước keyword đã cho
#                         if i - 1 >= 0:
#                             extracted_floor = value_list[i - 1].replace(',', '.')
#                             word_lower = i - 4 if i - 4 >= 0 else 0
#                             word_upper = i + 4 if i + 4 < len(value_list) else len(value_list) - 1
#                             search_range = ' '.join(value_list[word_lower:word_upper + 1]) # Tìm trong khoảng 5 từ trước - sau của từ
#                             forbidden_word = re.search(pattern=forbidden_pattern, string=search_range)
#                             if forbidden_word: # Nếu xuất hiện forbidden word
#                                 i += 1
#                                 continue
#                             else:
#                                 if 'hiện trạng' in ' '.join(value_list[word_lower:i]): # Nếu hiện trạng 3 tầng --> return luôn
#                                     if is_float(extracted_floor):
#                                         print(f'Extracted value: {abs(float(extracted_floor))}')
#                                         return abs(float(extracted_floor))
#                                     elif extracted_floor in word_to_num.keys():
#                                         print(f'Extracted value: {word_to_num[extracted_floor]}')
#                                         return word_to_num[extracted_floor]
#                                     # else:
#                                     #     i += 1
#                                 else:
#                                     if is_float(extracted_floor) or (extracted_floor in word_to_num.keys()):
#                                         add_key = new_check_additional_floor(search_range, additional_floor)
#                                         if is_float(extracted_floor):
#                                             print(f'Extracted value with add key: {abs(float(extracted_floor)) + add_key}')
#                                             return abs(float(extracted_floor)) + add_key
#                                         print(f'Extracted value with add key: {word_to_num[extracted_floor] + add_key}')
#                                         return word_to_num[extracted_floor] + add_key
#                                     else:
#                                         add_key = new_check_additional_floor(search_range, additional_floor)
#                                         if add_key > 0:
#                                             return add_key + 1
#                                         # else:
#                                         #     i += 1
#                         # else:
#                         #     i += 1
#                 # else:
#                 #     i += 1
#                 i += 1
    
#     return None


# def clean_num_floor(row):
#     print(f'Cleaning for row {row["index"]}')
#     floor_keywords = ['tầng', 'lầu', 'tấm', 'mê']
#     word_to_num = {
#             "một": 1, "hai": 2, "ba": 3, "bốn": 4, "năm": 5, "sáu": 6,
#             "bảy": 7, "bẩy": 7, "tám": 8, "chín": 9, "mười": 10,
#             "mười một": 11, "mười hai": 12, "mười ba": 13, "mười bốn": 14,
#             "mười lăm": 15, "mười sáu": 16
#         }
#     # ------- TH1: Thông tin đã có sẵn ở other_info ------
#     if row['other_info'] != {} and row['other_info'].get('Số tầng'):
#         return int(row['other_info'].get('Số tầng').split()[0]), 'other_info'
#     # ------ TH2: Nhà cũ/nhà cấp 4 ở title/description ------
#     # Xét của description trước do description thường được viết đầy đủ hơn
#     if pd.notna(row['description']):
#         lower_des = row['description'].lower().replace('+', ' ').replace('x',' ').replace('*', ' ')
#         old_house = re.search(pattern=r'nhà (?:\w+\s*){0,5}cũ', string=lower_des)
#         if old_house:
#             return 0, 'description'
#         cap4 = re.search(pattern = r'nhà cấp 4|nhà c4|cấp 4|nc4|nhà trệt', string=lower_des)
#         if cap4:
#             if cap4.group(0) == 'nhà trệt':
#                 extract_result = extract_separate(lower_des, floor_keywords)
#                 if extract_result:
#                     return extract_result, 'description'
#             return 1, 'description'
#     if pd.notna(row['title']):
#         lower_title = row['title'].lower().replace('+', ' ').replace('x',' ').replace('*', ' ')
#         old_house = re.search(pattern=r'nhà (?:\w+\s*){0,5}cũ', string=lower_title)
#         if old_house:
#             return 0, 'title'
#         cap4 = re.search(pattern = r'nhà cấp 4|nhà c4|cấp 4|nc4|nhà trệt', string=lower_title)
#         if cap4:
#             if cap4.group(0) == 'nhà trệt':
#                 extract_result = extract_separate(lower_title, floor_keywords)
#                 if extract_result:
#                     return extract_result, 'title'
#             return 1, 'title'
#     # ------ TH3: Xét tổng số tầng ------
#         extract_result = extract_separate(lower_title, floor_keywords)
#         if extract_result:
#             return extract_result, 'title'
#     # Có lẽ với trường hợp này, nếu có add_key thì skip xuống extract description cho đủ, nếu description không na hoặc kệ luôn
#     # if pd.notna(row['title']):
#     #     add_key = check_additional_floor(lower_title)
#     #     for keyword in floor_keywords:
#     #         if keyword in lower_title:
#     #             num_floor = re.search(pattern=rf'(\d|{num_words_pattern})\s*{keyword}', string=lower_title)
#     #             if num_floor:
#     #                 print(f'Extracted floor in title: {num_floor.group(1)}')
#     #                 print(f'Additional value: {add_key}')
#     #                 if num_floor.group(1).isdigit():
#     #                     possible_float = re.search(pattern=rf'(\d+[.,]\d+)\s*{keyword}', string=lower_title)
#     #                     if possible_float:
#     #                         print(f'Found possible float: {possible_float.group(1)}')
#     #                         return float(possible_float.group(1).replace(',','.')) + add_key, 'title'
#     #                     return int(num_floor.group(1)) + add_key, 'title'
#     #                 return word_to_num[num_floor.group(1)] + add_key, 'title'
#     #                 # elif num_floor.group(1) in word_to_num.keys():
#     #                 #     index_needed.append(row['index'])
#     #                 #     return word_to_num[num_floor.group(1)] + add_key
#     if pd.notna(row['description']):
#         # add_key = check_additional_floor(lower_des)
#         # Trong trường hợp nêu rõ tầng 1, tầng 2,... thì max sẽ là tổng số tầng
#         total_pattern = re.findall(pattern=r'(?:tầng|lầu|tấm|mê)\s* ([\d\w]+):', string=lower_des)
#         if total_pattern:
#             print(f"Extracted total floor in description: {total_pattern}")
#             total_floor_num = []
#             for digit in total_pattern:
#                 if is_float(digit):
#                     total_floor_num.append(abs(float(digit)))
#                 elif digit in word_to_num.keys():
#                     total_floor_num.append(word_to_num[digit])
#             if total_floor_num:
#                 return max(total_floor_num), 'description'
#     #------TH4: Xét số tầng mà có miêu tả cấu trúc cụ thể (Kiểu như trệt 2 lầu)------
#         else:
#             extract_result = extract_separate(lower_des, floor_keywords)
#             if extract_result:
#                 return extract_result, 'description'
#             else:
#                 extract_result = extract_separate(lower_des, ['trệt', 'trêt', 'tret'])
#                 if extract_result:
#                     return extract_result, 'description trệt'   
#                 extract_result = extract_separate(lower_title, ['trệt', 'trêt', 'tret'])     
#                 if extract_result:
#                     return extract_result, 'title trệt'        
#     # if pd.notna(row['description']):
#     #     extract_result = extract_separate(lower_des)
#     #     if extract_result:
#     #         return extract_result, 'description'
#     # if pd.notna(row['title']):
#     #     extract_result = extract_separate(lower_title)
#     #     if extract_result:
#     #         return extract_result, 'title'
#         # # Trong trường hợp liệt kê ra cả lố tầng thì là cộng tổng vào
#         # separate_pattern = re.search(pattern=rf'(\d|{num_words_pattern})\s*(?:tầng|lầu|tấm|mê)', string=lower_des)
#         # if separate_pattern:
#         #     print(f'Extracted floor that needs to be sum up: {separate_pattern.group(1)}')
#         #     print(f'Additional value: {add_key}')
#         #     if separate_pattern.group(1).isdigit():
#         #         possible_float = re.search(pattern=rf'(\d+[.,]\d+)\s*(?:tầng|lầu|tấm|mê)', string=lower_des)
#         #         if possible_float:
#         #             print(f'Found possible float: {possible_float.group(1)}')
#         #             return float(possible_float.group(1).replace(',','.')) + add_key, 'description'
#         #         return int(separate_pattern.group(1)) + add_key, 'description'
#         #     return word_to_num[separate_pattern.group(1)] + add_key, 'description'
#     return 1, 'NaN values'
#     # elif row['description'] is not None:
#     #     lower_des = row['description'].lower()
#     #     old_house = re.search(pattern=rf'nhà [\w+\s]{0-5}cũ', string=lower_des)
#     #     if old_house:
#     #         return 0
#     #     cap4 = re.search(pattern = r'nhà cấp 4|nhà c4|cấp 4|nc4|nhà trệt', string=lower_des)
#     #     if cap4:
#     #         return 1
        
#     #     add_key = check_additional_floor(lower_des)

# df['index'] = df.index
# df[['floor', 'floor_extracted_from']] = df.apply(clean_num_floor, axis = 1, result_type='expand')

In [ ]:
clean_num_floor(df.iloc[412])

1

In [ ]:
print(f"Title new: {df[df['floor_extracted_from'] == 'title'].shape[0]}")
print(f"Description new: {df[df['floor_extracted_from'] == 'description'].shape[0]}")
print(f"Title trệt new: {df[df['floor_extracted_from'] == 'title trệt'].shape[0]}")
print(f"Description trệt new: {df[df['floor_extracted_from'] == 'description trệt'].shape[0]}")
print(f"NaN values new: {df[df['floor_extracted_from'] == 'NaN values'].shape[0]}")

Title new: 280
Description new: 1112
Title trệt new: 0
Description trệt new: 16
NaN values new: 9376


# Test Shape (Hình dạng)

In [ ]:
import pandas as pd
import json

listing_details = pd.read_csv('output/listing_details.csv')
listing_details.drop(['latitude', 'longitude', 'image_urls', 'description'], axis=1, inplace=True)

listing_details_cleaned = pd.read_csv('output/listing_details_cleaned.csv')
listing_details_cleaned.rename(columns={'Nguồn thông tin': 'url'}, inplace=True)
df = pd.merge(listing_details_cleaned, listing_details, how='left', on='url')

df['other_info'] = df['other_info'].apply(json.loads)
df['main_info'] = df['main_info'].apply(json.loads)

In [ ]:
df['Hình dạng'].value_counts()

Hình dạng
Chữ nhật                     25123
Nở hậu                        2065
Chữ L                           21
Thóp hậu                        10
Tam giác                         8
Chữ T                            5
Chữ U                            3
Đa giác từ 5 cạnh, méo mó        2
Chữ nhật vát góc                 1
Name: count, dtype: int64

In [ ]:
from src.config import NEGATION_PATTERNS, SHAPE_KEYWORDS

def extract_shape(row):
    def is_negated(text: str, kw: str) -> bool:
            for pattern in NEGATION_PATTERNS:
                if re.search(pattern.format(re.escape(kw)), text):
                    return True
            return False

    text = f"{row.get('title', '')} {row.get('description', '')}".lower()

    for shape, kws in SHAPE_KEYWORDS.items():
        for kw in kws:
            if re.search(rf"\b{re.escape(kw)}\b", text) and not is_negated(text, kw):
                return shape, kw

    return "Chữ nhật", 'NaN'

In [ ]:
from src.config import NEGATION_PATTERNS, SHAPE_KEYWORDS
from sentence_transformers import SentenceTransformer, util

# Load embedding model
model = SentenceTransformer("all-MiniLM-L6-v2")

# Precompute embeddings for your keywords
shape_embeddings = {}
for shape, kws in SHAPE_KEYWORDS.items():
    shape_embeddings[shape] = [(kw, model.encode(kw, convert_to_tensor=True)) for kw in kws]

def new_extract_shape(row, threshold=0.7):
    def is_negated(text: str, kw: str) -> bool:
        for pattern in NEGATION_PATTERNS:
            if re.search(pattern.format(re.escape(kw)), text):
                return True
        return False

    text = f"{row.get('title', '')} {row.get('description', '')}".lower()
    words = re.findall(r'\w+', text)

    for word in words:
        word_vec = model.encode(word, convert_to_tensor=True)
        for shape, kw_embs in shape_embeddings.items():
            for kw, kw_vec in kw_embs:
                sim = util.cos_sim(word_vec, kw_vec).item()
                if sim >= threshold and not is_negated(text, kw):
                    return (shape, word)

    return ('Chữ nhật', 'NaN')

In [ ]:
df[['shape', 'shape_keyword']] = df.apply(extract_shape, axis = 1, result_type='expand')

In [ ]:
df[['new_shape', 'new_shape_keyword']] = df.apply(new_extract_shape, axis = 1, result_type='expand')

#  Test Chất lượng còn lại 

In [ ]:
import pandas as pd
import json
import numpy as np

listing_details = pd.read_csv('output/listing_details.csv')
listing_details.drop(['latitude', 'longitude', 'image_urls', 'description'], axis=1, inplace=True)

listing_details_cleaned = pd.read_csv('output/listing_details_cleaned.csv')
listing_details_cleaned.rename(columns={'Nguồn thông tin': 'url'}, inplace=True)
df = pd.merge(listing_details_cleaned, listing_details, how='left', on='url')

df['other_info'] = df['other_info'].apply(json.loads)
df['main_info'] = df['main_info'].apply(json.loads)

In [6]:
from rapidfuzz import fuzz
import re

QUALITY_LEVELS = [
    # Priority 1: Structure has essentially no value (0%)
    (0.0, [
        'tặng nhà', 'bán đất tặng nhà', 'chỉ tính tiền đất',
        'đất nền', 'nhà tạm', 'chủ yếu lấy đất', 'tặng nhà'
        'có nhà nhưng không đáng giá', 'không tính giá trị nhà',
        'nhà cấp 4 cũ', 'nhà xuống cấp', 'giá trị đất là chính',
        'bán đất'
    ]),
    # Priority 2: Old or needs significant repair (50%)
    (0.5, [
        'nhà cũ', 'nhà nát', 'cần sửa chữa', 'tiện xây mới',
        'xây lâu năm', 'xuống cấp', 'cũ nhưng ở tạm được',
        'cũ kỹ', 'nhiều năm chưa sửa', 'cần cải tạo',
        'nền móng yếu', 'sắp sập', 'cần xây lại', 
        'không có giá trị sử dụng',
    ]),
    # Priority 3: Good, well-maintained condition (85%)
    (0.85, [
        'nhà đẹp', 'còn mới', 'giữ gìn', 'full nội thất', 'thiết kế hiện đại',
        'nhà sạch sẽ', 'ở ngay', 'nhà gọn gàng', 'nội thất cao cấp',
        'không cần sửa', 'đẹp như hình', 'vào ở liền',
        'nội thất đầy đủ', 'tiện nghi', 'nhà không lỗi phong thủy',
        'còn bảo hành', 'nhà chất lượng tốt',
    ]),
    # Priority 4: Brand-new condition (100%)
    (1.0, [
        'mới xây', 'mới hoàn thiện', 'mới 100%', 'nhà mới keng',
        'vừa xây xong', 'mới bàn giao', 'mới nhận nhà', 'nhà rất mới',
        'chưa ở lần nào', 'nhà mới tinh', 'nhà mới toanh',
        'nhà xây mới', 'vừa hoàn thiện', 'còn thơm mùi sơn',
        'mới hoàn công', 'nhà xây kiên cố', 'đảm bảo kết cấu mới',
    ]),   
]

DEFAULT_QUALITY = 0.75

def estimate_remaining_quality(row):
    text = f"{row.get('title', '')} {row.get('description', '')}".lower()
    result = {}
    # result_qual = 0.75
    # result_ratio = 0
    for quality_val, keywords in QUALITY_LEVELS:
        for kw in keywords:
            pattern = kw.replace(' ', '(?:\s*\w+\s*){0,2} ')
            pattern = pattern.strip()
            pattern = '\W' + pattern + '\W'
            qual = re.search(pattern, text)
            if qual:
                ratio = fuzz.ratio(kw, qual.group(0))
                if quality_val == 0 or quality_val == 1:
                    ratio += 3
                result[quality_val] = [qual.group(0), ratio]
                # if ratio >= result_ratio:
                #     result_ratio = ratio
                #     result_qual = round(quality_val, 2)
                #     # result_qual.append(round(quality_val, 2))
                # return round(quality_val, 2), qual.group(0)
    # return round(DEFAULT_QUALITY, 2), 'None'
    # if 0 in result_qual:
    #     result_qual = 0
    # if 1 in result_qual:
    #     result_qual = 1
    # else:
    #     result_qual = max(result_qual)
    if result:
        # Sort by ratio first, then by quality value
        best_quality, (match, score) = max(result.items(), key=lambda x: (x[1][1], x[0]))
        return best_quality, result 
    else:
        return DEFAULT_QUALITY, result

    # return result_qual, result

In [ ]:
string = df.loc[5]['description']
print(string)
pattern = 'full(?:\s*\S+\s){0,2} nội(?:\s*\S+\s){0,2}'
print(f"{re.search(pattern, string).group(0) + 'hhh'}")

Toà nhà hẻm 8m Hoàng Hoa Thám, P.13 Tân Bình, hiện đang cho thuê khoán làm căn hộ dịch vụ 100tr/tháng. Thích hợp mua giữ tiền..
Diện tích: Đất 130m², vuông vắn. Sàn sử dụng 650m².
Hiện trạng: Nhà 5 tầng. Có thang máy, gồm 32 phòng full nội thất, cho thuê khoán là 100tr/tháng. Tự khai thác 150tr/tháng.
Hẻm rộng 8m thông, ngay sát nhà ga T3. Khu vực nhiều văn phòng, trung tâm thương mại.
Giá 19.2 tỷ thương lượng.
LH:
0903 992 ***
. MTG.
full nội thất, cho hhh


In [ ]:
estimate_remaining_quality(df.loc[69])

(1.0,
 {0.85: [' tiện nghi', 94.73684210526316],
  1.0: [' mới xây', 96.33333333333333]})

In [ ]:
df['quality keyword'] = ''
df[['new quality', 'quality keyword']] = df.apply(estimate_remaining_quality, axis=1, result_type = 'expand')

In [ ]:
pd.set_option('display.max_rows', None)
pd.set_option('display.max_colwidth', None)

df[df['new quality'] != df['Chất lượng còn lại']][['new quality', 'Chất lượng còn lại', 'description', 'title']].iloc[:10]

In [ ]:
pd.set_option('display.max_rows', None)
pd.set_option('display.max_colwidth', None)

print(f'Quality level 0: {df[df["Chất lượng còn lại"] == 0.0].shape[0]}')
print(f'Quality level 0.5: {df[df["Chất lượng còn lại"] == 0.5].shape[0]}')
print(f'Quality level 0.75: {df[df["Chất lượng còn lại"] == 0.75].shape[0]}')
print(f'Quality level 0.85: {df[df["Chất lượng còn lại"] == 0.85].shape[0]}')
print(f'Quality level 1: {df[df["Chất lượng còn lại"] == 1].shape[0]}')

Quality level 0: 8774
Quality level 0.5: 482
Quality level 0.75: 9595
Quality level 0.85: 7049
Quality level 1: 1348


In [ ]:
pd.set_option('display.max_rows', None)
pd.set_option('display.max_colwidth', None)

print(f'Quality level 0: {df[df["new quality"] == 0.0].shape[0]}')
print(f'Quality level 0.5: {df[df["new quality"] == 0.5].shape[0]}')
print(f'Quality level 0.75: {df[df["new quality"] == 0.75].shape[0]}')
print(f'Quality level 0.85: {df[df["new quality"] == 0.85].shape[0]}')
print(f'Quality level 1: {df[df["new quality"] == 1].shape[0]}')

Quality level 0: 5150
Quality level 0.5: 497
Quality level 0.75: 12152
Quality level 0.85: 8014
Quality level 1: 1435


# Test Đơn giá xây dựng

Các loại đơn giá xây dựng:
- Nhà cấp 4: 4,000,000
- Nhà 1 tầng bê tông cốt thép: 6,275,876
- Nhà từ 2 tầng, bê tông cốt thép, có hầm: 9,504,604
- Nhà từ 2 tầng, bê tông cốt thép, không hầm: 8,221,171
- Nhà biệt thự: 10,510,920
- Nhà biệt thự có hầm: 12,848,184

In [ ]:
import pandas as pd
import json
import numpy as np

listing_details = pd.read_csv('output/listing_details.csv')
listing_details.drop(['latitude', 'longitude', 'image_urls', 'description'], axis=1, inplace=True)

listing_details_cleaned = pd.read_csv('output/listing_details_cleaned.csv')
listing_details_cleaned.rename(columns={'Nguồn thông tin': 'url'}, inplace=True)
df = pd.merge(listing_details_cleaned, listing_details, how='left', on='url')

df['other_info'] = df['other_info'].apply(json.loads)
df['main_info'] = df['main_info'].apply(json.loads)

In [ ]:
yo = 'hầm + trệt + 3 lầu sân thượng akl dn hs'
print(yo)
yo = yo.replace('+', ' ')
pattern = '(?:\S+\s+){0,5}lầu(?:\s*\S+){0,5}'
string = yo.lower()
print(re.findall(pattern, string))

hầm + trệt + 3 lầu sân thượng akl dn hs
['hầm   trệt   3 lầu sân thượng akl dn hs']


In [ ]:
import re

def check_ham(text):
    # text = text.replace(',', ' ').replace('+', ' ')
    string = re.findall(pattern=r'(?:(?!được xây|giấy phép xây dựng|gpxd|cải tạo)\b\w+\b\W+){1,7}hầm(?:(?!\schui)\W+\b\w+\b){1,7}', string=text)
    if string:
        for substr in string:
            ham = re.search(pattern=r'tầng|lầu|tấm|mê|\d+|xe|kết cấu|kc|ô tô|thang máy|trệt|lửng', string=substr)
            if ham:
                return True
    return False
    
def extract_construction_cost(row):
    title = row['title']
    title_lower = title.lower()
    if pd.notna(row['description']):
        des_lower = row['description'].lower()
        text = f'{title_lower} {des_lower}'
    else:
        text = title_lower
        des_lower = 'none'
    text = text.replace(',',' ').replace('+',' ').replace('\n',' ').replace('*', ' ')
    text = ' '.join(text.split())
    des_lower = des_lower.replace(',',' ').replace('+',' ').replace('\n',' ').replace('*', ' ')
    des_lower = ' '.join(des_lower.split())
    if 'nhà trệt' in text:
        if not re.search(r'nhà trệt\s*(?:\S+\s+){0,2}(?:\d*\s*)(?:tầng|lầu|tấm|mê)', text):
            return 4000000
    cap4 = re.search(pattern = r'nhà cấp 4|nhà c4|cấp 4\W|nc4|nhà trệt|nhà nát', string=text)
    if cap4:
        return 4000000 #4,000,000
    if row['Số tầng công trình'] == 1:
        return 6275876
    
    ham = check_ham(text)
    if re.search(r'biệt thự', title_lower) or re.search(r'villa\W', title_lower):
    # if 'biệt thự' in title_lower or 'villa' in title_lower:
        if ham:
            return 12848184
        return 10510920
    if des_lower != 'none' and (re.search(r'biệt thự', des_lower) or re.search(r'villa\W', des_lower)):
        villa_pattern = [
            r'(?:thiết kế|xây)*\s*(?:\S+\s+){0,5} (?:phong cách|kiểu|dạng|kiến trúc|cấu trúc)\s*(?:\S+\s+){0,2} (?:biệt thự|villa\W)', #Các nhà có cấu trúc villa
            r'bán (?:(?!mua|xây)\S+\s+){0,3}(?:biệt thự|villa\W)', # Bán biệt thự
            r'(?:biệt thự|villa\W)\s*(?:\S+\s+){0,3}\d+\s*tầng' # Biệt thự bao nhiêu tầng
        ]
        not_villa_pattern = [
            r'(?:đối diện|nằm|sát|cạnh|ngay|liền kề|hàng xóm|xung quanh|gần|view|nhiều)\s*(?:\S+\s+){0,5}\s*(?:biệt thự|villa)', # Bên cạnh là khu villa
            r'(?:làm|xây|cải tạo)\s*(\S+\s+){0,4}(?:biệt thự|villa)', # Có thể xây thành biệt thự
            r'(?:nhà|phố|mặt tiền|tòa nhà|building|chuyên|kinh doanh|chdv|căn hộ dịch vụ|kdt|kđt|khu đô thị|(?:\+84|0)\s*(?:\d\s*){3,6}(?:\d\s*){0,3}|văn phòng|cao ốc|nhà cao tầng)(?:\s+\S+){0,5} (?:biệt thự|villa)', # Tránh giới thiệu về cò
            r'(?:biệt thự|villa)(?:\s+\S+){0,5} (?:nhà|phố|mặt tiền|tòa nhà|building|chuyên|kinh doanh|chdv|căn hộ dịch vụ|kdt|kđt|khu đô thị|(?:\+84|0)\s*(?:\d\s*){3,6}(?:\d\s*){0,3}|văn phòng|cao ốc|nhà cao tầng)', # Tránh giới thiệu về cò
            r'(?:mua|xây) (\S+\s+){0,3}(?:biệt thự|villa)', # Loại các trường bán để chuyển qua mua hoặc xây biệt thự
            r'(?:như|khu|toàn)\s*(?:\S+\s+){0,1}(?:biệt thự|villa)', # Các trường hợp đẹp như biệt thự, khu biệt thự
            r'(?:ra|chuyển)\s*(?:\S+\s+){0,2}(?:biệt thự|villa)' # Chuyển ra để ở khu villa
        ]
        for pattern in villa_pattern:
            if re.search(pattern, des_lower):
                if ham:
                    return 12848184 # Biệt thự có hầm
                return 10510920 # Biệt thự không hầm
        for pattern in not_villa_pattern:
            if re.search(pattern, des_lower):
                if row['Số tầng công trình'] == 2:
                    if ham:
                        return 6275876 # Nhà 1 tầng 1 hầm
                    else:
                        return 8221171 # Nhà 2 tầng không hầm
                if row['Số tầng công trình'] < 2:
                    if ham:
                        return 6275876 # ví dụ như nhà 1.5 thì 0.5 đó chính là tầng hầm 
                    return 8221171 # Nhà 2 tầng không hầm
                if ham:
                    return 9504604 # Nhà hơn 2 tầng, có hầm
                return 8221171 # Nhà hơn 2 tầng, không hầm
        if ham:
            return 12848184 # Biệt thự có hầm
        return 10510920 # Biệt thự không hầm
    if row['Số tầng công trình'] == 2:
        if ham:
            return 6275876 # Nhà 1 tầng 1 hầm
        else:
            return 8221171 # Nhà 2 tầng không hầm
    if row['Số tầng công trình'] < 2:
        if ham:
            return 6275876 # ví dụ như nhà 1.5 thì 0.5 đó chính là tầng hầm 
        return 8221171 # Nhà 2 tầng không hầm
    if ham:
        return 9504604 # Nhà hơn 2 tầng, có hầm
    return 8221171 # Nhà hơn 2 tầng, không hầm

In [ ]:
df['construction_cost'] = df.apply(extract_construction_cost, axis = 1)
df['construction_cost'].value_counts()

construction_cost
8221171     15569
6275876      1442
4000000       826
9504604       337
10510920      336
12848184       26
Name: count, dtype: int64

In [ ]:
have_biet_thu = df[df['description'].str.lower().str.contains('biệt thự') | df['description'].str.lower().str.contains('villa') |df['title'].str.lower().str.contains('biệt thự') |df['title'].str.lower().str.contains('villa')]
have_biet_thu.shape[0]

791

In [ ]:
have_biet_thu['construction_cost'].value_counts()

construction_cost
10510920    336
8221171     290
6275876      65
4000000      52
12848184     26
9504604      22
Name: count, dtype: int64

# Define Mặt phố / Mặt ngõ

In [87]:
import pandas as pd
import json
import numpy as np
import re

listing_details = pd.read_csv('output_27k/listing_details.csv')
listing_details.drop(['image_urls', 'description'], axis=1, inplace=True)

listing_details_cleaned = pd.read_csv('output_27k/listing_details_cleaned.csv')
listing_details_cleaned.rename(columns={'Nguồn thông tin': 'url'}, inplace=True)
df = pd.merge(listing_details_cleaned, listing_details, how='left', on='url')

df['other_info'] = df['other_info'].apply(lambda x: json.loads(x) if x != np.nan else None)
df['main_info'] = df['main_info'].apply(json.loads)
df.dropna(subset='description', inplace=True)
df['index'] = df.index

pd.set_option('display.max_rows', None)
pd.set_option('display.max_colwidth', None)

Notes about real, inspected mặt phố - mặt ngõ
<!-- - Ngách có mặt phố: **TOÀN BỘ LÀ NHÀ NGÁCH THẬT** 
    - 550: nhà bán nằm trong ngách rộng 3m (bán nhà đẹp phố yên lạc)
    - 1374: nhà 1 mặt ngõ, 1 mặt ngách nên phòng nào cũng có ánh sáng tự nhiên (từ nhà ra mặt phố lớn chưa đến 100m)
    - 2136: nhà lô góc một mặt ngõ một mặt ngách (nhà nằm trên phố lĩnh nam)
    - 4726: đi ngõ 63 ngách 59 phố Cổ Linh (bán căn nhà ngõ 191 phố thạch bàn)
    - 9556: bán nhà số 23 ngách 26 (bán nhà phố nghĩa dũng)
    - 9569: nhà lô góc, mặt ngách (tương lai sau quy hoạch ra mặt đường lớn)
    - 10606: ngõ ngách sạch đẹp, đường vào rộng thoáng, ngõ thông, ba gác đỗ tận cửa (bán nhà phố, vài trăm mét ra mặt phố bùi xương trạch)
    - 11490: nơi mặt ngách/hẻm vẫn kinh doanh được 17 tỷ (1 nhà ra mặt phố)
    - 14560: ngõ ngách thông tứ tung (bán nhà đẹp ngõ phố yên hòa)
    - 14593: bán nhà 4 tầng ngách 298 (cách 200m ra mặt đường quốc lộ 1 và đường phan trọng tuệ)
- Kiệt có mặt phố: trừ các trường hợp mà cách mặt tiền đường lớn ctct tức là nó chỉ cần các khu đó thôi, còn lại nếu mình lấy vài từ sau mấy chữ mặt phố mà nó ko xuất hiện lại trong các cụm như kiểu cách bao nhiêu m, ra vài bước chân, sau lưng, đối diện, đối lưng,... thì nó sẽ __đều là mặt phố thật__. Kiệt ở đây thường là kiệt bên hông/đằng sau thôi chứ mặt tiền vẫn là đường
    - 574: bán nhà kiệt ôtô (cách mặt tiền đường lớn chỉ vài bước chân)
    - **1500**: mặt tiền tô hiến thành, vị trí: mặt tiền đường 5m5 tô hiến thành (vs kiệt 3m) -> nhà mặt tiền đường có kiệt bên hông nên vẫn là nhà mặt tiền
    - 6547: nhà kiệt 2 tầng lê duẩn (cách mặt đường chính chỉ 70m)
    - 6854: kiệt chuẩn 4m (bán nhà phố cổ hội an + cách 300m đến phố đi bộ trong phố cổ)
    - 10356: kiệt rộng 3m (sau lưng mặt tiền đường lớn)
    - **11559**: kiệt bên hông 2m (nhà 3 tầng mặt tiền nguyễn đình) -> kiệt chỉ là bên hông còn vẫn đất mặt tiền
    - 13100: nhà 2 tầng kiệt thái thị bôi (cơ hội sở hữu nhà phố 3 tầng)
    - 15937: bán nhà kiệt lê độ (sơn thành, chuyên nhà phố trung tâm đà nẵng)
    - 16285: bán nhà kiệt lê độ (gần mặt đường đoạn trước nhà 5m)
    - 18252: nhà 3 tầng kiệt ô tô (kiệt ô tô thông cách mặt tiền vài căn)
    - **19039**: lô đất 2 mặt tiền đường trần nhân tông (có 2 mặt tiền đường gồm đường trần nhân tông rộng 19,5m và đường kiệt betong 4m)
    - **19211**: 2 mặt tiền đường trương định (kẹp kiệt 2m)
    - **19554**: bán nhanh lô đất đường lê văn thứ (đường kiệt 5m trải nhựa sạch sẽ)
    - 19898: đường kiệt ô tô 6m thông (sau lưng mt lê thanh nghị chỉ vài bước ra trục chính)
    - **19941**: 2 mt đường phan bôi, an hải đông (kẹp kiệt thông thoáng)
    - **20177**: mặt tiền trần hưng đạo (1 mặt chính trần hưng đạo, 2 mặt kiệt bên hông cực thoáng)
    - **21105**: siêu lô đất mặt tiền đưuòng 10m5 sơn trà (giá chỉ ngang đất kiệt)
    - 21165: cặp kiệt sau chợ khái tây (đối lưng mặt tiền lưu quang vũ)
    - **21348**: mặt tiền đường 2 tháng 9 (kẹp kiệt 4m)
    - **21604**: bán lô đất mặt tiền đường phó đức chính (bên hông kẹp kiệt 3m thoáng)
    - 21776: kẹp kiệt thông sau lưng 5m (mặt tiền đường 7m5)
    - 21799: như trên
    - 22564: như trên
    - _**22585**_: mặt tiền đường 5m5, đất kiệt ô tô đã 70tr/m2 trong thời điểm hiện tại -> không thể chắc chắn mặt tiền đường như thế này thì có phải mặt phố không, còn kiệt ở đây chỉ được để như 1 so sánh, không thật sự là tính chất khu đất
    - **22634**: mặt tiền đường trần hưng đạo, 1 mặt chính đường trần hưng đạo, 2 mặt kiệt bên hông cực thoáng
    - **23174**: lô đất 3 mặt đường trục chính phú quý, trục chính phú quý đường lề 5m, đất 3 mặt kiệt thông thoáng
    - **23224**: hai mặt tiền đường hải hồ (kiệt sau 3m)
    - _**23422**_: mặt tiền đường 10m5, giá chỉ ngang đất kiệt
    - **23557**: mặt tiền đường nguyễn tất thành (sau lưng có kiệt 5m) 
    - **24845**: 3 lô mặt tiền đường nguyễn tất thành (2 mặt tiền trước sau, phía sau có kiệt ô tô 5m)
    - **25438**: MT trương định (2 mặt tiền đường kiệt bên hông ô tô ra vào)
    - _**25663**_: bán đất mặt tiền kẹp kiệt 5m đường mỹ khê 8
    - 26072: bán đất kiệt 7m (mặt tiền kiệt 7m, nằm trên trục chính của dân cư khu vực)
- Hẻm xe tải/hơi/sẹc có mặt phố: **không cần check đâu**
- Hẻm có mặt phố: trừ các dòng liên hệ mua nhà hẻm còn đâu khá legit. Vì số lượng ít nên sẽ để vậy luôn
    - 38: hẻm sạch sẽ an ninh, cho anh bảo chuyên nhà phố
    - 39: Hẻm 4M gần mặt tiền đường
    - 68: hẻm ô tô, Tương lai 2 mặt đường trước và sau
    - 112:  hẻm ba gác thông thoáng, Nhà rất gần mặt tiền đường lớn, cách khoảng 40m.
    - 119: Nhà đẹp 6 lầu T/máy hẻm 10m, bán nhanh căn nhà phố 6 tầng
    - 173: nhà hẻm xe hơi cách 30m mặt tiền đường
    - 180: vị trí hẻm oto 8m, ký gửi mua bán nhà phố
    - 198: Hẻm 8m xe hơi tránh nhau, nhà phố 4 tầng khu trung tâm
    - 200: hẻm xe hơi hai chiều, Bán nhà phố chính chủ
    - 229: hẻm trước nhà 7m rộng rãi sạch sẽ và cách vài căn ra mặt tiền đường
    - 234:  hẻm 5M sạch đẹp, thẳng 1 trục vài bước ra mặt tiền đường và thông tứ tung
    - 245: Nhà 1/, XH ngủ trong nhà, hẻm 5M sạch sẽ yên tĩnh, thẳng 1 trục ra mặt tiền đường và thông tứ tung
    - 320: hẻm 790/33/ hương lộ 2, Bán nhà phố quận Bình Tân
    - 339: Bán nhà hẻm xe hơi 8m, Nhà Phố Kiến Hưng
    - 359: BÁN NHÀ HẺM XE HƠI 12M, Liên hệ: Nhà Phố Kiến Hưng
    - 383: hẻm ôtô trung tâm Linh Chiểu, chỉ 40m ra mặt tiền đường 16
    - 393: mặt tiền đường 8m, Đường nhựa 8m. Hẻm thông thoáng. 60m ra Hoàng Trọng Mậu.
    - **405**: Cần bán nhà đường 17B, Chuyên nhận mua bán ký gửi:\n- Căn hộ chung cư cao cấp quận Tân Phú, Tân Bình.\n- Nhà phố, biệt thự, nhà hẻm,...\n -> TẠI CÁI DÒNG LIÊN HỆ NÀY
    - 407: Hẻm 10m kinh doanh, vui lòng gọi ninh nhà phố
    - **412**: cần bán nhà cấp 4 đường nội bộ -> TẠI CÁI DÒNG LIÊN HỆ Y HỆT 405
    - 428: Nhà phố 3 tầng mặt tiền hẻm 6m
    - 551: Bán Nhà phố mới keng 1/ TA05, xây 2 lầu hẻm xe hơi đậu cửa
    - 554: Bán Nhà 1 Trệt 2 Lầu xây tâm huyết Hẻm Ô Tô, Nhà phố hẻm ô tô
    - 561: Nhà mới đẹp 3 tầng hẻm xe tải, gần trục chính
    - 565: hẻm xe tải, gần trục chính
    - 627: LÔ GÓC 2 MẶT HẺM XE HƠI, gặp e thuận chuyên nhà phố gò vấp
    - 630: BÁN NHÀ HẺM XE HƠI, chỉ cách mặt tiền đường Lạc Long Quân vài căn
    - 665: Hẻm 6m Nguyễn Phúc Chu, gần mặt tiền đường
    - 671:  Hẻm xe hơi quay đầu thoải mái, vài bước chân ra mặt tiền đường lớn
    - 813: hẻm 5m,  Mặt tiền đường 6m
    - 935: Hẻm nhựa trước nhà rộng 8m xe hơi quay đầu, Nhà Phố 2 Mặt Tiền
    - 976: Hẻm rộng 5m, Địa chỉ: 1/ Lê Văn Thọ, Vị trí hẻm 1 trục chỉ 30m ra mặt tiền đường lớn
    - 1061: Bán nhà đẹp hẻm Nguyễn Biểu, Hẻm trước nhà 3.5m, thẳng đẹp, chỉ cách mặt tiền đường chính 30m
    - 1073: HẺM XE HƠI NGUYỄN VĂN TRỖI, TRỤC CHÍNH VĂN PHÒNG
    - 1077: hẻm xe hơi, trục chính văn phòng
    - 1107: Hẻm số 1, Loại hình: Nhà phố
    - 1126: nhà mặt tiền hẻm thông, Gặp Thành nhà phố
    - 1237: Nhà Phố hiện đại mới - hẻm 1806 Huỳnh Tấn Phát cách Q7 300m -
    - 1285: hẻm 8m, Nhận ký gửi Bất Động Sản Nhà Phố.
    - 1288: Bán nhà phố, đường Lê Văn Lương, hẻm xe hơi, 5 tầng
    - 1339: Hẻm ôtô đỗ cửa, Cách mặt tiền đường Bàn Cờ chỉ 20m
    - 1366: hẻm xe hơi , sát mặt tiền đường Bàu Bàng
    - 1410: hẻm rộng thoáng, Em Tân nhận ký gửi trao đổi nhà phố
    - 1432: Hẻm ba gác, Liên hệ ngay:\nLong Nhà Phố
    - 1434: SIÊU PHẨM NHÀ PHỐ, hẻm rộng 6m, xe hơi ra vào thoải mái
    - 1513: hẻm xe hơi, Cách mặt tiền Đường Nguyễn Văn Linh 50m
    - 1630: Bán căn nhà phố, Hẻm xe hơi số 64 Hoa Lan
    - 1644: Nhà bán hẻm xe hơi Bùi Minh Trực, cách mặt tiền đường 4 căn
    - 1693: Bán nhà hẻm VIP Nguyễn Trãi, bán bất động sản nhà phố trung tâm Sài Gòn.
    - 1698: Hẻm 5m, Phương Honestly Chuyên Gia Nhà Phố Tân Bình
    - 1774: Bán nhanh nhà góc 2 mặt tiền đường, Bán nhà hẻm xe hơi
    - 1790: Nhà hẻm, rất gần mặt tiền đường Phan Văn Trị
    - 1798: hẻm thông lộ giới 6m, nhà siêu rẻ tại hẻm xe hơi Bùi Đình Túy,  Nhận ký gửi mua bán nhà phố
    - 1816: Hẻm nhựa 5m, Hẻm xe hơi 5m, Chuyên nhà phố Tân Phú
    - 1854: hẻm xe hơi thông, LH: Hùng chuyên nhà phố
    - 1867: hẻm xe hơi, gần mặt tiền đường bạch đằng
    - 1901: hẻm 3m sát mặt tiền phan xích long, nhận ký gửi mua bán nhà phố
    - 1908: nhà phố đường nguyễn đình chiểu, vị trí hẻm xe hơi đường nguyễn đình chiểu
    - 2018: BÁN GẤP NHÀ HẺM OTO, HẺM XE HƠI 8M, sát mặt tiền đường lớn
    - 2102: căn góc 2 mặt hẻm xe hơi, cách mặt tiền đường đồng nai khoảng 50m
    - 2110: bán nhà hẻm, gần mt đưuòng lạc long quân
    - 2120: góc 2 mặt tiền đường bê tông, diện tích sau khi mở rộng hẻm còn lại (check tin thì không phải kiểu đường chính gì)
    - 2128: hẻm 3,5m thực tế -cách măt tiền đường 20m
    - 2278: hẻm ô tô, chuyên nhà phố sài gòn
    - 2311: hẻm xe hơi 5m, nhận ký gửi mua bán nhà phố
    - 2399: gần mặt tiền đường, hẻm rộng
    - 2483: hẻm rộng, vị trí vip gần mặt tiền đường bà hom
    - 2554: bán căn nhà 1/, căn nhà phố trệt 2 lầu, hẻm nhựa 1/ xe hơi đậu cửa
    - 2603: nhà hẻm xe hơi, chỉ cách mặt tiền đường lê quang định 20m
    - 2684: bán nhà hẻm 7m, gần mt đường ba tháng hai
    - 2686: hẻm 6m thông, nhà sát mặt tiền đường
    - 2701: đường hẻm vào 6m, nhà cách khu phố ẩm thực
    - 2735: bán nhà hẻm xe hơi, cách mặt tiền đường chỉ 5 mét
    - 2758: cơ hội hiếm có nhà phố trung tâm phú nhuận, cách hẻm xe hơi chỉ 3 bước chân, nhà gần mặt tiền khu phan xích long phố ẩm thực sầm uất (check ảnh thì là hẻm)
    - 2775: mặt tiền đường đẹp, xe hơi vào nhà hẻm sạch, khu dân trí cao
    - 2776: như bên trên
    - _**2849**_: hẻm oto, nhà mặt đường đường đào duy anh (không biết là kiểu gì)
    - 2965: hẻm xe hơi, 3 bước ra mặt tiền đường
    - 2995: bán nhà mặt tiền đường, bán nhà mặt tiền hẻm đường 38
    - 3002: siêu dòng tiền hẻm trần bình trọng, nhà 1/ hẻm xe hơi 6m, nhà gần mặt tiền đường
    - 3062: hẻm to 8m, hỗ trợ tìm nhà phố miễn phí các quận trung tâm tphcm
    - 3109: nhà xinh hẻm xh, gần mặt tiền đường
    - 3144: sát hẻm oto lê văn duyệt, nhà hẻm 3m, ký gửi mua bán nhà phố
    - 3169: vị trí hẻm 6m, xanh mát trong không gian nhà phố hiện đại
    - 3249: bán nhà hẻm xe hơi đường, nhận hỗ trợ ký gởi mua bán nhà phố
    - 3258: hẻm rộng rãi, sạch sẽ, gần mặt tiền đường hvt
    - 3327: nhà mặt tiền hẻm 8m, nhà phố mặt tiền hẻm
    - 3334: em bán căn nhà phố,hẻm nhựa hoàng trọng mậu rộng 16m
    - 3356: sát mặt tiền đường lê văn sỹ, hẻm trước nhà rộng 4 mét thông
    - 3400: bán nhà hẻm xe hơi, thiện nhà phố saigon
    - 3419: nhà phố hẻm xe hơi đường hai bà trưng
    - 3424: hẻm 5m, khu nội bộ nhà phố xây kín an ninh
    - 3426: nhà phố 5m x 14m, hẻm 5m
    - 3429: nhà phố 1 lửng 3 lầu, hẻm 8m thông
    - 3432: có ô thang máy 1/ hẻm 11m, cách mt đường dương thị mười chỉ 50m
    - 3433: nhà phố 5m x 20m, 1/ đường trần thị do, 1/ hẻm 11m 
    - 3435: Nhà phố 1 lửng 3 lầu full nội thất / ngắn hẻm 6m
    - 3444: nhà phố 4m x 15m, hẻm 8m
    - 3445: siêu phẩm 4 tầng góc 2mt hẻm 8m, góc 2mt đường 8m
- Gần phố và có mặt phố: gần phố thì oke, gần đường chỉ khi xét xem cái đường sau chữ mặt phố đó có khớp hay không thôi
    - **118**: bán nhà đường láng, gần phố
    - 175: liên nhà phố, gần đường thành (drop)
    - **377**: bán nhà đường thống nhất, bán nhà 3 tầng đường rộng 6m, gần đường lê đức thọ
    - 392: cách mặt phố định công 70m
    - 542: cách trục chính 200m,gần đường vành đai 4
    - **543**: bán nhà phố trạm, gần phố lâm hạ
    - 701: nằm gần đường lớn dương quảng hàm chỉ cách vài bước, đây là căn nhà đẹp nhất cung đường trần bá giao
    - 830: bán nhà phố linh lang, gần đường văn cao trục chính dẫn ra tây hồ
    - 951: bán nhà 3 thoáng phố nguyễn hoàng, trần bình (xem ảnh thì không phải)
    - 1170: cần bán nhà phố vọng, nhà ở dọc phố vọng (basically phố vọng không phải phố ấy)
    - 1185: nhà gần đường văn tiến dũng
    - 1278: nhà đẹp phố nguyễn văn cừ, vị trí đắc địa cách phố chỉ 1 phút đi bộ (không biết kiểu gì)
    - 1297: nhà phố nằm gần đường trịnh như khuê
    - 1372: gần phố, cách 1 nhà ra phố
    - 1403: bán nhà giáp ngoại giao đoàn, từ nhà ra mặt phố 35m
    - 1448: gần phố, nhà rộng - gần phố
    - **1482**: bán nhà riêng tại đường lạc long quân
    - 1624: nhà phố cầu giấy, gần phố
    - 1673: nhà gần đường lớn ô tô qua, 100m ra đường ỷ la dương nội
    - 1947: chính chủ bán nhà phố đại cát, gần đường lớn, cách mặt đường liên mạc 10m
    - 1951: bán nhà phố phạm văn đồng, gần phố
    - 2054: gần đường ô tô, cách mặt phố chỉ vài bước chân
    - 2123: đường trước nhà thông ra phố
    - **2173**: bán nhà riêng đường chiến thắng, gần phố, gần đường trần phú 
    - 2243: ngay gần phố, nằm gần các tuyến đường lớn, liên hệ ngay (24/7) lê đình phúc nhà phố
    - 2267: nhà cách đường lớn chỉ vài bước chân, bán nhà phân lô hoàng quốc việt
    - 2302: bán nhà phố ngô thì nhậm, bán nhà gần phố ngô thì nhậm
    - 2355: bán nhà gần trần khát chân, căn nhà gần phố chính
    - 2447: bán nhà 2 thoáng phố hoàng văn thái
    - **2456**: nhà thuộc phố thượng thanh, gần đường lý sơn
    - 2634: gần đường ô tô tránh
    - 3020: bán nhà phố bạch mai, gần phố bạch mai
    - 3344: vài bước chân ra mặt phố quan nhân
    - **3404**: bán nhà 5 tầng phố bế văn đàn, gần phố quang trung
    - 3648: nhà phố trần duy hưng, nhà gần phố
    - 3816: Với nguồn nhà phong phú hàng 1000 căn nhà Hà Nội phố sẽ rất nhanh chóng tìm ra căn nhà ưng ý cho quý khách,
    - 3915: nhà mặt phố nguyễn cao, gần phố lò đúc, nhà mặt phố (vị trí thì không hẳn là mặt phố)
    - 4179: nhà phố lê trọng tấn
    - 4377: căn nhà tại phố trương định, gần phố (vị trí thì ở trong ngõ)
    - 4448: gần phố, nam nhà phố HN
    - 4463: gần phố tứ hiệp, quanh nhà 500m phố chợ thời trang
    - 5239: bán nhà riêng đường Mỗ Lao, Hà Đông, gần đường thanh bình
    - 5244: nhà vài bước ra mặt phố, vài bước ra đường ngô thì sĩ, gần phố ô tô tránh đỗ,
    - 5894: bán nhà phố lâm hạ, cách mặt phố lâm hạ khoảng 30m,
    - 6304: cách mặt phố hạ yên quyết 30m ô tô đỗ cửa
    - 6515: nhà gần phố gần ô tô
    - 7318: ban nhà phố đàm quang trung, 50m ra mặt phố đàm quang trung
    - 7769: nhà đẹp gần phố
    - **8159**: bán nhà phố nghĩa đô, vài bước ra mặt phố hoàng quốc việt
    - 8286: nhà mới ở phố giảng võ, gần phố
    - 9033: bán nhà 48m2 phố thái hà, cách mặt phố thái hà chỉ 30m
    - 9575: nhà gần phố dương văn bé
    - **9646**: bán nhà phố thụy khuê, 10m ra phố
    - 10077: bán nhà phố sài đồng, gần phố nguyễn văn linh (địa chỉ ngõ phố sài đồng)
    - 10614: sát mặt phố nguyễn khang, nằm trên tuyến phố hạ yên quyết đang mở rộng, 
    - 10759: cách mặt phố chưa đến 50m, liên hệ: tâm nhà phố
    - 10857: Bán Nhà đẹp gần phố 
    - 10995: nhà đẹp gần phố
    - 11164: ba bước là mặt phố láng hạ
    - 11424: gần phố trần cung, cách mặt phố trần cung chỉ 50m
    - 12569: bán nhà phố nghĩa tân, nghĩa tân 30m
    - 12583: bán nhà phố ha đình, gần phố ô tô tránh
    - 12677: nhà phố minh khai, 30m ra mặt phố minh khai
    - 12721: bán nhà cách mặt phố trường chinh 15m
    - 12722: bán gấp nhà phố tây sơn, gần phố (trông ảnh không phải đường tây sơn)
    - 12874: 30m ra mặt phố
    - 13271: nhà gần phố ngọc lâm
    - 13304: chủ bán đi mua nhà mặt phố to hơn, bán nhà ngọc lâm, vị trí: ngọc lâm phố cổ, gần phố nguyễn văn cừ
    - 13492: nhà gần phố xung quanh nhiều tiện ích gần trường
    - **13873**: nhà ở đầu phố nhân hòa, gần phố quan nhân, 500m ra đường nguyễn trãi
    - 14182: gần phố, 50m ra mặt phố
    - 14990: rất gần phố, trong tương lai gần, mặt sau nhà sẽ ra mặt phố to
    - 15387: bán nhà riêng tại đưuòng tô ngọc vân, gần phố (ngõ nha)
    - 15437: bán nhà phố xuân đỉnh, ô tô tránh gần phố xuân đỉnh
    - 15526: bán gấp nhà phố bạch đằng, gần phố (địa chỉ là trong ngõ)
    - 15891: nhà gần đường lớn yên hòa
    - 18197: nhà gần phố
    - 18528: gần phố âu cơ, chỉ cách mặt phố âu cơ đúng 1 nhà
    - 23888: mặt đường chia ô bàn cờ, gần phố điền lư -->

## Mặt phố mặt ngõ chính thức (hai block code dưới)

In [168]:
def search_pho(string, short_add):
    string_lower = string.lower()
    # main_road = '(?:\S+\s){0,5}(?:nhà(?:\s\S+){0,2} phố|nhà(?:\s\S+){0,2} mặt phố|mặt phố|mặt tiền phố|mt phố|phân lô phố|nhà(?:\s\S+){0,2} mặt đường|nhà(?:\s\S+){0,2} đường|mặt đường| mt đường|mặt tiền đường|\Wmtd\W|\Wmtđ\W|(?<!ngõ\s)trục chính)\W?\s?(?:\S+\s){0,4}'
    # short_main_road = '(?:nhà(?:\s\S+){0,2} phố|nhà(?:\s\S+){0,2} mặt phố|mặt phố|mặt tiền phố|mt phố|phân lô phố|nhà(?:\s\S+){0,2} mặt đường|nhà(?:\s\S+){0,2} đường|mặt đường| mt đường|mặt tiền đường|\Wmtd\W|\Wmtđ\W|trục chính)'
    main_road = '(?:\S+\s){0,5}(?:nhà(?:\s\S+){0,2} mặt phố|mặt phố|mặt tiền phố|mt phố|phân lô phố|nhà(?:\s\S+){0,2} mặt đường|nhà(?:\s\S+){0,2} đường|mặt đường| mt đường|mặt tiền đường|\Wmtd\W|\Wmtđ\W)\s?(?:\S+\s){0,4}'
    short_main_road = '(?:nhà(?:\s\S+){0,2} mặt phố|mặt phố|mặt tiền phố|mt phố|phân lô phố|nhà(?:\s\S+){0,2} mặt đường|nhà(?:\s\S+){0,2} đường|mặt đường| mt đường|mặt tiền đường|\Wmtd\W|\Wmtđ\W)'
    if len(re.findall(short_main_road, string_lower)) >= 5:
        return 'Drop'
    close = 'gần|cạnh|\Wra\W|sát|giáp|cách|sau|tránh|đối diện|kết nối|tương lai|quy hoạch|ký gửi|ký gởi|kí gửi|kí gởi|chuyên|nhà ngõ|nhà ngách|nhà hẻm|nhà kiệt|biệt thự|liên hệ|\Wlh\W|bước|căn|(?:vài|\d+)\snhà|phút|\d+p'
    if short_add != '':
        short_add_split = short_add.lower().strip().split(',')
        if 'đường' in short_add_split[0] or 'phố' in short_add_split[0]:
            road_name_in_short_add = short_add_split[0].replace('đường', '').replace('phố', '').strip()
            if re.search(rf'(?:{close})\s?(?:\S+\s){{0,5}}{re.escape(road_name_in_short_add)}', string_lower):
                # return re.search(rf'(?:{close})\s?(?:\S+\s){{0,5}}{re.escape(road_name_in_short_add)}', string_lower)
                return None
            if re.search(rf'{re.escape(road_name_in_short_add)}(?![^\.,\?!]*[.,\?!])\s?(?:\S+\s){{0,2}}(?:{close})', string_lower):
                # return re.search(rf'{re.escape(road_name_in_short_add)}(?![^\.,\?!]*[.,\?!])\s?(?:\S+\s){{0,2}}(?:{close})', string_lower)
                return None
            # if len(re.findall('nhà phố', string_lower)) == 1 and road_name_in_short_add not in string and re.search(r'(?:nhà(?:\s\S+){0,2} mặt phố|mặt tiền phố|mt phố|phân lô phố|nhà(?:\s\S+){0,2} mặt đường|nhà(?:\s\S+){0,2} đường|mặt đường| mt đường|mặt tiền đường|\Wmtd\W|\Wmtđ\W)', string_lower) is None:
            #     return None
    pho = re.search(main_road, string_lower)
    if pho:
        # Nếu các cụm đó chỉ là gần phố, gần đường abc --> thì bỏ
        if re.search(close, pho.group(0)):
            return None
        # return 'Mặt phố'
        else:
            # Tìm xem nó đang nằm trên mặt đường nào
            road = re.search(short_main_road, string_lower)
            # if road:
            road_span = road.span()
            # start = 0 if road_span[0] < 40 else road_span[0] - 40
            # Tìm 20 ký tự sau các keyword về mặt phố mặt ngõ
            end = len(string) if road_span[1] + 20 > len(string) else road_span[1] + 20
            road_name_list = string[road_span[1]:end].split()
            if len(road_name_list) < 1:
                road_name = None
            elif len(road_name_list) == 1:
                if road_name_list[0][0].isupper() or re.match(r'\d+/\d+', road_name_list[0]):
                    road_name = road_name_list[0]
                else:
                    road_name = None
            else:
                # Nếu hai từ đầu tiên sau đó được viết hoa thì khả năng cao nó chính là tên đường
                if road_name_list[0][0].isupper() and road_name_list[1][0].isupper():
                    road_name = road_name_list[0]  + ' ' + road_name_list[1]
                # Nếu từ đầu tiên có dạng kiểu 23/5 (đường 2/9)
                elif re.match(r'\d+/\d+', road_name_list[0]):
                    road_name = road_name_list[0]
                else:
                    road_name = None
            if road_name:
                # Tìm sự xuất hiện của tên đường trong phần còn lại của description
                search_string = f'(?:\S+\s){{0,5}}{re.escape(road_name)}\W?\s?(?:\S+\s){{0,4}}'
                while True:
                    if len(string) <= 5:
                        if re.search('(?:gần|cạnh|cách|\Wra|giáp|sát) (?:phố|mặt phố)', string_lower) or re.search(r'(?:phố|mặt phố)\s(?:\S+\s)?(?:gần|cạnh|cách|ra\W|giáp|sát|vào)', string_lower):
                            return None
                        return 'Mặt phố'
                    road_appearance = re.search(search_string, string)
                    if road_appearance:
                        # Nếu có các từ trong trường gần ở xung quanh tên đường ở đằng sau
                        if re.search(close, road_appearance.group(0)):
                            return None
                        else:
                            string = string[road_appearance.span()[1]:]
                    else:
                        # Nếu có các cụm gần phố thì thôi (kiểu gần phố không thôi, không có mấy cái kiểu gần phố A B gì cả)        
                        if re.search('(?:gần|cạnh|cách|\Wra|giáp|sát) (?:phố|mặt phố)', string_lower) or re.search(r'(?:phố|mặt phố)\s(?:\S+\s)?(?:gần|cạnh|cách|ra\W|giáp|sát|vào)', string_lower):
                            return None
                        return 'Mặt phố'                
            else:
                if re.search('(?:gần|cạnh|cách|\Wra|giáp|sát) (?:phố|mặt phố)', string_lower) or re.search(r'(?:phố|mặt phố)\s(?:\S+\s)?(?:gần|cạnh|cách|ra\W|giáp|sát|vào)', string_lower):
                    return None
                return 'Mặt phố'
    return None

In [172]:
from rapidfuzz.fuzz import ratio

def new_define_mat_pho_mat_ngo(row): #Code chính hiện tại
    #------TH0: check từ short_address------
    road_add = row['short_address'].split(',')[0].lower()
    if '/' in road_add:
        # Đường 2/9 (đại khái không phải xoẹt)
        if re.search(r'(?:đường|phố) (?:\S+\s){0,2}(?:\S+/\S+)', road_add):
            pass 
        else:
            return 'Mặt ngõ'
    if re.search(r'hẻm|ngõ|ngách|kiệt\s', road_add):
        return 'Mặt ngõ'
    
    if pd.notna(row['description']):
        des = row['description']
    else:
        des = ''
    if pd.notna(row['title']):
        title = row['title']
    else:
        title = ''

    string = title + '. ' + des
    short_add = row['short_address']
    if short_add is None:
        short_add = ''
    pho = search_pho(string, short_add)
    string = string.lower()
    # main_road = '(?:\S+\s){0,5}(?:nhà(?:\s\S+){0,2} phố|nhà(?:\s\S+){0,2} mặt phố|nhà(?:\s\S+){0,2} mặt đường|nhà(?:\s\S+){0,2} đường|mặt phố|mặt đường|mặt tiền phố|mt phố| mt đường|mặt tiền đường|\Wmtd\W|\Wmtđ\W|trục chính|phân lô phố)\W?\s?(?:\S+\s){0,4}'
    # pho = re.search(main_road, string)
    # if pho and re.search(r'gần (?:\S+\s){0,2}phố', pho.group(0)):
    #     pho = None
    # pho = search_pho(string)
    #------ TH1: Hẻm xe hơi, hẻm xe tải và sẹc ------
    if re.search(r'hxh|hxt|sẹc|sẹt|xẹc|xẹt| sec ', string):
        return 'Mặt ngõ'
    
    #------ TH2: Ngách ------
    result = re.findall(r'(?:\S+\s+){0,5}(\S+\sngách)\s*(?:\S+\s+){0,5}', string)
    if result != []:
        for i in result:
            if i.startswith('ng'):
                if ratio(i, 'ngóc ngách') >= 90:
                    continue
                return 'Mặt ngõ'
            return 'Mặt ngõ'
        
    #------ TH3: Kiệt ------
    kiet = re.findall(r'(?:\S+\s){0,3}kiệt(?:\s\S+){0,2}', string)
    if len(kiet) > 0:
        for k in kiet:
            if re.search(r'(?:lý thường |võ văn |phạm |anh |em |mr.\s?|tuấn |tam |nhân |văn )kiệt', k) or 'kiệt tác' in k:
                continue
            else:
                if pho:
                    break # return 'Kiệt có mặt phố'
                return 'Mặt ngõ'
    
        # if re.search(r'(?:lý thường|võ văn|nhân|phạm)\skiệt', string) or 'kiệt tác' in string and len(re.findall('')):
        #     pass
        # else:
        #     if pho:
        #         return 'Kiệt có mặt phố'
        #     return 'Kiệt'

    # kiet = re.search(r'(?<!lý\sthường\s)(?<!võ\svăn\s)(?<!nhân\s)(?<!phạm\s)kiệt(?!\stác)\W', string)
    # if kiet:
    #     if pho:
    #         return 'Kiệt có mặt phố'
    #     return 'Kiệt'
    # if re.search(r'mặt kiệt|măt kiệt|mat kiệt|đất kiệt|nhà kiệt', string):
    #     return 'Kiệt new'
    
    #------ TH4: Hẻm ------
    if re.search(r'(?<!như)(?<!hơn)(?:\S+\s){0,2}(?:hẻm|\Whem\W)',string):
        return 'Mặt ngõ'
    
    #------ TH5: Các trường hợp drop define từ search_pho ------
    if pho == 'Drop':
        return 'Drop'
    
    #------ TH6: Ngõ ------
    ngo = re.findall(r'(?:(?<!hơn\s)(?<!như\s)(?<!giá\s)(?:\S+\s*){1,3})ngõ', string)
    cua_ngo = re.search(r'(?<!đỗ\s)(?:cửa ngõ|cưa ngõ|một mặt ngõ|1 mặt ngõ|một ngõ|1 ngõ)', string)
    if ngo:
        if "nhà ngõ" in string:
        # if re.search(r'(?:nhà|mặt) (?:\w+\s){0,2}ngõ', string):
            return 'Mặt ngõ'
        if 'mặt ngõ' in string:
            return 'Mặt ngõ'
        if 'ngõ vào' in string:
            return 'Mặt ngõ'
        if not cua_ngo:
            if pho:
                if re.search(r'như (?:\S+\s){0,2}ngõ', string):
                    return 'Mặt phố'
                return 'Mặt ngõ' # Ngõ hết
            return 'Mặt ngõ'
        elif cua_ngo and len(ngo) == 1:
            pass
        else:
            if pho:
                return 'Drop' # Drop hết các dòng trong phần này vì nó lẫn lộn giữa mặt phố và mặt ngõ
            return 'Mặt ngõ'
    if pho:
        # if re.search(r'ngõ|ngách|hẻm|kiệt', pho.group(0)):
        #     return None
        slash = re.search(r'nhà \d+/\D', string)
        if slash and slash.group(0) != '24/24' and slash.group(0) != '24/7':
            return 'Mặt ngõ'
        return 'Mặt phố' # return 'Có mặt phố'
    return None 

df['des + title'] = df['title'] + '. ' + df['description']
df['mat_ngo'] = df.apply(new_define_mat_pho_mat_ngo, axis = 1)
df['mat_ngo'].value_counts(dropna=False)

# df['mat_ngo'] = df['description'].apply(new_define_mat_pho_mat_ngo) # Cái này là để xem có bao nhiêu cái là các trường hợp của mặt ngõ
# mask = df['mat_ngo'].isna()
# df.loc[mask, 'mat_ngo'] = df.loc[mask, 'title'].apply(new_define_mat_pho_mat_ngo) # Apply extract hẻm ngách kiệt cho title nếu không có trong description
# df['mat_ngo'].value_counts(dropna=False)

mat_ngo
Mặt ngõ    13471
None       11678
Mặt phố     2034
Drop          25
Name: count, dtype: int64

In [104]:
df['index'] = df.index

def find_model(row):
    string = row['description'].lower()
    result = re.findall('(?:nhà(?:\s\S+){0,2} phố|nhà(?:\s\S+){0,2} mặt phố|nhà(?:\s\S+){0,2} mặt đường|mặt phố|mặt đường|mặt tiền phố|\Wmt phố|\Wmt đường|mặt tiền đường|\Wmtd\W|\Wmtđ\W|trục chính|phân lô phố)', string)
    if len(result) > 1:
        return len(result)
    return None

df_copy = df.copy()
df_copy['pho'] = df_copy.apply(find_model, axis = 1)
df_copy['pho'].value_counts()

pho
2.0     894
3.0     187
4.0      31
5.0      10
8.0       3
7.0       3
6.0       3
10.0      1
9.0       1
Name: count, dtype: int64

In [105]:
df_new = df_copy.copy()
df_new[(df_new['pho'].notna()) & (df_copy['mat_ngo'].isna())]['pho'].value_counts()

pho
2.0     684
3.0     142
4.0      28
5.0       7
8.0       3
7.0       3
6.0       3
10.0      1
9.0       1
Name: count, dtype: int64

## Check mặt phố

In [ ]:
def find_pho(row): # Khi ghép vào với code bên trên thì 3 dòng trên cùng sẽ bị loại bỏ
    if pd.notna(row['mat_ngo']): 
        return row['mat_ngo']
    string = row['description']
    string = string.lower()
    #------ TH6: Phố ------
    find_pho_keyword = re.findall(r'(?:\S+\s){0,5}(?:nhà (?:mặt)? (?:phố|đường)|mặt phố|mặt đường|mặt tiền đường|mặt tiền phố|nhà phố|\Wmp\W)\s*(?:\S+\s?){0,4}?(?=[.,-])', string)
    if find_pho_keyword != []:
        street_name = []
        for key in find_pho_keyword:
            if re.search(r'cách|ra|gần|liên hệ|hơn|như|sát|giáp|\d{3,}\s*[*]{1,3}|\d{3,}\s*\d{3,}', key):
                continue
            else:
                street = re.search(r'(?:\S+\s){0,5}(?:nhà (?:mặt)? (?:phố|đường)|mặt phố|mặt đường|mặt tiền đường|mặt tiền phố|nhà phố|\Wmp\W)\s*((?:\S+\s?){0,4}?(?=[.,-]))', string)
                if len(street.group(1)) > 0:
                    street_name.append(street.group(1))
            if len(street_name) > 0:
                return street_name
            return find_pho_keyword
            # return 'mặt phố'
        # return None
    # not_road = 'trường(?!\s*sa)|học|chợ|siêu thị|vincom|aeon|lotte|biển|sông|\Whồ\W|bệnh viện|ubnd \
    #             |công viên|\Wcv\W|hẻm|hxh|ngõ|chung cư|\Wcc\W|vườn|trung tâm|khu đô thị|\Wkđt\W \
    #             |\Wkdt\W|vinmart|winmart|vin|mall|tttm|bigc|\Wgo\W|gigamall|sân bay|quận|q(?:\d+) \
    #             |thành phố|\Wtp|huyện|thị xã|thị trấn|tx|bến xe|bx|xanh|cửa|vào'
    # duong = f'đường|(?<!thành\s)phố|mặt đường|mặt phố|mp|vành đai|đại lộ|đl|mặt tiền (?!.*?(?:{not_road}))|mt (?!.*?(?:{not_road}))|trục chính|quốc lộ|ql|qlo|tỉnh lộ|tl|cầu(?!\s*giấy)|ngã tư|ngã ba|ngã 4|ngã 3|nhà'
    # duong_khong_nha = 'đường|(?<!thành\s)phố|mặt đường|mặt phố|mp|vành đai|đại lộ|đl|mặt tiền|mt|trục chính|quốc lộ|ql|qlo|tỉnh lộ|tl|cầu(?!\s*giấy)|ngã tư|ngã ba|ngã 4|ngã 3'
    
    # cach_duong = re.search(rf'(?<!phong\s)cách\s*(?:\S+\s){{0,5}}(?:{duong})\s*(?:\S+\s){{0,5}}(?:\d+(?:[.,]d+)?\s?k?m|căn|nhà|bước|đi|di chuyển|(?:\d+)\s*(?:p|phút))', string) # cách mặt tiền đường phạm văn đồng 30m/vài bước chân/một nhà/vài phút di chuyển
    # digit_ra_duong = re.search(rf'(?:\d+(?:[.,]d+)?\s?k?m|bước|căn|nhà|đi|(?:\d+)\s*(?:p|phút))\s(?:\S+\s){{0,4}}(?:ra|tới|đến)\s(?:\S+\s){{0,2}}(?:{duong})', string) #10m/vài bước chân/một nhà ra mặt tiền đường
    # ra_duong_digit = re.search(rf'(?:ra|tới|đến) (?:\S+\s){{0,2}}(?:{duong})\s*(?:\S+\s){{0,3}}(?:\d+(?:[.,]d+)?\s?k?m|bước|căn|nhà|đi|(?:\d+)\s*(?:p|phút))', string) # ra cầu Sài Gòn chỉ 10m
    # cach_not_forbid = re.search(rf'(?<!phong\s)cách\s*(?!.*?(?:{not_road}))(?:(?!{not_road})\S+\s){{0,5}}(?:\d+(?:[.,]d+)?\s?k?m|căn|nhà|bước|đi|di chuyển|(?:\d+)\s*(?:p|phút))', string)
    # ra_not_forbid = re.search(rf'(?:\d+(?:[.,]d+)?\s?k?m|bước|căn|nhà|đi|(?:\d+)\s*(?:p|phút))\s(?:\S+\s){{0,3}}(?:ra|tới|đến)\s(?!.*?(?:{not_road}))(?:(?!{not_road})\S+\s){{0,5}}', string) #10m/vài bước chân/một nhà ra Phạm Văn Đồng
    # # if (cach_duong and re.search(rf'{not_road}', cach_duong.group(0)) is None) or (digit_ra_duong and re.search(rf'{not_road}', digit_ra_duong.group(0)) is None) or (ra_duong_digit and re.search(rf'{not_road}', ra_duong_digit.group(0)) is None):
    # if cach_duong or digit_ra_duong: 
    #     return 'ngõ cách đường'
    # if ra_duong_digit:
    #     start = ra_duong_digit.span()[0] - 7 if ra_duong_digit.span()[0] >= 7 else 0
    #     stop = ra_duong_digit.span()[1]
    #     if re.search(r'(?:ngoài ra|ra vào|đưa ra|đua ra)', string[start:stop]) is None:
    #         return 'ra đường'
    # if cach_not_forbid and re.search(rf'{not_road}', cach_not_forbid.group(0)) is None:
    #     return 'cách không phải đường'
    # if ra_not_forbid:# and re.search(rf'(?:ngoài ra|ra vào|đưa ra|đua ra|{not_road})', ra_not_forbid.group(0)) is None:
    #     start = ra_not_forbid.span()[0] - 7 if ra_not_forbid.span()[0] >= 7 else 0
    #     stop = ra_not_forbid.span()[1]
    #     if re.search(rf'(?:ngoài ra|ra vào|đưa ra|đua ra|{not_road})', string[start:stop]) is None:
    #         return 'ra không phải đường'
    #     # return 'Ra không phải đường'
    # close_to_duong = re.search(rf'(?:gần|giáp|sát)\s(?:\S+\s){{0,2}}(?:{duong_khong_nha})', string)
    # if close_to_duong:
    #     return 'gần đường nè'
    # #------ TH7: Các trường hợp còn lại ------
    return None

df['pho'] = df['mat_ngo'].copy()
df['pho'] = df.apply(find_pho, axis=1)
df['pho'].value_counts(dropna=False)

In [ ]:
import time
from geopy.geocoders import Nominatim
import random
from geopy.exc import GeocoderTimedOut, GeocoderServiceError

def ngo(row):
    if pd.notna(row['description']):
        des = row['description'].lower()
    else:
        des = ''

    if pd.notna(row['title']):
        title = row['title'].lower()
    else:
        title = ''

    string = title + '. ' + des
    return find_pattern(string, row['latitude'], row['longitude'])

def find_pattern(string, lat, lon):
    streets = 'phố|mặt|mp |mt |đường|ô tô|ôtô|o tô|otô|o to|oto|ô to|ôto|xe hơi|đại lộ|\Wđl|\Wdl|tỉnh lộ|\Wtl|quốc lộ|\Wql|ngã tư|ngã 4|ngã ba|ngã 3|vành đai|cao tốc|cầu(?!\sgiấy)|trục (?:\S+\s){0,2}chính|ga|hương lộ|\Whl\W'
    main_road = 'nhà(?:\s\S+){0,2} phố|nhà(?:\s\S+){0,2} mặt phố|nhà(?:\s\S+){0,2} mặt đường|mặt phố|mặt đường|mặt tiền phố|mt phố| mt đường|mặt tiền đường|trục chính|phân lô phố'
    not_streets = 'trường(?!\s*sa)|học|đh|chợ|siêu thị|vincom|aeon|lotte|biển|bờ biển|bãi biển|sông|bờ sông|\Whồ\W|bờ \Whồ\W|bệnh viện|ubnd \
                 |công viên|\Wcv\W|hẻm|hxh|ngõ|chung cư|\Wcc\W|vườn|trung tâm|khu đô thị|\Wkđt\W \
                 |\Wkdt\W|vinmart|winmart|vin|mall|tttm|bigc|big c|\Wgo\W|gigamall|sân bay|quận|q(?:\d+) \
                 |thành phố|\Wtp|huyện|thị xã|thị trấn|tx|bến xe|bx|xanh|cửa|vào|đền|chùa|đình|bãi'
    cars_words = 'ô tô|ôtô|o tô|otô|o to|oto|ô to|ôto|xe hơi|xe tải'
    num_words = 'một|hai|ba|bốn|năm|sáu|bảy|bẩy|tám|chín|mười|mười một|mười hai|mười ba|mười bốn|mười lăm|mười năm|mười sáu'

    vai = re.search(rf'vài (?:bước|căn|nhà|phút|trăm|chục)\s(?:\S+\s){{0,5}}(?:{streets})', string)
    gan = re.search(rf'(?:gần|giáp|sát|liền kề|cạnh) (?:\S+\s){{0,3}}(?:{streets})', string) # bỏ 'ngay'
    cach_streets = re.search(rf'cách (?:\S+\s){{0,2}}(?:{streets})', string)
    duong = re.search(r'đường (?:to|rộng|bự|đẹp|nhựa|thoáng|thông|phân lô|ô bàn cờ|\d+|xe tải|xe hơi|(?:xe\s)?ô tô|(?:xe\s)?ôtô|(?:xe\s)?ô to|(?:xe\s)?ôto|(?:xe\s)?o tô|(?:xe\s)?otô|(?:xe\s)?o to|(?:xe\s)?oto|trước nhà|trước mặt|vào|trục chính)', string)
    cars = re.search(rf'(?:(?:\d+|{num_words})m?\s*)?(?:{cars_words}) (?:\S+\s){{0,2}}(tránh|đỗ(?!\strong)|đổ|(?<!ra\s)vào|né)', string)
    ra_1 = re.search(rf'(?:\d+k?m?|nhà|bước|bước chân|căn|phút|\d+p|mét|thông|kết nối)\s(?:ra|sang)\s(?:\S+\s){{0,3}}(?:{streets})', string)
    ra_2 = re.search(rf'\W(?:ra|sang)\s(?:{streets}(?!như|trọng))\s(?:\S+\s){{0,7}}(?:\d+k?m?|nhà|bước|bước chân|căn|phút|\d+p|mét|thông)', string)
    ra_3 = re.search(rf'\Wra (?:\S+\s){{0,3}}(?:{streets})', string)
    cach_notstreets = re.search(r'cách (?:\S+\s){0,4}', string) # xong xét xem có bị vướng mấy cái không phải không nha
    gan_notstreets = re.search(r'gần (?!\S+(?:tr|tỷ|triệu|m²|m2)\W\s)(?:\S+\s){0,4}', string)
    ra_notstreets = re.search(rf'(?<!tạo)(?<!nhìn)(?<!view)(?<!làm)(?<!đâu)(?<!mới)(?<!tìm)(?<!ngoài)(?<!mở)(?<!vào)(?<!bán)(?<!đua)(?<!đưa)\Wra (?:(?!m²|m2|giá|nhanh)\S+\s){{0,3}}(?!m²|m2|giá|nhanh)', string)
    # connect = re.search(rf'kết nối (?:\S+\s){{0,2}}(?:{streets})', string)
    kdc = re.search(r'(?<!gần\s)(?<!hàng xóm\s)(?<!đối diện\s)(?:\S+\s){0,2}(?:khu vip|khu dc|khu tái định cư|khu dân cư|kdc|khu nhà|nội bộ|nội khu|khu biệt thự|khu)', string) # tại sao không thêm khu vào vậy?
    pho = re.search(main_road, string)

    if vai:
        if pho: 
            return 'Vài mà có mặt phố'
        return 'Vài'
    if cach_streets:
        if pho:
            return 'Cách đường có mặt phố'
        return 'Cách đường'
    if (ra_1 and not re.search(not_streets, ra_1.group(0))) or (ra_2 and not re.search(not_streets, ra_2.group(0))):
        if pho:
            return 'Ra đường có mặt phố'
        return 'Ra đường'
    if (ra_3 and not re.search(not_streets, ra_3.group(0))):
        return 'Ra cái gì cũng được'
    if gan and re.search(not_streets, gan.group(0)) is None and re.search(r'm2|m²', gan.group(0)) is None:
        if pho:
            return 'Gần có mặt phố'
        return 'Gần'
    if kdc:
        if pho:
            return 'Khu dân cư có mặt phố'
        return 'Khu dân cư'
    if duong:
        if pho:
            return 'Đường vào có mặt phố'
        return 'Đường vào to rộng'
    if cars:
        if pho:
            return 'Ô tô có mặt phố'
        return 'Ô tô'
    if cach_notstreets and re.search(not_streets, cach_notstreets.group(0)) is None:
        if pho:
            return 'Ngõ cách không đường có mặt phố'
        return 'Ngõ cách không đường'
    if gan_notstreets and re.search(not_streets, gan_notstreets.group(0)) is None:
        if pho:
            return 'Ngõ gần không đường có mặt phố'
        return 'Ngõ gần không đường'
    if ra_notstreets and re.search(not_streets, ra_notstreets.group(0)) is None:
        if pho:
            return 'Ngõ ra không đường có mặt phố' # đã chỉnh để chỉ có ngõ
        return 'Ngõ ra không đường'
    # if connect:
    #     return 'Kết nối thông hehe'
    if pho:
        return 'Có mặt phố'
    return None

In [40]:
mask = df['mat_ngo'].isna()
df['new_mat_ngo'] = None
df.loc[mask, 'new_mat_ngo'] = df.loc[mask].apply(ngo, axis = 1)
df['new_mat_ngo'].value_counts(dropna=False)

new_mat_ngo
None                               14725
Khu dân cư                          4030
Khu dân cư có mặt phố               1300
Gần                                 1231
Đường vào to rộng                   1040
Cách đường                          1002
Cách đường có mặt phố                638
Gần có mặt phố                       518
Đường vào có mặt phố                 422
Ra đường                             419
Có mặt phố                           344
Ra đường có mặt phố                  305
Ô tô                                 257
Ngõ gần không đường                  189
Vài                                  188
Vài mà có mặt phố                    152
Ra cái gì cũng được                  132
Ngõ cách không đường                 101
Ngõ ra không đường                    61
Ngõ gần không đường có mặt phố        44
Ngõ cách không đường có mặt phố       25
ô tô tránh                            18
ô tô vào                              15
ô tô đỗ                               11
ôtô 

In [133]:
string = df.loc[116]['description'].lower()
print(string)
print('\n')
# not_road = 'trường(?!\s*sa)|học|chợ|siêu thị|vincom|aeon|lotte|biển|sông|hồ|bệnh viện|ubnd \
#             |công viên|cv|hẻm|hxh|ngõ|chung cư|cc|vườn|trung tâm|khu đô thị|kđt \
#             |kdt|vinmart|winmart|vin|mall|tttm|bigc|go|gigamall|sân bay|quận|q(?:\d+) \
#             |thành phố|tp|huyện|thị xã|thị trấn|tx|bến xe|bx|xanh|cửa|vào'
not_road = 'trường(?!\s*sa)|học|chợ|siêu thị|vincom|aeon|lotte|biển|sông|\Whồ\W|bệnh viện|ubnd \
            |công viên|\Wcv\W|hẻm|hxh|ngõ|chung cư|\Wcc\W|vườn|trung tâm|khu đô thị|\Wkđt\W \
            |\Wkdt\W|vinmart|winmart|vin|mall|tttm|bigc|\Wgo\W|gigamall|sân bay|quận|q(?:\d+) \
            |thành phố|\Wtp|huyện|thị xã|thị trấn|tx|bến xe|bx|xanh|cửa|vào'
duong = f'đường|(?<!thành\s)phố|mặt đường|mặt phố|mp|vành đai|đại lộ|đl|mặt tiền (?!.*?(?:{not_road}))|mt (?!.*?(?:{not_road}))|trục chính|quốc lộ|ql|qlo|tỉnh lộ|tl|cầu(?!\s*giấy)|ngã tư|ngã ba|ngã 4|ngã 3|nhà'
duong_khong_nha = 'đường|(?<!thành\s)phố|mặt đường|mặt phố|mp|vành đai|đại lộ|đl|mặt tiền|mt|trục chính|quốc lộ|ql|qlo|tỉnh lộ|tl|cầu(?!\s*giấy)|ngã tư|ngã ba|ngã 4|ngã 3'

# Test 'ngõ cách đường'
cach_duong = re.search(rf'(?<!phong\s)cách\s*(?:\S+\s){{0,5}}(?:{duong})\s*(?:\S+\s){{0,5}}(?:\d+(?:[.,]d+)?\s?k?m|căn|nhà|bước|đi|di chuyển)', string) # cách mặt tiền đường phạm văn đồng 30m/vài bước chân/một nhà/vài phút di chuyển
digit_ra_duong = re.search(rf'(?:\d+(?:[.,]d+)?\s?k?m|bước|căn|nhà|đi)\s(?:\S+\s){{0,4}}(?:ra|tới|đến)\s(?:\S+\s){{0,2}}(?:{duong})', string) #10m/vài bước chân/một nhà ra mặt tiền đường
ra_duong_digit = re.search(rf'(?:ra|tới|đến) (?:\S+\s){{0,2}}(?:{duong})\s*(?:\S+\s){{0,3}}(?:\d+(?:[.,]d+)?\s?k?m|bước|căn|nhà|đi)', string) # ra cầu Sài Gòn chỉ 10m
print(f'cach_duong: {cach_duong}')
# print(f'search for not road: {re.search(rf"{not_road}", cach_duong.group(0))}')
print(f'digit_ra_duong: {digit_ra_duong}')
print(f'ra_duong_digit: {ra_duong_digit}')
# print(re.search(rf'(?:ngoài ra|ra vào|đưa ra|đua ra)', ra_duong_digit.group(0)))

# Test 'cách không phải đường'
cach_not_forbid = re.search(rf'(?<!phong\s)cách\s*(?!.*?(?:{not_road}))(?:(?!{not_road})\S+\s){{0,5}}(?:\d+(?:[.,]d+)?\s?k?m|căn|nhà|bước|đi|di chuyển)', string)
print(f'cach_not_forbid: {cach_not_forbid}')

# Test 'ra không phải đường'
ra_not_forbid = re.search(rf'(?:\d+(?:[.,]d+)?\s?k?m|bước|căn|nhà|đi)\s(?:\S+\s){{0,3}}(?:ra|tới|đến)\s(?!.*?(?:{not_road}))(?:(?!{not_road})\S+\s){{0,5}}', string) #10m/vài bước chân/một nhà ra Phạm Văn Đồng
print(f'ra_not_forbid: {ra_not_forbid}')

# Test 'gần đường nè'
close_to_duong = re.search(rf'(?:gần|giáp|sát)\s(?:\S+\s){{0,2}}(?:{duong_khong_nha})', string)
print(f'close_to_duong: {close_to_duong}')

bán luôn nhà đẹp giá tốt, ô tô đỗ cửa phú lương, hà đông.

không mua căn này thì mua căn nào nữa.
diện tích 33m² - thiết kế 5 tầng, 3pn, đầy đủ công năng.

giá: 4,95 tỷ còn thương lượng. chủ nhà vui tính, thiện chí bán.

giao thông thuận lợi: 5p ra đường ql21b, gần ngay trường đại học đại nam, xung quanh gần các trường học. ô tô đỗ cửa, 5m ra ô tô tránh. vị trí siêu đỉnh.

sổ đỏ nở hậu chính chủ. pháp lý chuẩn chỉnh.


cach_duong: None
digit_ra_duong: None
ra_duong_digit: None
cach_not_forbid: None
ra_not_forbid: <re.Match object; span=(339, 364), match='5m ra ô tô tránh. vị trí '>
close_to_duong: None


## Hẻm (đã bao gồm hẻm xe hơi, hẻm xe tải, sẹc đồ)

Chốt lại: hẻm vẫn dùng phương pháp loại trừ, cái nào dính vào trường hợp bị loại thì thôi (là cái đoạn như|hơn đó)

Sẹc/HXH/HXT quất hết mặt ngõ

In [157]:
import re

def mat_ngo(string):
    string = string.lower()
    ngo = re.findall('ngõ', string)
    cua_ngo = re.search(r'(?<!đỗ\s)(?:cửa ngõ|cưa ngõ)', string)
    if ngo:
        if not cua_ngo:
            pass
        elif cua_ngo and len(ngo) == 1:
            return None
    if re.search(r'ngõ:? (?:rất|cực|siêu|thông|cụt|(\w+\s){0,1}nông|rộng|sh|bên hông|hông|vào|thoáng|ô tô|ôtô|ô to|ôto|o tô|otô|o to|oto|to|trước|trc|\d+|thẳng|sạch|đẹp|xe|lớn|ba gác|cực|sau|riêng|vip|phân lô|kinh doanh|gần|phố|ngách|đi|ngắn|(?:\w+\s){0,1}nhựa)|mặt ngõ|trong ngõ|đầu ngõ|nhà ngõ', string):
        return 'Mặt ngõ'
    return None


def mat_hem(string):
    string = string.lower()
    if re.search(r'hxh|hxt|sẹc|sẹt|xẹc|xẹt| sec ', string):
        return 'hẻm xe tải/hơi/sẹc'
    if re.search(r'(?<!như|hơn)(?:\S+\s){0,2}hẻm\s?:? (?:cực|hiện trạng|hiện hữu|siêu|vào|vô cùng|rất|gần|hơn|hiếm|xh|hông|đường|rộng|\d+|xe|kinh doanh|kd|xi măng|vip|trước|sau|sạch|lớn|to|suôn|rộng|đẹp|thông|thẳng|ô|o|ôt|ot|nhựa|ba gác|thoáng|cụt|nội bộ|an ninh|dân trí|bê tông|đối diện|bagac|văn|ngắn|chuẩn|yên tĩnh|(?:\w+\s){0,1}nhựa|bên)|hxh|nhà hẻm|mặt hẻm|mặt tiền hẻm|nhà trong hẻm', string):
        return 'hẻm'
    return None

df['mat_ngo'] = df['description'].apply(mat_ngo)
df['mat_hem'] = df['description'].apply(mat_hem)
df['mat_hem'].value_counts()

mat_hem
hẻm                   5170
hẻm xe tải/hơi/sẹc     821
Name: count, dtype: int64

## Kiệt

Chốt lại: cũng là phương pháp loại trừ

In [ ]:
def extract_kiet(string):
    string = string.lower()
    kiet = re.search(r'(?<!lý\sthường\s)(?<!võ\svăn\s)(?<!nhân\s)(?<!phạm\s)kiệt(?!\stác)', string)
    # kiet =  re.findall(r'(?:\S+\s+){0,5}kiệt (?:\S+\s+){0,5}', string)
    # if kiet != []:
    #     for kiet_phrases in kiet:
    #         if ('lý thường kiệt' in kiet_phrases or 'võ văn kiệt' in kiet_phrases or 'kiệt tác' in kiet_phrases):
    #             continue
    #         else:
    #             return kiet_phrases
    # return None
    if kiet:
        return 'Kiệt'
#     return None

def extract_kiet_new(string): # OFFICIAL
    string = string.lower()
    kiet = re.search(r'(?<!lý\sthường\s)(?<!võ\svăn\s)(?<!nhân\s)(?<!phạm\s)kiệt(?!\stác)\s', string)
    # kiet =  re.findall(r'(?:\S+\s+){0,5}kiệt (?:\S+\s+){0,5}', string)
    # if kiet != []:
    #     for kiet_phrases in kiet:
    #         if ('lý thường kiệt' in kiet_phrases or 'võ văn kiệt' in kiet_phrases or 'kiệt tác' in kiet_phrases):
    #             continue
    #         else:
    #             return kiet_phrases
    # return None
    if kiet:
        return 'Kiệt'
    if re.search(r'mặt kiệt|măt kiệt|mat kiệt|đất kiệt|nhà kiệt', string):
    # if 'mặt kiệt' in string or 'măt kiệt' in string or 'mat kiệt' in string  or 'đất kiệt' in string or 'nhà kiệt' in string:
        return 'Kiệt'
    return None

# def extract_kiet_ver3(string):
#     string = string.lower()
#     pattern = r'(?<!lý\sthường\s)(?<!võ\svăn\s)(?<!nhân\s)(?<!phạm\s)kiệt (?:ô tô|ôtô|ô to|ôto|o tô|otô|oto|o to|(\d+)|rộng|thông|thoáng|hông|bên hông)|mặt kiệt|măt kiệt|mat kiệt'
#     if re.search(pattern, string):
#         return 'kiệt'
#     return None

# def extract_kiet_phrases(string):
#     string = string.lower()
#     kiet = re.findall(r'(?:\S+\s+){0,5}kiệt (?:\S+\s+){0,5}', string)
#     if kiet != []:
#         return kiet
#     return None

df['kiet'] = df['description'].apply(extract_kiet)
df['kiet_new'] = df['description'].apply(extract_kiet_new)
# df['kiet_phrases'] = df['description'].apply(extract_kiet_phrases)
# df['kiet_ver3'] = df['description'].apply(extract_kiet_ver3)

In [26]:
def extract_inside_alley(string):
    string = string.lower()
    if re.search(r'(\S+\s)\d+/\d+/\d+', string):
        return re.search(r'(\S+\s)\d+/\d+/\d+', string).group(0)
    return None

df['ngach'] = df['description'].apply(extract_inside_alley)

## Ngách

Loại trừ các trường hợp ngóc ngách, còn đâu thì oke

In [25]:
from rapidfuzz import fuzz

def extract_ngach(string):
    string = string.lower()
    # result = re.search(r'(?:\S+\s+){0,5}(\S+\sngách)\s*(?:\S+\s+){0,5}', string)
    # if result:
    #     if result.group(1).startswith('ng'):
    #         if fuzz.ratio(result.group(1), 'ngóc ngách') >= 90:
    #             return f'Original:{result.group(1)} but now is None'
    #         return result.group(1)
    #     return result.group(1)
    # return None
    result = re.findall(r'(?:\S+\s+){0,5}(\S+\sngách)\s*(?:\S+\s+){0,5}', string)
    if result != []:
        for i in result:
            if i.startswith('ng'):
                if fuzz.ratio(i, 'ngóc ngách') >= 90:
                    continue
                return i
            return i
    return None

df['ngach'] = df['description'].apply(extract_ngach)

In [44]:
def find_pho(string):
    string=string.lower()
    
    ngo = re.findall(r'(?:(?<!hơn\s)(?<!như\s)(?<!giá\s)(?:\S+\s*){1,3})ngõ', string)
    cua_ngo = re.search(r'(?<!đỗ\s)(?:cửa ngõ|cưa ngõ|một mặt ngõ|1 mặt ngõ|một ngõ|1 ngõ)', string)
    if ngo:
        if not cua_ngo:
            return None
        elif cua_ngo and len(ngo) == 1:
            pass
        else:
            return None
    # if re.search(r'ngõ (?:thông|nông|đẹp|sâu|sạch|thoáng|vào|trước|sau|rộng|to|bự|xe|ô tô|ôtô|ô to|ôto|o tô|otô|o to|oto|ba|3|bagac|phân lô|thẳng|kinh doanh|kd)|mặt ngõ|đầu ngõ|nhà ngõ', string):
    #     return None
    find_pho_keyword = re.findall(r'(?:\S+\s){0,5}(?:nhà (?:mặt)? (?:phố|đường)|mặt phố|mặt đường|mặt tiền đường|mặt tiền phố|nhà phố|mp)\s*(?:\S+\s){0,5}', string)
    if find_pho_keyword != []:
        for key in find_pho_keyword:
            if re.search(r'cách|ra|gần|liên hệ|hơn|như|sát|giáp|\d{3,}\s*[*]{1,3}|\d{3,}\s*\d{3,}', key):
                continue
            return find_pho_keyword
        return None
    
    duong = 'đường|phố|mặt đường|mặt phố|mp|vành đai|đại lộ|đl|mặt tiền|mt|trục chính|quốc lộ|ql|qlo|tỉnh lộ|tl|cầu|ngã tư|ngã ba|ngã 4|ngã 3|nhà'
    cach_duong = re.search(rf'cách\s*(?:\S+\s){{0,5}}(?:{duong})\s*(?:\S+\s){{0,5}}(?:\d+|nhà|bước chân)', string) # cách mặt tiền đường phạm văn đồng 30m/vài bước chân/một nhà
    ra_duong = re.search(rf'(?:\d+m|bước chân|nhà)\sra\s(?:\S+\s){{0,2}}(?:{duong})', string) #10m/vài bước chân/một nhà ra mặt tiền đường
    if cach_duong or ra_duong:
        return 'Ngõ cách đường'
    return None    
    
df['mat_pho'] = df['description'].apply(find_pho)

# Test cleaned 

In [2]:
import pandas as pd

pd.set_option('display.max_colwidth', None)
pd.set_option('display.max_rows', None)
listing_details = pd.read_csv('output/listing_details.csv')
listing_details.rename(columns={'url': 'Nguồn thông tin'}, inplace=True)

cleaned_old = pd.read_excel('output/listing_details_cleaned_old.xlsx')
cleaned_old.info()
cleaned_old = pd.merge(cleaned_old, listing_details, how='left', on='Nguồn thông tin')

cleaned = pd.read_excel('output/listing_details_cleaned.xlsx')
cleaned.info()
cleaned = pd.merge(cleaned, listing_details, how='left', on='Nguồn thông tin')

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 412 entries, 0 to 411
Data columns (total 32 columns):
 #   Column                                Non-Null Count  Dtype  
---  ------                                --------------  -----  
 0   Tỉnh/Thành phố                        412 non-null    object 
 1   Thành phố/Quận/Huyện/Thị xã           412 non-null    object 
 2   Xã/Phường/Thị trấn                    412 non-null    object 
 3   Đường phố                             412 non-null    object 
 4   Chi tiết                              412 non-null    object 
 5   Nguồn thông tin                       412 non-null    object 
 6   Tình trạng giao dịch                  412 non-null    object 
 7   Thời điểm giao dịch/rao bán           412 non-null    object 
 8   Thông tin liên hệ                     0 non-null      float64
 9   Giá rao bán/giao dịch                 412 non-null    int64  
 10  Giá ước tính                          412 non-null    int64  
 11  Loại đơn giá (đ/m2 

In [9]:
df_result = cleaned_old[~cleaned_old['Nguồn thông tin'].isin(cleaned['Nguồn thông tin'])]
df_result[['Độ rộng ngõ/ngách nhỏ nhất (m)', 'Nguồn thông tin']]

Độ rộng ngõ/ngách nhỏ nhất (m)  \
15                              5.0   
30                              4.0   
34                              5.0   
57                              5.0   
72                              5.0   
75                              5.0   
86                              5.0   
97                              5.0   
115                             4.0   
117                             4.0   
128                             5.0   
136                             4.0   
140                             7.5   
146                             4.0   
148                             5.0   
150                             4.0   
151                             4.0   
155                             4.0   
157                             4.0   
160                             4.0   
168                             5.0   
174                             3.5   
183                             5.0   
188                             7.5   
194                             4.0   
198                             5.0   
207                             4.0   
223                             5.0   
227                             4.0   
230                             4.0   
236                             4.0   
237                             4.0   
239                             4.0   
240                             5.0   
242                             4.0   
252                             7.5   
261                             5.0   
262                             5.0   
265                             3.0   
266                             4.0   
290                             1.5   
299                             4.0   
301                             4.0   
303                             3.5   
322                             4.0   
324                             5.0   
336                             5.0   
341                             5.0   
346                             5.0   
358                             1.5   
379                             4.0   
380                             5.0   
390                             5.0   
395                             4.0   
396                             4.0   
404                             2.5   
409                             4.0   

                                                                                                                                                                   Nguồn thông tin  
15                                 https://batdongsan.com.vn/ban-nha-rieng-pho-hong-tien-phuong-bo-de/ban-so-65m2-m-6m-lo-goc-7-tang-thang-may-dang-cho-thue-60tr-thang-pr43891309  
30              https://batdongsan.com.vn/ban-nha-rieng-duong-khuong-trung-phuong-khuong-trung/sieu-re-53m2x4t-gan-pho-gan-nga-tu-so-gia-7-95-ty-cam-ket-that-gia-chuan-pr44301330  
34                https://batdongsan.com.vn/ban-nha-rieng-duong-xuan-la-phuong-xuan-la/12-ty-hon-ban-ngoai-giao-doan-dinh-lo-goc-ngo-nong-o-to-gan-55m2-gan-5m-mat-tien-pr44327370  
57                  https://batdongsan.com.vn/ban-nha-rieng-duong-phan-ke-binh-phuong-cong-vi/mat-ngo-25m-o-to-tranh-lo-o-ban-co-ngo-thong-kinh-doanh-so-cc-o-ngay-38m2-pr44315310  
72                                             https://batdongsan.com.vn/ban-nha-rieng-duong-tu-hiep-xa-tu-hiep/-dep-2-mat-thoang-trung-tam-35m-x-4-tang-chi-nhinh-7-ty-pr44305757  
75                                                     https://batdongsan.com.vn/ban-nha-rieng-duong-nguyen-chanh-phuong-trung-hoa-4/ban-c4-phan-lo-ngo-2-oto-ngo-thong-pr44221747  
86                     https://batdongsan.com.vn/ban-nha-rieng-duong-xuan-la-phuong-xuan-la/re-t-18-ty-hon-ban-ltay-ho-ngoai-giao-doan-60m2-5-tang-o-to-tranh-thang-may-pr44300691  
97              https://batdongsan.com.vn/ban-nha-rieng-duong-nguyen-chi-thanh-phuong-lang-thuong/co-102-xay-moi-lo-goc-5-tang-co-thang-may-ngo-thong-20m-ra-o-to-tranh-pr44184736  
115                                        https://batdongsan.com.vn/ban-nha-rieng-pho-nguyen-xi-phuong-13-7/-xe-

In [18]:
import re
from src.config import ALLEY_WIDTH

patterns = '|'.join(ALLEY_WIDTH.keys())
print(patterns)
text = cleaned_old.loc[36]['title'].lower() + '. ' + cleaned_old.loc[36]['description'].lower()
print(re.findall(rf'{patterns}', text, re.IGNORECASE))

ngõ xe máy|hẻm xe máy|ngách xe máy|ngõ ba gác|hẻm ba gác|ngõ bagac|xe máy tránh|ba gác tránh|3 gác tránh|bagac tránh|ngõ ô tô|ngõ ôtô|ngõ ô to|ngõ ôto|ngõ o tô|ngõ otô|ngõ oto|ngõ o to|hẻm ô tô|hẻm ôtô|hẻm ô to|hẻm ôto|hẻm o tô|hẻm otô|hẻm oto|hẻm o to|hem ô tô|hem ôtô|hem ô to|hem ôto|hem o tô|hem otô|hem oto|hem o to|hxh|hẻm xe hơi|hem xe hơi|ô tô vào nhà|ôtô vào nhà|ô to vào nhà|ôto vào nhà|o tô vào nhà|otô vào nhà|o to vào nhà|oto vào nhà|ô tô vào tận nhà|ôtô vào tận nhà|ô to vào tận nhà|ôto vào tận nhà|o tô vào tận nhà|otô vào tận nhà|o to vào tận nhà|oto vào tận nhà|ô tô đỗ cửa|ôtô đỗ cửa|ô to đỗ cửa|ôto đỗ cửa|o tô đỗ cửa|otô đỗ cửa|o to đỗ cửa|oto đỗ cửa|ô tô đỗ ngay cửa|ôtô đỗ ngay cửa|ô to đỗ ngay cửa|ôto đỗ ngay cửa|o tô đỗ ngay cửa|otô đỗ ngay cửa|o to đỗ ngay cửa|oto đỗ ngay cửa|ô tô tránh|ôtô tránh|ô to tránh|ôto tránh|o tô tránh|otô tránh|o to tránh|oto tránh|hẻm xe tải|hem xe tải|hxt|ngõ xe tải|xe tải tránh nhau
[]


In [19]:
new_df = pd.read_excel('output/listing_details_cleaned.xlsx')
new_df_result = cleaned_old[~cleaned_old['Nguồn thông tin'].isin(new_df['Nguồn thông tin'])]
new_df_result[['Độ rộng ngõ/ngách nhỏ nhất (m)', 'Nguồn thông tin']]

Độ rộng ngõ/ngách nhỏ nhất (m)  \
15                              5.0   
30                              4.0   
34                              5.0   
57                              5.0   
72                              5.0   
75                              5.0   
97                              5.0   
117                             4.0   
118                             1.5   
128                             5.0   
140                             7.5   
146                             4.0   
148                             5.0   
150                             4.0   
151                             4.0   
155                             4.0   
157                             4.0   
168                             5.0   
174                             3.5   
183                             5.0   
188                             7.5   
194                             4.0   
198                             5.0   
207                             4.0   
223                             5.0   
227                             4.0   
230                             4.0   
236                             4.0   
237                             4.0   
239                             4.0   
240                             5.0   
252                             7.5   
261                             5.0   
262                             5.0   
265                             3.0   
266                             4.0   
290                             1.5   
299                             4.0   
301                             4.0   
303                             3.5   
305                             5.0   
306                             5.0   
311                             5.0   
322                             4.0   
324                             5.0   
336                             5.0   
341                             5.0   
346                             5.0   
358                             1.5   
380                             5.0   
390                             5.0   
395                             4.0   
396                             4.0   
404                             2.5   

                                                                                                                                                                   Nguồn thông tin  
15                                 https://batdongsan.com.vn/ban-nha-rieng-pho-hong-tien-phuong-bo-de/ban-so-65m2-m-6m-lo-goc-7-tang-thang-may-dang-cho-thue-60tr-thang-pr43891309  
30              https://batdongsan.com.vn/ban-nha-rieng-duong-khuong-trung-phuong-khuong-trung/sieu-re-53m2x4t-gan-pho-gan-nga-tu-so-gia-7-95-ty-cam-ket-that-gia-chuan-pr44301330  
34                https://batdongsan.com.vn/ban-nha-rieng-duong-xuan-la-phuong-xuan-la/12-ty-hon-ban-ngoai-giao-doan-dinh-lo-goc-ngo-nong-o-to-gan-55m2-gan-5m-mat-tien-pr44327370  
57                  https://batdongsan.com.vn/ban-nha-rieng-duong-phan-ke-binh-phuong-cong-vi/mat-ngo-25m-o-to-tranh-lo-o-ban-co-ngo-thong-kinh-doanh-so-cc-o-ngay-38m2-pr44315310  
72                                             https://batdongsan.com.vn/ban-nha-rieng-duong-tu-hiep-xa-tu-hiep/-dep-2-mat-thoang-trung-tam-35m-x-4-tang-chi-nhinh-7-ty-pr44305757  
75                                                     https://batdongsan.com.vn/ban-nha-rieng-duong-nguyen-chanh-phuong-trung-hoa-4/ban-c4-phan-lo-ngo-2-oto-ngo-thong-pr44221747  
97              https://batdongsan.com.vn/ban-nha-rieng-duong-nguyen-chi-thanh-phuong-lang-thuong/co-102-xay-moi-lo-goc-5-tang-co-thang-may-ngo-thong-20m-ra-o-to-tranh-pr44184736  
117                      https://batdongsan.com.vn/ban-nha-rieng-duong-phan-van-tri-phuong-11-7/ban-gia-ngop-2-95-ty-hxh-p-11-binh-thanh-dong-tien-20-eu-thang-so-rieng-pr44281701  
118                                                 https://batdongsan.com.vn/ban-nha-rieng-pho-bach-mai-phuong-bach-mai/6-35-ty-25-28m2-5-tang-ngo-nong-chua-lien-phai-pr44113135  
128                          https://batdongsan.c

In [25]:
new_new_df = pd.read_excel('output/listing_details_cleaned.xlsx')
yo = cleaned_old[~cleaned_old['Nguồn thông tin'].isin(new_new_df['Nguồn thông tin'])]
new_new_df[~new_new_df['Nguồn thông tin'].isin(new_df['Nguồn thông tin'])][['Độ rộng ngõ/ngách nhỏ nhất (m)', 'Nguồn thông tin']]

Độ rộng ngõ/ngách nhỏ nhất (m)  \
71                              5.0   
112                             4.0   
122                             5.0   
134                             7.5   
140                             4.0   
143                             4.0   
144                             4.0   
149                             4.0   
165                             3.5   
178                             7.5   
195                             4.0   
211                             5.0   
215                             4.0   
218                             4.0   
269                             1.5   
278                             4.0   
280                             4.0   
328                             1.5   
350                             5.0   
364                             4.0   
365                             4.0   
373                             2.5   

                                                                                                                                                                   Nguồn thông tin  
71                                                     https://batdongsan.com.vn/ban-nha-rieng-duong-nguyen-chanh-phuong-trung-hoa-4/ban-c4-phan-lo-ngo-2-oto-ngo-thong-pr44221747  
112                      https://batdongsan.com.vn/ban-nha-rieng-duong-phan-van-tri-phuong-11-7/ban-gia-ngop-2-95-ty-hxh-p-11-binh-thanh-dong-tien-20-eu-thang-so-rieng-pr44281701  
122                          https://batdongsan.com.vn/ban-nha-rieng-pho-xa-dan-phuong-kim-lien/chi-8-3-ty-ngo-2-oto-tranh-thong-thoang-y-chac-chan-bai-do-xe-kd-45m-5t-pr44263209  
134                                         https://batdongsan.com.vn/ban-nha-rieng-duong-thanh-xuan-25-phuong-thoi-an-1/hem-6m-khu-phan-lo-5-tang-tx25-52m-gia-3-75-ty-pr44239777  
140               https://batdongsan.com.vn/ban-nha-rieng-pho-trung-kinh-phuong-yen-hoa-2/chdv-ket-hop-o-20m-ra-2-thoang-tran-duy-hung-cau-giay-vi-tri-dac-dia-cho-thue-pr44312348  
143             https://batdongsan.com.vn/ban-nha-rieng-duong-nguyen-thai-son-phuong-3-20/90m2-60tr-th-hxh-ban-chdv-5-tang-thang-may-truc-le-lai-p3-ngay-dh-cong-nghiep-pr43688582  
144                                                     https://batdongsan.com.vn/ban-nha-rieng-duong-ho-ba-kien-phuong-15-3/hiem-hxh-tng-tang-3t-156m-ngang-n-4m-9-8ty-pr44336815  
149            https://batdongsan.com.vn/ban-nha-rieng-duong-nguyen-van-sang-phuong-tan-son-nhi/-ngay-p-gia-sieu-re-dt-61m2-2-g-hem-xe-hoi-thong-tu-phia-gia-chi-5-ty-6-pr44336755  
165  https://batdongsan.com.vn/ban-nha-rieng-duong-xuan-thuy-phuong-dich-vong-hau/lo-goc-3-mat-thoang-o-to-do-cua-kinh-doanh-dinh-ngo-thong-tran-thai-tong-so-vuong-dep-pr44232773  
178               https://batdongsan.com.vn/ban-nha-rieng-duong-no-trang-long-phuong-13-7/binh-thanh-4mx20-5m-a4-hem-xe-tai-gan-mat-tien-4-tang-moi-82m2-9-4-ty-con-bot-pr42778060  
195             https://batdongsan.com.vn/ban-nha-rieng-duong-giap-hai-xa-bat-trang-1/-dep-3-tang-59m-nhinh-9-ty-mat-ngo-o-to-tranh-kinh-doanh-no-hau-gan-cau-thanh-tri-pr44336350  
211                          https://batdongsan.com.vn/ban-nha-rieng-duong-xuan-la-phuong-xuan-la/chinh-chu-ban-ngo-2-o-to-tranh-pho-tay-ho-dt-150m2-mt-6m-2-tang-26-ty-pr44302224  
215                                                          https://batdongsan.com.vn/ban-nha-rieng-duong-ban-co-phuong-3-13/-6x12-4-lau-dang-thue-45-trieu-gia-18-9ty-pr44335025  
218                          https://batdongsan.com.vn/ban-nha-rieng-duong-le-quang-dinh-phuong-11-7/ban-hem-xe-hoi-11-binh-thanh-27m2-1-tret-lung-2-lau-2pn-master-3wc-pr44336203  
269                                             https://batdongsan.com.vn/ban-nha-rieng-pho-tran-xuan-soan-phuong-tan-hung-14/-3-tang-lien-ke-him-lam-quan-7-gia-2-3-ty-pr44335681  
278          https://batdongsan.com.vn/ban-nha-rieng-pho-vu-tong-phan-phuong-khuong-dinh/chat-lu-toa-chdv-70m2-7t-18-phong-kk-ngo-o-to-thong-kd-du-pccc-dong-tien-7-nam-pr44204464  
280                     https:

In [28]:
yo[['Độ rộng ngõ/ngách nhỏ nhất (m)', 'Nguồn thông tin']]

Độ rộng ngõ/ngách nhỏ nhất (m)  \
15                              5.0   
30                              4.0   
34                              5.0   
57                              5.0   
72                              5.0   
97                              5.0   
118                             1.5   
148                             5.0   
155                             4.0   
168                             5.0   
183                             5.0   
194                             4.0   
198                             5.0   
236                             4.0   
237                             4.0   
239                             4.0   
240                             5.0   
252                             7.5   
261                             5.0   
262                             5.0   
265                             3.0   
266                             4.0   
303                             3.5   
305                             5.0   
306                             5.0   
311                             5.0   
322                             4.0   
324                             5.0   
336                             5.0   
341                             5.0   
346                             5.0   
390                             5.0   

                                                                                                                                                                 Nguồn thông tin  
15                               https://batdongsan.com.vn/ban-nha-rieng-pho-hong-tien-phuong-bo-de/ban-so-65m2-m-6m-lo-goc-7-tang-thang-may-dang-cho-thue-60tr-thang-pr43891309  
30            https://batdongsan.com.vn/ban-nha-rieng-duong-khuong-trung-phuong-khuong-trung/sieu-re-53m2x4t-gan-pho-gan-nga-tu-so-gia-7-95-ty-cam-ket-that-gia-chuan-pr44301330  
34              https://batdongsan.com.vn/ban-nha-rieng-duong-xuan-la-phuong-xuan-la/12-ty-hon-ban-ngoai-giao-doan-dinh-lo-goc-ngo-nong-o-to-gan-55m2-gan-5m-mat-tien-pr44327370  
57                https://batdongsan.com.vn/ban-nha-rieng-duong-phan-ke-binh-phuong-cong-vi/mat-ngo-25m-o-to-tranh-lo-o-ban-co-ngo-thong-kinh-doanh-so-cc-o-ngay-38m2-pr44315310  
72                                           https://batdongsan.com.vn/ban-nha-rieng-duong-tu-hiep-xa-tu-hiep/-dep-2-mat-thoang-trung-tam-35m-x-4-tang-chi-nhinh-7-ty-pr44305757  
97            https://batdongsan.com.vn/ban-nha-rieng-duong-nguyen-chi-thanh-phuong-lang-thuong/co-102-xay-moi-lo-goc-5-tang-co-thang-may-ngo-thong-20m-ra-o-to-tranh-pr44184736  
118                                               https://batdongsan.com.vn/ban-nha-rieng-pho-bach-mai-phuong-bach-mai/6-35-ty-25-28m2-5-tang-ngo-nong-chua-lien-phai-pr44113135  
148                                https://batdongsan.com.vn/ban-nha-rieng-duong-nguyen-thi-dinh-phuong-trung-hoa-4/-5-tang-43-8m2-2-thoang-ngo-thong-kinh-doanh-dinh-pr44336852  
155                           https://batdongsan.com.vn/ban-nha-rieng-duong-an-duong-vuong-phuong-13-3/quan-6-hon-2-ty-nho-kho-tiem-ngang-5m-so-hong-ko-qh-ko-lo-gioi-pr44210729  
168                                  https://batdongsan.com.vn/ban-nha-rieng-duong-lang-phuong-lang-ha/ban-62m-5-tang-lo-goc-2-mat-thoang-15m-ra-o-to-tranh-22-599-ty-pr44321036  
183                                     https://batdongsan.com.vn/ban-nha-rieng-duong-tran-thi-trong-phuong-15-8/-dep-moi-o-ngay-2-lau-btct-46m2-ngang-4-nhinh-4-dong-pr44315734  
194                             https://batdongsan.com.vn/ban-nha-rieng-pho-thai-thinh-phuong-thinh-quang/ban-42m-7-tang-thang-may-full-noi-that-gan-o-to-gia-15-2-ty-pr44291365  
198                      https://batdongsan.com.vn/ban-nha-rieng-duong-tran-quang-dieu-phuong-o-cho-dua/ban-nga-tu-dang-tien-dng-65-7m-x-5-tang-t-d-cng-gia-13-868-ty-pr44290184  
236                           https://batdongsan.com.vn/ban-nha-rieng-duong-phan-xich-long-phuong-7-11/chi-can-5-55-ty-co-ngay-40m2-can-goc-2mt-3pn-moi-full-noi-that-pr44302765  
237                             